In [1]:
import pandas as pd
import mysql.connector
from sqlalchemy import create_engine

# Replace with your own database credentials
db_config = {
    "host": "db00",
    "user": "root",
    "password": "Local1234567",
    "database": "osticket_1-10-1_live"
}
# Create a SQLAlchemy engine using the MySQL connector connection
engine = create_engine(f"mysql+mysqlconnector://{db_config['user']}:{db_config['password']}@{db_config['host']}/{db_config['database']}")

# Define your SQL query
query = """
    SELECT 
        CONCAT(st.firstname, ' ', st.lastname) AS 'AssignedTo',
        te.name AS AssignedToTeam,
        t.created AS created,
        t.updated AS updated,
        Title.value AS Title,
        Classification.value AS Classification,
        Topic.value AS Topic,
        tre.body AS Text
    FROM 
        ost_ticket t
        JOIN ost_ticket_status ts ON (t.status_id = ts.id)
        JOIN ost_department d ON (t.dept_id = d.id)
        JOIN ost_thread tr ON (t.ticket_id = tr.object_id)
        JOIN ost_thread_entry tre ON (tr.id = tre.thread_id AND tre.type = 'M' AND tre.pid = 0)
        JOIN ost_form_entry f1 ON (t.ticket_id = f1.object_id AND f1.form_id = 2)
        LEFT JOIN ost_staff st ON (t.staff_id = st.staff_id)
        LEFT JOIN ost_team te ON (t.team_id = te.team_id)
        LEFT JOIN ost_form_entry_values Title ON (f1.id = Title.entry_id AND Title.field_id = 5 AND f1.form_id = 2)
        LEFT JOIN ost_form_entry_values Priority ON (f1.id = Priority.entry_id AND Priority.field_id = 7 AND f1.form_id = 2)
        LEFT JOIN ost_form_entry_values Classification ON (f1.id = Classification.entry_id AND Classification.field_id = 29 AND f1.form_id = 2)
        LEFT JOIN ost_form_entry_values Topic ON (f1.id = Topic.entry_id AND Topic.field_id = 31 AND f1.form_id = 2)
    WHERE 
        d.name = 'TABZ FLS'
    ORDER BY 
        created DESC
    LIMIT 5000
"""

# Use SQLAlchemy engine to execute the query and load data into a DataFrame
df = pd.read_sql(query, engine)


In [2]:
print(df)

              AssignedTo            AssignedToTeam             created  \
0                   None                       CRM 2023-10-19 14:40:17   
1     Patrik Platzgummer                       NAV 2023-10-19 14:07:03   
2        Arashdeep Singh  User Identity Management 2023-10-19 13:44:05   
3           Daniele Neri               H/S Support 2023-10-19 13:38:41   
4           Daniele Neri                       NAV 2023-10-19 13:21:20   
...                  ...                       ...                 ...   
4995     Arashdeep Singh               H/S Support 2023-04-14 14:45:15   
4996     Arashdeep Singh               H/S Support 2023-04-14 14:45:15   
4997        Daniele Neri                       NAV 2023-04-14 14:34:14   
4998        Daniele Neri                       NAV 2023-04-14 14:34:14   
4999        Daniele Neri  User Identity Management 2023-04-14 14:32:21   

                 updated                                          Title  \
0    2023-10-19 14:47:04            

In [3]:
# List of columns to keep (exclude the ones you want to remove)
columns_to_keep = ['Title', 'Topic', 'Text']

# Create a new DataFrame with only the selected columns
df = df[columns_to_keep]

# df now contains only columns A and B
print(df)

                                              Title  \
0                                   display problem   
1                   WG: SKU - Change Purchaser CODE   
2                                             Handy   
3                  Non escono le Mail nell' Outlook   
4        Modifica combinazione IVA su VCEE-23.05167   
...                                             ...   
4995  PC che fa rumore. Microfono o audio difettoso   
4996  PC che fa rumore. Microfono o audio difettoso   
4997                                  TRPT-23.01119   
4998                                  TRPT-23.01119   
4999                           Programminstallation   

                                                  Topic  \
0                                 {"15":"Dynamics CRM"}   
1                                 {"22":"Dynamics NAV"}   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...   
4                                 {"22":"Dyn

In [4]:
import re

values_to_keep = [
    '{"16":"User identity management, Permissions, Badge, Mail"}',
    '{"12":"Standard Software: Operating systems, Microsoft Office, Citrix clients, CRM Plugin, Acrobat Reader etc."}',
    '{"11":"Hardware, Telephony, Smartphones, Monitor, Printer,  etc"}'
]

# Use str.contains to create a boolean mask, replace NaN with False, and then filter
mask = df['Topic'].str.contains('|'.join(map(re.escape, values_to_keep))).fillna(False)
filtered_df = df[mask]

# Print the filtered DataFrame
print(filtered_df)

                                                  Title  \
2                                                 Handy   
3                      Non escono le Mail nell' Outlook   
7                               problemi uscita e-mails   
11                  digitale Prüfprotokoll non funziona   
15                                Access L folder TA US   
...                                                 ...   
4985                      Abwesenheitsassistent OUTLOOK   
4990  Remote controll LAPTOP - Brandt Veronika per 1...   
4995      PC che fa rumore. Microfono o audio difettoso   
4996      PC che fa rumore. Microfono o audio difettoso   
4999                               Programminstallation   

                                                  Topic  \
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...   
7     {"16":"User identity management, Permissions, ...   
11    {"12":"Standard Software: Operating systems, M...

In [5]:
# Reset the index to start from 0
filtered_df = filtered_df.reset_index(drop=True)

# Print the filtered DataFrame
print(filtered_df)

                                                  Title  \
0                                                 Handy   
1                      Non escono le Mail nell' Outlook   
2                               problemi uscita e-mails   
3                   digitale Prüfprotokoll non funziona   
4                                 Access L folder TA US   
...                                                 ...   
2785                      Abwesenheitsassistent OUTLOOK   
2786  Remote controll LAPTOP - Brandt Veronika per 1...   
2787      PC che fa rumore. Microfono o audio difettoso   
2788      PC che fa rumore. Microfono o audio difettoso   
2789                               Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
1     {"12":"Standard Software: Operating systems, M...   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...

In [6]:
from IPython.display import display, HTML

display(HTML('<style>.output { overflow-x: scroll; white-space: nowrap; }</style>'))
filtered_df

Title  \
0                                                 Handy   
1                      Non escono le Mail nell' Outlook   
2                               problemi uscita e-mails   
3                   digitale Prüfprotokoll non funziona   
4                                 Access L folder TA US   
...                                                 ...   
2785                      Abwesenheitsassistent OUTLOOK   
2786  Remote controll LAPTOP - Brandt Veronika per 1...   
2787      PC che fa rumore. Microfono o audio difettoso   
2788      PC che fa rumore. Microfono o audio difettoso   
2789                               Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
1     {"12":"Standard Software: Operating systems, M...   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2785  {"16":"User identity management, Permissions, ...   
2786  {"11":"Hardware, Telephony, Smartphones, Monit...   
2787  {"11":"Hardware, Telephony, Smartphones, Monit...   
2788  {"11":"Hardware, Telephony, Smartphones, Monit...   
2789  {"16":"User identity management, Permissions, ...   

                                                   Text  
0     <p>Ciao,</p> <p>per Stefan Mayr avrei bisogno ...  
1     <p>Ciao, non escono piu' alcune Mail nel Outlo...  
2     <p>Ciao, </p> <p>è la seconda volta che mi cap...  
3                                         <p>Grazie</p>  
4     <p><br /></p>Hello,<br />Angelo Maestre from T...  
...                                                 ...  
2785  <p>Ciao Manuel,</p> <p>come da tel. di oggi vo...  
2786  <p>Mi dispiace tanto ma la gente non usa il ce...  
2787  <p><span dir="ltr">ciao Arash, </span></p> <p>...  
2788  <p>quanto tempo ti serve per fare la operazion...  
2789  <p>Brauche die Zugangserlaubnis vom admin um d...  

[2790 rows x 3 columns]

In [7]:
pip install beautifulsoup4

Note: you may need to restart the kernel to use updated packages.


In [8]:
#keep only the text

In [9]:
# Assuming you have a DataFrame named 'df' and you want to see all rows of the 'column_name' column
column_name = 'Text'
pd.set_option('display.max_rows', None)  # Set the option to display all rows
print(filtered_df[column_name])
pd.reset_option('display.max_rows')  # Reset the option to its default value

0       <p>Ciao,</p> <p>per Stefan Mayr avrei bisogno ...
1       <p>Ciao, non escono piu' alcune Mail nel Outlo...
2       <p>Ciao, </p> <p>è la seconda volta che mi cap...
3                                           <p>Grazie</p>
4       <p><br /></p>Hello,<br />Angelo Maestre from T...
5       <p>Hallo, mein Chrome speichert leider keine P...
6       <p>potete reinstallarmi anche la APP stessa</p...
7       <p>Ciao,<br />Sul nuovo portatile mi mancano l...
8       Module General Warning\n\n--ManageUPSnet Infor...
9       <p>Ciao,</p> <p>hanno problema di accesso nell...
10      <p>Hallo,</p> <p>ilTablet  TBLT009 a un proble...
11      <p>hallo,</p> <p>e la presa dove metto il cavo...
12      <p>Hallo,</p> <p>si appena fatto il problema e...
13      <p>ciao,</p> <p>Sul PC del nuovo collega Stefa...
14                                          <p>Grazie</p>
15      <p>Ciao Daniele</p> <p>bei dem Versand von Rec...
16      <p>Ciao Daniele</p> <p>foult again :-(</p><fig...
17      <p>Buo

In [10]:
import pandas as pd
from bs4 import BeautifulSoup
import re

In [11]:
def remove_html_tags(text):
    # Parse the HTML content using BeautifulSoup
    soup = BeautifulSoup(text, 'html.parser')
    
    # Remove HTML tags and extract only the text
    text = soup.get_text()
    
    # Remove any remaining special characters
    pattern = r'[^a-zA-Z0-9\s]'
    return re.sub(pattern, '', text)

# Apply the remove_html_tags function to the DataFrame columns containing HTML data
filtered_df['Text'] = filtered_df['Text'].apply(remove_html_tags)


C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\1070994409.py:3: MarkupResemblesLocatorWarning: The input looks more like a filename than markup. You may want to open this file and pass the filehandle into Beautiful Soup.
  soup = BeautifulSoup(text, 'html.parser')


In [12]:
column_name = 'Text'
pd.set_option('display.max_rows', None)  # Set the option to display all rows
print(filtered_df[column_name])
pd.reset_option('display.max_rows')  # Reset the option to its default value

0       Ciao per Stefan Mayr avrei bisogno di un cellu...
1       Ciao non escono piu alcune Mail nel Outlook Ho...
2       Ciao   la seconda volta che mi capita questo  ...
3                                                  Grazie
4       HelloAngelo Maestre from TA US needs access to...
5       Hallo mein Chrome speichert leider keine Passw...
6       potete reinstallarmi anche la APP stessa come ...
7       CiaoSul nuovo portatile mi mancano le applicaz...
8       Module General Warning\n\nManageUPSnet Informa...
9       Ciao hanno problema di accesso nella produzion...
10      Hallo ilTablet  TBLT009 a un problema con la p...
11      hallo e la presa dove metto il cavo che non va...
12          Hallo si appena fatto il problema e la spina 
13      ciao Sul PC del nuovo collega Stefano Salzburg...
14                                                 Grazie
15      Ciao Daniele bei dem Versand von Rechnungen VR...
16                              Ciao Daniele foult again 
17      Buon d

In [13]:
filtered_df.to_csv('cleaned_data.csv', index=False)

In [14]:
df = pd.read_csv('cleaned_data.csv')
df

Title  \
0                                                 Handy   
1                      Non escono le Mail nell' Outlook   
2                               problemi uscita e-mails   
3                   digitale Prüfprotokoll non funziona   
4                                 Access L folder TA US   
...                                                 ...   
2785                      Abwesenheitsassistent OUTLOOK   
2786  Remote controll LAPTOP - Brandt Veronika per 1...   
2787      PC che fa rumore. Microfono o audio difettoso   
2788      PC che fa rumore. Microfono o audio difettoso   
2789                               Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
1     {"12":"Standard Software: Operating systems, M...   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2785  {"16":"User identity management, Permissions, ...   
2786  {"11":"Hardware, Telephony, Smartphones, Monit...   
2787  {"11":"Hardware, Telephony, Smartphones, Monit...   
2788  {"11":"Hardware, Telephony, Smartphones, Monit...   
2789  {"16":"User identity management, Permissions, ...   

                                                   Text  
0     Ciao per Stefan Mayr avrei bisogno di un cellu...  
1     Ciao non escono piu alcune Mail nel Outlook Ho...  
2     Ciao   la seconda volta che mi capita questo  ...  
3                                                Grazie  
4     HelloAngelo Maestre from TA US needs access to...  
...                                                 ...  
2785  Ciao Manuel come da tel di oggi vorrei una fir...  
2786  Mi dispiace tanto ma la gente non usa il cerve...  
2787  ciao Arash  ho sempre quel problema del rumore...  
2788       quanto tempo ti serve per fare la operazione  
2789  Brauche die Zugangserlaubnis vom admin um die ...  

[2790 rows x 3 columns]

In [15]:
df = df.dropna()

# The df_cleaned DataFrame will contain only rows with no NaN values
df

Title  \
0                                                 Handy   
1                      Non escono le Mail nell' Outlook   
2                               problemi uscita e-mails   
3                   digitale Prüfprotokoll non funziona   
4                                 Access L folder TA US   
...                                                 ...   
2785                      Abwesenheitsassistent OUTLOOK   
2786  Remote controll LAPTOP - Brandt Veronika per 1...   
2787      PC che fa rumore. Microfono o audio difettoso   
2788      PC che fa rumore. Microfono o audio difettoso   
2789                               Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
1     {"12":"Standard Software: Operating systems, M...   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2785  {"16":"User identity management, Permissions, ...   
2786  {"11":"Hardware, Telephony, Smartphones, Monit...   
2787  {"11":"Hardware, Telephony, Smartphones, Monit...   
2788  {"11":"Hardware, Telephony, Smartphones, Monit...   
2789  {"16":"User identity management, Permissions, ...   

                                                   Text  
0     Ciao per Stefan Mayr avrei bisogno di un cellu...  
1     Ciao non escono piu alcune Mail nel Outlook Ho...  
2     Ciao   la seconda volta che mi capita questo  ...  
3                                                Grazie  
4     HelloAngelo Maestre from TA US needs access to...  
...                                                 ...  
2785  Ciao Manuel come da tel di oggi vorrei una fir...  
2786  Mi dispiace tanto ma la gente non usa il cerve...  
2787  ciao Arash  ho sempre quel problema del rumore...  
2788       quanto tempo ti serve per fare la operazione  
2789  Brauche die Zugangserlaubnis vom admin um die ...  

[2671 rows x 3 columns]

In [16]:
df.to_csv('final_data.csv', index=False)

In [17]:
df = pd.read_csv('final_data.csv')
df

Title  \
0                                                 Handy   
1                      Non escono le Mail nell' Outlook   
2                               problemi uscita e-mails   
3                   digitale Prüfprotokoll non funziona   
4                                 Access L folder TA US   
...                                                 ...   
2666                      Abwesenheitsassistent OUTLOOK   
2667  Remote controll LAPTOP - Brandt Veronika per 1...   
2668      PC che fa rumore. Microfono o audio difettoso   
2669      PC che fa rumore. Microfono o audio difettoso   
2670                               Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
1     {"12":"Standard Software: Operating systems, M...   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2666  {"16":"User identity management, Permissions, ...   
2667  {"11":"Hardware, Telephony, Smartphones, Monit...   
2668  {"11":"Hardware, Telephony, Smartphones, Monit...   
2669  {"11":"Hardware, Telephony, Smartphones, Monit...   
2670  {"16":"User identity management, Permissions, ...   

                                                   Text  
0     Ciao per Stefan Mayr avrei bisogno di un cellu...  
1     Ciao non escono piu alcune Mail nel Outlook Ho...  
2     Ciao   la seconda volta che mi capita questo  ...  
3                                                Grazie  
4     HelloAngelo Maestre from TA US needs access to...  
...                                                 ...  
2666  Ciao Manuel come da tel di oggi vorrei una fir...  
2667  Mi dispiace tanto ma la gente non usa il cerve...  
2668  ciao Arash  ho sempre quel problema del rumore...  
2669       quanto tempo ti serve per fare la operazione  
2670  Brauche die Zugangserlaubnis vom admin um die ...  

[2671 rows x 3 columns]

In [18]:
#DELETE CONFIDENTIAL MESSAGE

import pandas as pd
import re

# Create or load your DataFrame 'df' with columns 'Title', 'Topic', and 'Text'

# Define a regular expression pattern to match the confidential message
confidential_pattern = re.compile(r"(?i)THIS MESSAGE INCLUDING ANY ATTACHMENTS CONTAINS CONFIDENTIAL INFORMATION.*?PROHIBITED", re.DOTALL)

# Function to remove text containing the confidential message
def remove_confidential_text(text):
    return re.sub(confidential_pattern, '', text)

# Apply the function to the 'Text' column
df['Text'] = df['Text'].apply(remove_confidential_text)

# Display the modified DataFrame
print(df)


                                                  Title  \
0                                                 Handy   
1                      Non escono le Mail nell' Outlook   
2                               problemi uscita e-mails   
3                   digitale Prüfprotokoll non funziona   
4                                 Access L folder TA US   
...                                                 ...   
2666                      Abwesenheitsassistent OUTLOOK   
2667  Remote controll LAPTOP - Brandt Veronika per 1...   
2668      PC che fa rumore. Microfono o audio difettoso   
2669      PC che fa rumore. Microfono o audio difettoso   
2670                               Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
1     {"12":"Standard Software: Operating systems, M...   
2     {"16":"User identity management, Permissions, ...   
3     {"12":"Standard Software: Operating systems, M...

In [19]:
import pandas as pd

desired_value = r'{"16":"User identity management, Permissions, Badge, Mail"}'

df_1 = df[df['Topic'].str.contains(desired_value, regex=True)]
df_1

Title  \
0                                         Handy   
2                       problemi uscita e-mails   
5             Chrome speichert keine Passwörter   
9                                         Badge   
20    FW: I: Delayed Mail (still being retried)   
...                                         ...   
2661                                      Badge   
2663                    Approvatori Utenti SAP    
2664         Richiesta accesso wifi - guest lan   
2666              Abwesenheitsassistent OUTLOOK   
2670                       Programminstallation   

                                                  Topic  \
0     {"16":"User identity management, Permissions, ...   
2     {"16":"User identity management, Permissions, ...   
5     {"16":"User identity management, Permissions, ...   
9     {"16":"User identity management, Permissions, ...   
20    {"16":"User identity management, Permissions, ...   
...                                                 ...   
2661  {"16":"User identity management, Permissions, ...   
2663  {"16":"User identity management, Permissions, ...   
2664  {"16":"User identity management, Permissions, ...   
2666  {"16":"User identity management, Permissions, ...   
2670  {"16":"User identity management, Permissions, ...   

                                                   Text  
0     Ciao per Stefan Mayr avrei bisogno di un cellu...  
2     Ciao   la seconda volta che mi capita questo  ...  
5     Hallo mein Chrome speichert leider keine Passw...  
9     Ciao hanno problema di accesso nella produzion...  
20     Potete verificare come mai i miei clienti non...  
...                                                 ...  
2661  Si un Saldatore che e arrivato oggi il HR sa n...  
2663  Ciao Prego verificare ed aggironare dai vendit...  
2664  Ciao nostro agente Santiago Hardt chiede un ac...  
2666  Ciao Manuel come da tel di oggi vorrei una fir...  
2670  Brauche die Zugangserlaubnis vom admin um die ...  

[945 rows x 3 columns]

In [20]:
# Reset the index to start from 0
df_1 = df_1.reset_index(drop=True)
df_1

Title  \
0                                        Handy   
1                      problemi uscita e-mails   
2            Chrome speichert keine Passwörter   
3                                        Badge   
4    FW: I: Delayed Mail (still being retried)   
..                                         ...   
940                                      Badge   
941                    Approvatori Utenti SAP    
942         Richiesta accesso wifi - guest lan   
943              Abwesenheitsassistent OUTLOOK   
944                       Programminstallation   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
940  {"16":"User identity management, Permissions, ...   
941  {"16":"User identity management, Permissions, ...   
942  {"16":"User identity management, Permissions, ...   
943  {"16":"User identity management, Permissions, ...   
944  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    Ciao per Stefan Mayr avrei bisogno di un cellu...  
1    Ciao   la seconda volta che mi capita questo  ...  
2    Hallo mein Chrome speichert leider keine Passw...  
3    Ciao hanno problema di accesso nella produzion...  
4     Potete verificare come mai i miei clienti non...  
..                                                 ...  
940  Si un Saldatore che e arrivato oggi il HR sa n...  
941  Ciao Prego verificare ed aggironare dai vendit...  
942  Ciao nostro agente Santiago Hardt chiede un ac...  
943  Ciao Manuel come da tel di oggi vorrei una fir...  
944  Brauche die Zugangserlaubnis vom admin um die ...  

[945 rows x 3 columns]

In [21]:
import pandas as pd

# Convert the 'Text' column to uppercase
df_1['Text'] = df_1['Text'].str.upper()

df_1

Title  \
0                                        Handy   
1                      problemi uscita e-mails   
2            Chrome speichert keine Passwörter   
3                                        Badge   
4    FW: I: Delayed Mail (still being retried)   
..                                         ...   
940                                      Badge   
941                    Approvatori Utenti SAP    
942         Richiesta accesso wifi - guest lan   
943              Abwesenheitsassistent OUTLOOK   
944                       Programminstallation   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
940  {"16":"User identity management, Permissions, ...   
941  {"16":"User identity management, Permissions, ...   
942  {"16":"User identity management, Permissions, ...   
943  {"16":"User identity management, Permissions, ...   
944  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    CIAO PER STEFAN MAYR AVREI BISOGNO DI UN CELLU...  
1    CIAO   LA SECONDA VOLTA CHE MI CAPITA QUESTO  ...  
2    HALLO MEIN CHROME SPEICHERT LEIDER KEINE PASSW...  
3    CIAO HANNO PROBLEMA DI ACCESSO NELLA PRODUZION...  
4     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...  
..                                                 ...  
940  SI UN SALDATORE CHE E ARRIVATO OGGI IL HR SA N...  
941  CIAO PREGO VERIFICARE ED AGGIRONARE DAI VENDIT...  
942  CIAO NOSTRO AGENTE SANTIAGO HARDT CHIEDE UN AC...  
943  CIAO MANUEL COME DA TEL DI OGGI VORREI UNA FIR...  
944  BRAUCHE DIE ZUGANGSERLAUBNIS VOM ADMIN UM DIE ...  

[945 rows x 3 columns]

In [22]:
import pandas as pd

desired_value = r'{"12":"Standard Software: Operating systems, Microsoft Office, Citrix clients, CRM Plugin, Acrobat Reader etc."}'  # Note the 'r' before the string for a raw string

df_2 = df[df['Topic'].str.contains(desired_value, regex=True)]
df_2

Title  \
1        Non escono le Mail nell' Outlook   
3     digitale Prüfprotokoll non funziona   
4                   Access L folder TA US   
6                             viva engage   
7           Installazione NAV-DMS-ProFIle   
...                                   ...   
2653                       Citrix non va?   
2654                       Citrix non va?   
2655                       Citrix non va?   
2662                Update CVE-2023-28252   
2665                                teams   

                                                  Topic  \
1     {"12":"Standard Software: Operating systems, M...   
3     {"12":"Standard Software: Operating systems, M...   
4     {"12":"Standard Software: Operating systems, M...   
6     {"12":"Standard Software: Operating systems, M...   
7     {"12":"Standard Software: Operating systems, M...   
...                                                 ...   
2653  {"12":"Standard Software: Operating systems, M...   
2654  {"12":"Standard Software: Operating systems, M...   
2655  {"12":"Standard Software: Operating systems, M...   
2662  {"12":"Standard Software: Operating systems, M...   
2665  {"12":"Standard Software: Operating systems, M...   

                                                   Text  
1     Ciao non escono piu alcune Mail nel Outlook Ho...  
3                                                Grazie  
4     HelloAngelo Maestre from TA US needs access to...  
6     potete reinstallarmi anche la APP stessa come ...  
7     CiaoSul nuovo portatile mi mancano le applicaz...  
...                                                 ...  
2653  Tutti i documenti che ho salvato in locale sul...  
2654  Tutti i documenti che ho salvato in locale sul...  
2655                             1 579 581 334 qa4p69z3  
2662  Ciao  su windows update mi dice che  tutto agg...  
2665  Ciao con laggiornamento il teams  scappato dal...  

[858 rows x 3 columns]

In [23]:
# Reset the index to start from 0
df_2 = df_2.reset_index(drop=True)
df_2

Title  \
0       Non escono le Mail nell' Outlook   
1    digitale Prüfprotokoll non funziona   
2                  Access L folder TA US   
3                            viva engage   
4          Installazione NAV-DMS-ProFIle   
..                                   ...   
853                       Citrix non va?   
854                       Citrix non va?   
855                       Citrix non va?   
856                Update CVE-2023-28252   
857                                teams   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
853  {"12":"Standard Software: Operating systems, M...   
854  {"12":"Standard Software: Operating systems, M...   
855  {"12":"Standard Software: Operating systems, M...   
856  {"12":"Standard Software: Operating systems, M...   
857  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    Ciao non escono piu alcune Mail nel Outlook Ho...  
1                                               Grazie  
2    HelloAngelo Maestre from TA US needs access to...  
3    potete reinstallarmi anche la APP stessa come ...  
4    CiaoSul nuovo portatile mi mancano le applicaz...  
..                                                 ...  
853  Tutti i documenti che ho salvato in locale sul...  
854  Tutti i documenti che ho salvato in locale sul...  
855                             1 579 581 334 qa4p69z3  
856  Ciao  su windows update mi dice che  tutto agg...  
857  Ciao con laggiornamento il teams  scappato dal...  

[858 rows x 3 columns]

In [24]:
df_2['Text'] = df_2['Text'].str.upper()

df_2

Title  \
0       Non escono le Mail nell' Outlook   
1    digitale Prüfprotokoll non funziona   
2                  Access L folder TA US   
3                            viva engage   
4          Installazione NAV-DMS-ProFIle   
..                                   ...   
853                       Citrix non va?   
854                       Citrix non va?   
855                       Citrix non va?   
856                Update CVE-2023-28252   
857                                teams   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
853  {"12":"Standard Software: Operating systems, M...   
854  {"12":"Standard Software: Operating systems, M...   
855  {"12":"Standard Software: Operating systems, M...   
856  {"12":"Standard Software: Operating systems, M...   
857  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    CIAO NON ESCONO PIU ALCUNE MAIL NEL OUTLOOK HO...  
1                                               GRAZIE  
2    HELLOANGELO MAESTRE FROM TA US NEEDS ACCESS TO...  
3    POTETE REINSTALLARMI ANCHE LA APP STESSA COME ...  
4    CIAOSUL NUOVO PORTATILE MI MANCANO LE APPLICAZ...  
..                                                 ...  
853  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  
854  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  
855                             1 579 581 334 QA4P69Z3  
856  CIAO  SU WINDOWS UPDATE MI DICE CHE  TUTTO AGG...  
857  CIAO CON LAGGIORNAMENTO IL TEAMS  SCAPPATO DAL...  

[858 rows x 3 columns]

In [25]:
import pandas as pd

desired_value = r'{"11":"Hardware, Telephony, Smartphones, Monitor, Printer,  etc"}'

df_3 = df[df['Topic'].str.contains(desired_value, regex=True)]
df_3

Title  \
8                                Module General Warning   
10                              Tablet problema con USB   
11                              Tablet problema con USB   
12                              Tablet problema con USB   
17                            Deviazione delle chiamate   
...                                                 ...   
2658                                    Laptop USB door   
2659                          Suono - Pro Call - cuffie   
2667  Remote controll LAPTOP - Brandt Veronika per 1...   
2668      PC che fa rumore. Microfono o audio difettoso   
2669      PC che fa rumore. Microfono o audio difettoso   

                                                  Topic  \
8     {"11":"Hardware, Telephony, Smartphones, Monit...   
10    {"11":"Hardware, Telephony, Smartphones, Monit...   
11    {"11":"Hardware, Telephony, Smartphones, Monit...   
12    {"11":"Hardware, Telephony, Smartphones, Monit...   
17    {"11":"Hardware, Telephony, Smartphones, Monit...   
...                                                 ...   
2658  {"11":"Hardware, Telephony, Smartphones, Monit...   
2659  {"11":"Hardware, Telephony, Smartphones, Monit...   
2667  {"11":"Hardware, Telephony, Smartphones, Monit...   
2668  {"11":"Hardware, Telephony, Smartphones, Monit...   
2669  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                   Text  
8     Module General Warning\n\nManageUPSnet Informa...  
10    Hallo ilTablet  TBLT009 a un problema con la p...  
11    hallo e la presa dove metto il cavo che non va...  
12        Hallo si appena fatto il problema e la spina   
17    Buon d da qualche tempo ormai che ho notato un...  
...                                                 ...  
2658                                       out of order  
2659  Ciao Arashdeep purtroppo con il nr 832 la chia...  
2667  Mi dispiace tanto ma la gente non usa il cerve...  
2668  ciao Arash  ho sempre quel problema del rumore...  
2669       quanto tempo ti serve per fare la operazione  

[868 rows x 3 columns]

In [26]:
# Reset the index to start from 0
df_3 = df_3.reset_index(drop=True)
df_3

Title  \
0                               Module General Warning   
1                              Tablet problema con USB   
2                              Tablet problema con USB   
3                              Tablet problema con USB   
4                            Deviazione delle chiamate   
..                                                 ...   
863                                    Laptop USB door   
864                          Suono - Pro Call - cuffie   
865  Remote controll LAPTOP - Brandt Veronika per 1...   
866      PC che fa rumore. Microfono o audio difettoso   
867      PC che fa rumore. Microfono o audio difettoso   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
863  {"11":"Hardware, Telephony, Smartphones, Monit...   
864  {"11":"Hardware, Telephony, Smartphones, Monit...   
865  {"11":"Hardware, Telephony, Smartphones, Monit...   
866  {"11":"Hardware, Telephony, Smartphones, Monit...   
867  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    Module General Warning\n\nManageUPSnet Informa...  
1    Hallo ilTablet  TBLT009 a un problema con la p...  
2    hallo e la presa dove metto il cavo che non va...  
3        Hallo si appena fatto il problema e la spina   
4    Buon d da qualche tempo ormai che ho notato un...  
..                                                 ...  
863                                       out of order  
864  Ciao Arashdeep purtroppo con il nr 832 la chia...  
865  Mi dispiace tanto ma la gente non usa il cerve...  
866  ciao Arash  ho sempre quel problema del rumore...  
867       quanto tempo ti serve per fare la operazione  

[868 rows x 3 columns]

In [27]:
df_3['Text'] = df_3['Text'].str.upper()

df_3

Title  \
0                               Module General Warning   
1                              Tablet problema con USB   
2                              Tablet problema con USB   
3                              Tablet problema con USB   
4                            Deviazione delle chiamate   
..                                                 ...   
863                                    Laptop USB door   
864                          Suono - Pro Call - cuffie   
865  Remote controll LAPTOP - Brandt Veronika per 1...   
866      PC che fa rumore. Microfono o audio difettoso   
867      PC che fa rumore. Microfono o audio difettoso   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
863  {"11":"Hardware, Telephony, Smartphones, Monit...   
864  {"11":"Hardware, Telephony, Smartphones, Monit...   
865  {"11":"Hardware, Telephony, Smartphones, Monit...   
866  {"11":"Hardware, Telephony, Smartphones, Monit...   
867  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    MODULE GENERAL WARNING\n\nMANAGEUPSNET INFORMA...  
1    HALLO ILTABLET  TBLT009 A UN PROBLEMA CON LA P...  
2    HALLO E LA PRESA DOVE METTO IL CAVO CHE NON VA...  
3        HALLO SI APPENA FATTO IL PROBLEMA E LA SPINA   
4    BUON D DA QUALCHE TEMPO ORMAI CHE HO NOTATO UN...  
..                                                 ...  
863                                       OUT OF ORDER  
864  CIAO ARASHDEEP PURTROPPO CON IL NR 832 LA CHIA...  
865  MI DISPIACE TANTO MA LA GENTE NON USA IL CERVE...  
866  CIAO ARASH  HO SEMPRE QUEL PROBLEMA DEL RUMORE...  
867       QUANTO TEMPO TI SERVE PER FARE LA OPERAZIONE  

[868 rows x 3 columns]

# MOST USED WORDS

# df_1
{"16":"User identity management, Permissions, Badge, Mail"}

In [28]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

In [29]:
import nltk
nltk.download('stopwords')

# Tokenize and remove stopwords
stop_words = set(stopwords.words('english'))
df_1['tokens'] = df_1['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in stop_words])


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!


In [30]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('stopwords')
nltk.download('punkt')

# Tokenize and remove stopwords for the 'Text' column
stop_words = set(stopwords.words('english'))
df_1['tokens'] = df_1['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in stop_words])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_1['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(100)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package stopwords to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package stopwords is already up-to-date!
[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('di', 365), ('per', 354), ('il', 282), ('grazie', 280), ('e', 270), ('ciao', 254), ('non', 232), ('che', 211), ('la', 205), ('badge', 148), ('da', 145), ('mi', 135), ('mail', 128), ('un', 122), ('come', 120), ('bitte', 115), ('saluti', 113), ('technoalpin', 112), ('prego', 110), ('le', 102), ('die', 101), ('al', 101), ('hallo', 100), ('email', 97), ('please', 95), ('39', 93), ('con', 88), ('una', 84), ('anche', 82), ('favore', 78), ('0471', 76), ('von', 76), ('fr', 76), ('und', 75), ('danke', 75), ('ha', 75), ('via', 73), ('potete', 68), ('ho', 66), ('2', 65), ('se', 65), ('der', 63), ('outlook', 62), ('ich', 61), ('si', 59), ('sono', 59), ('mille', 58), ('nicht', 57), ('del', 57), ('hello', 57), ('nuovo', 57), ('password', 55), ('accesso', 53), ('vi', 52), ('1', 52), ('solo', 50), ('den', 50), ('ad', 49), ('manuel', 48), ('f', 46), ('nel', 46), ('alla', 45), ('licenza', 44), ('agostini', 44), ('hi', 44), ('ta', 44), ('account', 43), ('alle', 43), ('das', 42), ('bolzano', 41), ('id',

In [31]:
#It includes a custom list of words to remove

import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('punkt')

# custom list of words to remove (greetings and articles)
custom_stopwords = ['hello', 'hi', 'a', 'an', 'the', 'is', 'di','per','grazie', 'e', 'il', 'ciao','non', 'che','la','da', 'bitte', 'mi', 'hallo', 
                    'die','come','le', 'un', 'saluti','al','technoalpin','prego', 'von', 'danke', 'please','con', 'favore', '39', 'und',
                    'fr', 'una', 'ha', 'via', 'intended', 'ich','potete','mille', 'anche', 'der', '2', 'nicht','ho', '1', 'se', '0471', 
                    'sono', 'use', 'den', 'manuel', 'del','si', 'vi','hi','id', 'ta','das', 'nuovo',
                    'ad', 'agostini','im','information','pi','0', 'buongiorno','mit','f', 'horst',
                    'action','bei','ihr', 'including', 'contains','confidential', 'individual','purpose', 
                    'protected', 'law', 'notify','taking', 'based', 'strictly','prohibited',  
                    'martin', 'thanks', 'solo','in', 'i', 'and', 'you', 'this', 'to', 'it',
                    'for', 'any', 'of', 'not','on', 'my', 'can', 'me','or', 'if', 'by','are', 'ma', 'at', 't', 
                    'have', 'should','might','am', 'delete', 'm','mio', 'alle', 'ancora', 'alla','daniele', 
                    'wwwtechnoalpincom','bolzano','from','fare','tutti','new','mir', 'hanno', 'kann','thank',
                    'matthias', '2023','zu', 'nel', 'auf', 'nella', '39100', 'bozen', 'with','hat','gi',
                    'questo', 'gli', 'sul','o', 'p', 'sie', 'teamviewer','knnt', 'lo','aggiungere', 
                    'dei', 'spa', 'help','specific', 'assegnare', 'team', 'ticket','laccesso', 
                    'serve','gre','della', 'stefan', 'service','betreff', 'n','perch', 
                    'but','suo','habe','firma','ok','no','could','oggi','su', 'ore', 'siemens',
                    'dare','pagostinistrae','200','43','posso' ,'ts','bisogno','delle', 'need', 
                    'produzione','dal','funziona','chiedo','riesco', '441', 'ist', 'neuen', 
                    'questa', 'ti','gruppo', 'that', 'regards', 'when', 'ci', 'so', 'essere', 'aprire',
                    'um','due','mai', 'usa', 'hier', 'we', 'dalle', 'de', 'en', 'zugang', 'noi', 
                    'quando', 'be','auch', 'wir', 'li' ,'cambiare', 'possibile', 'togliere',
                    'mitarbeiter','thomas', 'egregi', 'signori', 'creare', 'patrick', 'adesso',
                    'sales', 'manager','dass','gentilmente', 'mehr','gmbh', 'ept','gesendet', 'entrare', 
                    'cartella']


# Tokenize and remove stopwords from the 'Text' column
df_1['tokens'] = df_1['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in custom_stopwords])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_1['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(30)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('badge', 148), ('mail', 128), ('email', 97), ('outlook', 62), ('password', 55), ('accesso', 53), ('licenza', 44), ('account', 43), ('diritti', 32), ('accedere', 31), ('server', 28), ('phone', 28), ('nav', 28), ('pc', 27), ('access', 27), ('your', 25), ('do', 25), ('porte', 25), ('will', 24), ('entrata', 24), ('here', 23), ('microsoft', 23), ('mensa', 23), ('nostro', 23), ('crm', 23), ('message', 22), ('vpn', 22), ('computer', 22), ('ufficio', 21), ('abbiamo', 21)]


In [32]:
import pandas as pd

# Create keywords for each subset
keywords = {
    'df_1_email': ['message', 'mail', 'email', 'emails', 'account', 'sender', 'recipient',
                   'microsoft', 'outlook', 'password', 'attachments', 'send','licenza'],
    'df_2_rights': ['badge', 'accedere', 'diritti', 'access', 'porte', 'mensa', 'accesso'],
    'df_3_computer': ['pc', 'laptop', 'computer', 'phone', 'password'],
    'df_4_software': ['server', 'nav', 'vpn', 'crm', 'sap', 'concur']
}

# Initialize empty DataFrames for each subset
subset_dfs = {key: pd.DataFrame(columns=['Text']) for key in keywords.keys()}

# Iterate through each row in df_1 and assign it to the appropriate subset
for index, row in df_1.iterrows():
    text = row['Text']
    for subset_name, subset_keywords in keywords.items():
        if any(keyword in text.lower() for keyword in subset_keywords):
            subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)

# Now, you have four subsets in separate DataFrames
df_1_email = subset_dfs['df_1_email']
df_2_rights = subset_dfs['df_2_rights']
df_3_computer = subset_dfs['df_3_computer']
df_4_software = subset_dfs['df_4_software']

# You can access and work with each subset as needed
print("df_1_email:")
print(df_1_email)

print("\ndf_2_rights:")
print(df_2_rights)

print("\ndf_3_computer:")
print(df_3_computer)

print("\ndf_4_software:")
print(df_4_software)


C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method 

df_1_email:
                                                  Text
0    CIAO   LA SECONDA VOLTA CHE MI CAPITA QUESTO  ...
1     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...
2    CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...
3        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...
4    HELLO I RECENTLY CHANGE MY  MICROSOFT PASSWORD...
..                                                 ...
317   BUONGIORNO   HO VISTO CHE NON TUTTI I COLLEGH...
318  CIAO NELLOUTLOOK NON MI ATTACHA LA SIGNATURA N...
319     HALLO  IST OK SPAM     VON MEINEMMEINER GAL...
320  GUTEN MORGEN BEI MIR FEHLT DIE EMAIL VORLAGE W...
321  CIAO MANUEL COME DA TEL DI OGGI VORREI UNA FIR...

[322 rows x 1 columns]

df_2_rights:
                                                  Text
0    CIAO HANNO PROBLEMA DI ACCESSO NELLA PRODUZION...
1    PER DARE LA POSSIBILIT AD ALCUNI UTENTI CM SAL...
2    HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE...
3    CIAO LEON MAXIMILIAN PLANK NON RIESCE PI AD AC...
4    ESATTO LEO

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  subset_dfs[subset_name] = subset_dfs[subset_name].append({'Text': text}, ignore_index=True)
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\4151013874.py:20: FutureWarning: The frame.append method 

## df_1_email

In [33]:
import pandas as pd

words_to_check = ['message', 'mail', 'email', 'emails', 'account', 'sender', 'recipient',
                   'microsoft', 'outlook', 'password', 'attachments', 'send','licenza']
# Initialize an empty DataFrame to store the matching rows
df_1_email = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_email = df_1_email.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_email = df_1_email.reset_index(drop=True)

df_1_email

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3047725368.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_email = df_1_email.append(df_1[

Title  \
0            FW: I: Delayed Mail (still being retried)   
1    FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
2                      ENGO Mail esterne non arrivano    
3                   Receiving error message on Surface   
4                                              Outlook   
..                                                 ...   
556                                Disegnatore esterno   
557                                Disegnatore esterno   
558                                        Licenze CRM   
559                                        Licenze CRM   
560                                        Licenze CRM   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
556  {"16":"User identity management, Permissions, ...   
557  {"16":"User identity management, Permissions, ...   
558  {"16":"User identity management, Permissions, ...   
559  {"16":"User identity management, Permissions, ...   
560  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...   
1        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...   
2    THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPI...   
3    I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHE...   
4    HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15...   
..                                                 ...   
556  CIAO UN DISEGNATORE TECNICO ESTERNO CI DA UNAI...   
557  COME PU UNA PERSONA ESTERNA USARE LA NOSTRA LI...   
558  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...   
559  CIAOMI POTETE PER FAVORE MANDARE UNA LISTA ATT...   
560  CIAOPOTREMMO PER FAVORE ASSEGNARE A BLANDINE M...   

                                                tokens  
0    [verificare, miei, clienti, riescono, contarmi...  
1    [jiri, krticka, east, europe, sro, sk, 010, 01...  
2    [mail, system, host, mailtechnoalpincom, warni...  
3    [receiving, error, message, surface, opening, ...  
4    [karima, guerbaa, absent, until, september, 15...  
..                                                 ...  
556  [disegnatore, tecnico, esterno, unaiuto, reali...  
557  [pu, persona, esterna, usare, nostra, licenza,...  
558  [ciaopotremmo, licenza, fabien, garnier, jacob...  
559  [ciaomi, mandare, lista, attuale, persone, mom...  
560  [ciaopotremmo, blandine, markey, licenza, crm,...  

[561 rows x 4 columns]

In [34]:
df_1_email

Title  \
0            FW: I: Delayed Mail (still being retried)   
1    FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
2                      ENGO Mail esterne non arrivano    
3                   Receiving error message on Surface   
4                                              Outlook   
..                                                 ...   
556                                Disegnatore esterno   
557                                Disegnatore esterno   
558                                        Licenze CRM   
559                                        Licenze CRM   
560                                        Licenze CRM   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
556  {"16":"User identity management, Permissions, ...   
557  {"16":"User identity management, Permissions, ...   
558  {"16":"User identity management, Permissions, ...   
559  {"16":"User identity management, Permissions, ...   
560  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...   
1        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...   
2    THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPI...   
3    I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHE...   
4    HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15...   
..                                                 ...   
556  CIAO UN DISEGNATORE TECNICO ESTERNO CI DA UNAI...   
557  COME PU UNA PERSONA ESTERNA USARE LA NOSTRA LI...   
558  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...   
559  CIAOMI POTETE PER FAVORE MANDARE UNA LISTA ATT...   
560  CIAOPOTREMMO PER FAVORE ASSEGNARE A BLANDINE M...   

                                                tokens  
0    [verificare, miei, clienti, riescono, contarmi...  
1    [jiri, krticka, east, europe, sro, sk, 010, 01...  
2    [mail, system, host, mailtechnoalpincom, warni...  
3    [receiving, error, message, surface, opening, ...  
4    [karima, guerbaa, absent, until, september, 15...  
..                                                 ...  
556  [disegnatore, tecnico, esterno, unaiuto, reali...  
557  [pu, persona, esterna, usare, nostra, licenza,...  
558  [ciaopotremmo, licenza, fabien, garnier, jacob...  
559  [ciaomi, mandare, lista, attuale, persone, mom...  
560  [ciaopotremmo, blandine, markey, licenza, crm,...  

[561 rows x 4 columns]

In [35]:
df_1_email = df_1_email.drop(columns='tokens')
df_1_email

Title  \
0            FW: I: Delayed Mail (still being retried)   
1    FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
2                      ENGO Mail esterne non arrivano    
3                   Receiving error message on Surface   
4                                              Outlook   
..                                                 ...   
556                                Disegnatore esterno   
557                                Disegnatore esterno   
558                                        Licenze CRM   
559                                        Licenze CRM   
560                                        Licenze CRM   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
556  {"16":"User identity management, Permissions, ...   
557  {"16":"User identity management, Permissions, ...   
558  {"16":"User identity management, Permissions, ...   
559  {"16":"User identity management, Permissions, ...   
560  {"16":"User identity management, Permissions, ...   

                                                  Text  
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...  
1        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...  
2    THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPI...  
3    I AM RECEIVING AN ERROR MESSAGE ON SURFACE WHE...  
4    HI KARIMA GUERBAA IS ABSENT UNTIL SEPTEMBER 15...  
..                                                 ...  
556  CIAO UN DISEGNATORE TECNICO ESTERNO CI DA UNAI...  
557  COME PU UNA PERSONA ESTERNA USARE LA NOSTRA LI...  
558  CIAOPOTREMMO PER FAVORE ASSEGNARE LA LICENZA D...  
559  CIAOMI POTETE PER FAVORE MANDARE UNA LISTA ATT...  
560  CIAOPOTREMMO PER FAVORE ASSEGNARE A BLANDINE M...  

[561 rows x 3 columns]

# Further refinement

## look for df_1_email    'access'

In [36]:
import pandas as pd
import re


In [37]:
related_words = ['access', 'accessing', 'accessible', 'accessed', 'accesses', 'entry', 
                 'approach', 'admission', 'entrance', 'reach', 'open', 'connect', 
                 'visit', 'retrieve', 'use','Zugang', 'Zugriff', 'zugänglich',
                 'zugriffen', 'Zugänge', 'Eingang', 'Herangehensweise', 'Zulassung',
                 'Eingang', 'erreichen', 'öffnen', 'verbinden', 'besuchen', 'abrufen', 'benutzen',
                 'accesso', 'accesso', 'accessibile', 'accesso', 'accessi', 
                 'entrata', 'approccio', 'ammissione', 'ingresso', 'raggiungere', 
                 'aprire', 'collegare', 'visitare', 'recuperare', 'usare']

In [38]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_1_email = df_1_email[df_1_email['Text'].str.contains(pattern, case=False)]
filtered_df_1_email = filtered_df_1_email.reset_index(drop=True)

filtered_df_1_email

Title  \
0   FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
1                                        Mail history   
2   FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
3            Accesso email fatture.fornitori e VARHUB   
4                                Access spareparts US   
..                                                ...   
82                                        Licenze CRM   
83                    New Entry - Elias Malfertheiner   
84                                        Licenze CRM   
85                                Disegnatore esterno   
86                                        Licenze CRM   

                                                Topic  \
0   {"16":"User identity management, Permissions, ...   
1   {"16":"User identity management, Permissions, ...   
2   {"16":"User identity management, Permissions, ...   
3   {"16":"User identity management, Permissions, ...   
4   {"16":"User identity management, Permissions, ...   
..                                                ...   
82  {"16":"User identity management, Permissions, ...   
83  {"16":"User identity management, Permissions, ...   
84  {"16":"User identity management, Permissions, ...   
85  {"16":"User identity management, Permissions, ...   
86  {"16":"User identity management, Permissions, ...   

                                                 Text  
0       JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...  
1   HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022...  
2       JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...  
3   LA NUOVA COLLEGA GIULIA FARBENE DOVREBBE AVERE...  
4   CIAO POTETE PREGO DARE ACCESSO AL NOSTRO COORD...  
..                                                ...  
82  CIAOPOSSIAMO PER FAVORE ASSEGNARE A MATTIA RIC...  
83  CIAO LUNED PROSSIMA SETTIMANA INIZIA UN NUOVO ...  
84  CIAOPOSSIAMO PER FAVORE ASSEGNARE UNA LICENZA ...  
85  COME PU UNA PERSONA ESTERNA USARE LA NOSTRA LI...  
86  CIAOPOTREMMO PER FAVORE ASSEGNARE A BLANDINE M...  

[87 rows x 3 columns]

In [39]:
filtered_df_1_email

Title  \
0   FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
1                                        Mail history   
2   FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
3            Accesso email fatture.fornitori e VARHUB   
4                                Access spareparts US   
..                                                ...   
82                                        Licenze CRM   
83                    New Entry - Elias Malfertheiner   
84                                        Licenze CRM   
85                                Disegnatore esterno   
86                                        Licenze CRM   

                                                Topic  \
0   {"16":"User identity management, Permissions, ...   
1   {"16":"User identity management, Permissions, ...   
2   {"16":"User identity management, Permissions, ...   
3   {"16":"User identity management, Permissions, ...   
4   {"16":"User identity management, Permissions, ...   
..                                                ...   
82  {"16":"User identity management, Permissions, ...   
83  {"16":"User identity management, Permissions, ...   
84  {"16":"User identity management, Permissions, ...   
85  {"16":"User identity management, Permissions, ...   
86  {"16":"User identity management, Permissions, ...   

                                                 Text  
0       JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...  
1   HELLO I WOULD LIKE TO RETRIEVE MY OUTLOOK 2022...  
2       JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...  
3   LA NUOVA COLLEGA GIULIA FARBENE DOVREBBE AVERE...  
4   CIAO POTETE PREGO DARE ACCESSO AL NOSTRO COORD...  
..                                                ...  
82  CIAOPOSSIAMO PER FAVORE ASSEGNARE A MATTIA RIC...  
83  CIAO LUNED PROSSIMA SETTIMANA INIZIA UN NUOVO ...  
84  CIAOPOSSIAMO PER FAVORE ASSEGNARE UNA LICENZA ...  
85  COME PU UNA PERSONA ESTERNA USARE LA NOSTRA LI...  
86  CIAOPOTREMMO PER FAVORE ASSEGNARE A BLANDINE M...  

[87 rows x 3 columns]

In [40]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_1_email[i:i+n] for i in range(0,len(filtered_df_1_email),n)]
    #print(list_df)

In [41]:
len(list_df)


18

In [42]:
list_df[17]


Title                                              Topic  \
85  Disegnatore esterno  {"16":"User identity management, Permissions, ...   
86          Licenze CRM  {"16":"User identity management, Permissions, ...   

                                                 Text  
85  COME PU UNA PERSONA ESTERNA USARE LA NOSTRA LI...  
86  CIAOPOTREMMO PER FAVORE ASSEGNARE A BLANDINE M...

In [43]:
def put_together():
    list1=[]
    for index in range(0,17):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [44]:
summ_block = put_together()
summ_block

Result 0:
    JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE SRO  SK  010 01  ILINA  PRIEMYSELN 2  M 420 603 211 532  F 421 41 7002646  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM TECHNOALPIN ACCOUNTING USA  SENT TUESDAY OCTOBER 17 2023 321 PM TO RAGHURAMKARANEXPOCOM LTLRECEIVABLESXPOCOM JIRI KRTICKA  SUBJECT RE TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO     PLEASE FORWARD INVOICES BELOW 937462466 20231007  29272   937446344 20231007  31471    KIMBERLY COTTRELL HUMAN RESOURCES AND EXECUTIVE ASSISTANT TECHNOALPIN USA INC  US  80112  ENGLEWOOD CO  8536 CONCORD CENTER DR SUITE B T 17208952340  F 17208950100  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM XPO RAGHURAMKARANEXPOCOM  SENT MONDAY OCTOBER 16 2023 745 PM TO TECHNOALPIN ACCOUNTING USA USACCOUNTINGTECHNOALPINCOM JIRI KRTICKA JIRIKRTICKATECHNOALPINCOM CC LTLRECEIVABLESXPOCOM SUBJECT TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO     CAUTION THIS IS

['  \xa0 JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE SRO  SK  010 01  ILINA  PRIEMYSELN 2  M 420 603 211 532  F 421 41 7002646  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM TECHNOALPIN ACCOUNTING USA  SENT TUESDAY OCTOBER 17 2023 321 PM TO RAGHURAMKARANEXPOCOM LTLRECEIVABLESXPOCOM JIRI KRTICKA  SUBJECT RE TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO   \xa0 PLEASE FORWARD INVOICES BELOW 937462466 20231007 \xa029272 \xa0 937446344 20231007 \xa031471  \xa0 KIMBERLY COTTRELL HUMAN RESOURCES AND EXECUTIVE ASSISTANT TECHNOALPIN USA INC  US  80112  ENGLEWOOD CO  8536 CONCORD CENTER DR SUITE B T 17208952340  F 17208950100  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM XPO RAGHURAMKARANEXPOCOM  SENT MONDAY OCTOBER 16 2023 745 PM TO TECHNOALPIN ACCOUNTING USA USACCOUNTINGTECHNOALPINCOM JIRI KRTICKA JIRIKRTICKATECHNOALPINCOM CC LTLRECEIVABLESXPOCOM SUBJECT TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO   \xa0 CA

In [45]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 17):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [46]:
blocks_to_skip = [15]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)


Result 0:
    JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE SRO  SK  010 01  ILINA  PRIEMYSELN 2  M 420 603 211 532  F 421 41 7002646  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM TECHNOALPIN ACCOUNTING USA  SENT TUESDAY OCTOBER 17 2023 321 PM TO RAGHURAMKARANEXPOCOM LTLRECEIVABLESXPOCOM JIRI KRTICKA  SUBJECT RE TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO     PLEASE FORWARD INVOICES BELOW 937462466 20231007  29272   937446344 20231007  31471    KIMBERLY COTTRELL HUMAN RESOURCES AND EXECUTIVE ASSISTANT TECHNOALPIN USA INC  US  80112  ENGLEWOOD CO  8536 CONCORD CENTER DR SUITE B T 17208952340  F 17208950100  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM XPO RAGHURAMKARANEXPOCOM  SENT MONDAY OCTOBER 16 2023 745 PM TO TECHNOALPIN ACCOUNTING USA USACCOUNTINGTECHNOALPINCOM JIRI KRTICKA JIRIKRTICKATECHNOALPINCOM CC LTLRECEIVABLESXPOCOM SUBJECT TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO     CAUTION THIS IS

In [47]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
    JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE SRO  SK  010 01  ILINA  PRIEMYSELN 2  M 420 603 211 532  F 421 41 7002646  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM TECHNOALPIN ACCOUNTING USA  SENT TUESDAY OCTOBER 17 2023 321 PM TO RAGHURAMKARANEXPOCOM LTLRECEIVABLESXPOCOM JIRI KRTICKA  SUBJECT RE TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO     PLEASE FORWARD INVOICES BELOW 937462466 20231007  29272   937446344 20231007  31471    KIMBERLY COTTRELL HUMAN RESOURCES AND EXECUTIVE ASSISTANT TECHNOALPIN USA INC  US  80112  ENGLEWOOD CO  8536 CONCORD CENTER DR SUITE B T 17208952340  F 17208950100  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM XPO RAGHURAMKARANEXPOCOM  SENT MONDAY OCTOBER 16 2023 745 PM TO TECHNOALPIN ACCOUNTING USA USACCOUNTINGTECHNOALPINCOM JIRI KRTICKA JIRIKRTICKATECHNOALPINCOM CC LTLRECEIVABLESXPOCOM SUBJECT TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO     CAUTION THIS IS

['  \xa0 JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE SRO  SK  010 01  ILINA  PRIEMYSELN 2  M 420 603 211 532  F 421 41 7002646  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM TECHNOALPIN ACCOUNTING USA  SENT TUESDAY OCTOBER 17 2023 321 PM TO RAGHURAMKARANEXPOCOM LTLRECEIVABLESXPOCOM JIRI KRTICKA  SUBJECT RE TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO   \xa0 PLEASE FORWARD INVOICES BELOW 937462466 20231007 \xa029272 \xa0 937446344 20231007 \xa031471  \xa0 KIMBERLY COTTRELL HUMAN RESOURCES AND EXECUTIVE ASSISTANT TECHNOALPIN USA INC  US  80112  ENGLEWOOD CO  8536 CONCORD CENTER DR SUITE B T 17208952340  F 17208950100  WWWTECHNOALPINCOM         PLEASE FIND OUR PRIVACY POLICY HERE FROM XPO RAGHURAMKARANEXPOCOM  SENT MONDAY OCTOBER 16 2023 745 PM TO TECHNOALPIN ACCOUNTING USA USACCOUNTINGTECHNOALPINCOM JIRI KRTICKA JIRIKRTICKATECHNOALPINCOM CC LTLRECEIVABLESXPOCOM SUBJECT TECHNOALPIN USA INC TEDJUCTS900  UPCOMING PAYMENT REMINDER FROM XPO   \xa0 CA

In [48]:
pip install transformers

Note: you may need to restart the kernel to use updated packages.


# df_1_email_ signature

In [49]:
import pandas as pd
import re

In [50]:
related_words = [
    'Firma', 'Autografo', 'Sottoscrizione', 'Segno distintivo', 'Sigla', 'Marcatura',
    'Ratifica', 'Apposizione di firma', 'Sigillo', 'Atto autografo',
    'Signature', 'Autograph', 'Mark', 'Seal', 'Sign-off',
    'Inked mark', 'Signatory', 'Handwriting', 'Personal mark',
    'Unterschrift', 'Autogramm', 'Kennzeichen', 'Siegel', 'Namenszug', 'Paraphe',
    'Besiegelung', 'Unterzeichnung', 'Handschrift', 'Eigenhändige Unterschrift'
]


In [51]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_1_email_signature = df_1_email[df_1_email['Text'].str.contains(pattern, case=False)]
filtered_df_1_email_signature = filtered_df_1_email_signature.reset_index(drop=True)

filtered_df_1_email_signature

Title  \
0                            Email signature   
1                      Nuova firma per email   
2                 Email Signature - Immagine   
3                     Mail without signature   
4                             Mail signature   
5                              Mail Signatur   
6                          Richiesta accessi   
7              Problema arrivo ed invio mail   
8                                Firma Email   
9            New Entry - Elias Malfertheiner   
10                           Email Signature   
11                               firma email   
12                              firma e-mail   
13             Abwesenheitsassistent OUTLOOK   
14                           Email signature   
15                     Nuova firma per email   
16                Email Signature - Immagine   
17                            Mail signature   
18                             Mail Signatur   
19                               Firma Email   
20                           Email Signature   
21                              firma e-mail   
22                         Richiesta accessi   
23           New Entry - Elias Malfertheiner   
24                     Abwesenheitsassistent   
25        WG: telefono Dominik Schrott - SCM   
26             Nuovo collega Dominik Schrott   
27                  FIRMA OUTLOOK - D ROUZET   
28                   OUTLOOK - Antoine PAULY   
29                     Nuova firma per email   
30                            Mail signature   
31                               Firma Email   
32                     outlook web signature   
33                           Email Signature   
34                                   Outlook   
35                     Aggiornamento Outlook   
36        WG: telefono Dominik Schrott - SCM   
37    Peter Štaffen - phone number and photo   
38  Lenka Sevcikova - phone number and photo   
39           New Entry - Elias Malfertheiner   

                                                Topic  \
0   {"16":"User identity management, Permissions, ...   
1   {"16":"User identity management, Permissions, ...   
2   {"16":"User identity management, Permissions, ...   
3   {"16":"User identity management, Permissions, ...   
4   {"16":"User identity management, Permissions, ...   
5   {"16":"User identity management, Permissions, ...   
6   {"16":"User identity management, Permissions, ...   
7   {"16":"User identity management, Permissions, ...   
8   {"16":"User identity management, Permissions, ...   
9   {"16":"User identity management, Permissions, ...   
10  {"16":"User identity management, Permissions, ...   
11  {"16":"User identity management, Permissions, ...   
12  {"16":"User identity management, Permissions, ...   
13  {"16":"User identity management, Permissions, ...   
14  {"16":"User identity management, Permissions, ...   
15  {"16":"User identity management, Permissions, ...   
16  {"16":"User identity management, Permissions, ...   
17  {"16":"User identity management, Permissions, ...   
18  {"16":"User identity management, Permissions, ...   
19  {"16":"User identity management, Permissions, ...   
20  {"16":"User identity management, Permissions, ...   
21  {"16":"User identity management, Permissions, ...   
22  {"16":"User identity management, Permissions, ...   
23  {"16":"User identity management, Permissions, ...   
24  {"16":"User identity management, Permissions, ...   
25  {"16":"User identity management, Permissions, ...   
26  {"16":"User identity management, Permissions, ...   
27  {"16":"User identity management, Permissions, ...   
28  {"16":"User identity management, Permissions, ...   
29  {"16":"User identity management, Permissions, ...   
30  {"16":"User identity management, Permissions, ...   
31  {"16":"User identity management, Permissions, ...   
32  {"16":"User identity management, Permissions, ...   
33  {"16":"User identity management, Permissions, ...   
34  {"16":"User identity management, Permissions, ...   
35  {"16":"User id

In [52]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_1_email_signature[i:i+n] for i in range(0,len(filtered_df_1_email_signature),n)]
    #print(list_df)


In [53]:
len(list_df)

8

In [54]:
list_df[7]

Title  \
35                     Aggiornamento Outlook   
36        WG: telefono Dominik Schrott - SCM   
37    Peter Štaffen - phone number and photo   
38  Lenka Sevcikova - phone number and photo   
39           New Entry - Elias Malfertheiner   

                                                Topic  \
35  {"16":"User identity management, Permissions, ...   
36  {"16":"User identity management, Permissions, ...   
37  {"16":"User identity management, Permissions, ...   
38  {"16":"User identity management, Permissions, ...   
39  {"16":"User identity management, Permissions, ...   

                                                 Text  
35  BUONGIORNO  SI  AGGIORNATO OUTLOOK MA ADESSO S...  
36       MARIA OBERKALMSTEINER RECEPTION TECHNOALP...  
37  HELLO I AM SENDING YOU THE MOBILE NUMBER FOR N...  
38  HELLO I AM SENDING YOU THE MOBILE NUMBER FOR L...  
39  CIAO LUNED PROSSIMA SETTIMANA INIZIA UN NUOVO ...

In [55]:
def put_together():
    list1=[]
    for index in range(0,7):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


summ_block = put_together()
summ_block

Result 0:
HI  I TRIED TO UPDATE MY EMAIL SIGNATURE TO REMOVE MY MOBILE PHONE NUMBER AND ADD THE OFFICE NUMBER BUT I AM GETTING THIS ERROR CAN YOU FIX MY PHONE NUMBER TO OFFICE 7208952340 AND REMOVE MY MOBILETHAT IS MY PERSONAL CELL PHONE NUMBER IN PROPOSITO DEL NOSTRO NUOVO NOME AZIENDALE STIAMO PREPARANDO ANCHE UNA NUOVA FIRMA PER LE NOSTRE EMAIL COME VOGLIAMO FARE PPREPARIAMO UN HTML CHE VIENE IMPORTATO IN OUTLOOK OPPURE OGNI PERSONA SI SALVA LA NUOVA FIRMA DIRETTAMENTE IN OUTLOOK SALUTISALVE SAREBBE DA AGGIUNGERE SU TUTTI GLI UTENTI ENGO QUESTA IMMAGINE NELLA EMAIL SIGNATURE  GRAZIE E SALUTI TOBIAI CANT ADD MY SIGNATURE AUTOMATICALLY ON MY MAILHALLO   COULD YOU CREATE ME A OUTLOOK EMAIL SIGNATURE PLEASE THANK YOU TOMAS

Result 1:
PREGO AGGIUNGERE ALLA FIRMA EMAIL IN FONDO IL SEGUENTE TESTO INFO WARENEINGANG SIEMENSSTRAE 11082023  18082023 WEGEN FERIEN GESCHLOSSENENTRATA MERCI VIA SIEMENS 11082023  18082023 CHIUSO PER FERIEGOODS RECEIPT VIA SIEMENS 11082023  18082023 CLOSED FOR HOLID

['HI\xa0 I TRIED TO UPDATE MY EMAIL SIGNATURE TO REMOVE MY MOBILE PHONE NUMBER AND ADD THE OFFICE NUMBER BUT I AM GETTING THIS ERROR CAN YOU FIX MY PHONE NUMBER TO OFFICE 7208952340 AND REMOVE MY MOBILETHAT IS MY PERSONAL CELL PHONE NUMBER\xa0IN PROPOSITO DEL NOSTRO NUOVO NOME AZIENDALE STIAMO PREPARANDO ANCHE UNA NUOVA FIRMA PER LE NOSTRE EMAIL COME VOGLIAMO FARE PPREPARIAMO UN HTML CHE VIENE IMPORTATO IN OUTLOOK OPPURE OGNI PERSONA SI SALVA LA NUOVA FIRMA DIRETTAMENTE IN OUTLOOK SALUTISALVE SAREBBE DA AGGIUNGERE SU TUTTI GLI UTENTI ENGO QUESTA IMMAGINE NELLA EMAIL SIGNATURE  GRAZIE E SALUTI TOBIAI CANT ADD MY SIGNATURE AUTOMATICALLY ON MY MAILHALLO \xa0 COULD YOU CREATE ME A OUTLOOK EMAIL SIGNATURE PLEASE THANK YOU TOMAS',
 'PREGO AGGIUNGERE ALLA FIRMA EMAIL IN FONDO IL SEGUENTE TESTO INFO WARENEINGANG SIEMENSSTRAE 11082023  18082023 WEGEN FERIEN GESCHLOSSENENTRATA MERCI VIA SIEMENS 11082023  18082023 CHIUSO PER FERIEGOODS RECEIPT VIA SIEMENS 11082023  18082023 CLOSED FOR HOLIDAY  PE

In [56]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 7):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [57]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
HI  I TRIED TO UPDATE MY EMAIL SIGNATURE TO REMOVE MY MOBILE PHONE NUMBER AND ADD THE OFFICE NUMBER BUT I AM GETTING THIS ERROR CAN YOU FIX MY PHONE NUMBER TO OFFICE 7208952340 AND REMOVE MY MOBILETHAT IS MY PERSONAL CELL PHONE NUMBER IN PROPOSITO DEL NOSTRO NUOVO NOME AZIENDALE STIAMO PREPARANDO ANCHE UNA NUOVA FIRMA PER LE NOSTRE EMAIL COME VOGLIAMO FARE PPREPARIAMO UN HTML CHE VIENE IMPORTATO IN OUTLOOK OPPURE OGNI PERSONA SI SALVA LA NUOVA FIRMA DIRETTAMENTE IN OUTLOOK SALUTISALVE SAREBBE DA AGGIUNGERE SU TUTTI GLI UTENTI ENGO QUESTA IMMAGINE NELLA EMAIL SIGNATURE  GRAZIE E SALUTI TOBIAI CANT ADD MY SIGNATURE AUTOMATICALLY ON MY MAILHALLO   COULD YOU CREATE ME A OUTLOOK EMAIL SIGNATURE PLEASE THANK YOU TOMAS

Result 1:
PREGO AGGIUNGERE ALLA FIRMA EMAIL IN FONDO IL SEGUENTE TESTO INFO WARENEINGANG SIEMENSSTRAE 11082023  18082023 WEGEN FERIEN GESCHLOSSENENTRATA MERCI VIA SIEMENS 11082023  18082023 CHIUSO PER FERIEGOODS RECEIPT VIA SIEMENS 11082023  18082023 CLOSED FOR HOLID

In [58]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
HI  I TRIED TO UPDATE MY EMAIL SIGNATURE TO REMOVE MY MOBILE PHONE NUMBER AND ADD THE OFFICE NUMBER BUT I AM GETTING THIS ERROR CAN YOU FIX MY PHONE NUMBER TO OFFICE 7208952340 AND REMOVE MY MOBILETHAT IS MY PERSONAL CELL PHONE NUMBER IN PROPOSITO DEL NOSTRO NUOVO NOME AZIENDALE STIAMO PREPARANDO ANCHE UNA NUOVA FIRMA PER LE NOSTRE EMAIL COME VOGLIAMO FARE PPREPARIAMO UN HTML CHE VIENE IMPORTATO IN OUTLOOK OPPURE OGNI PERSONA SI SALVA LA NUOVA FIRMA DIRETTAMENTE IN OUTLOOK SALUTISALVE SAREBBE DA AGGIUNGERE SU TUTTI GLI UTENTI ENGO QUESTA IMMAGINE NELLA EMAIL SIGNATURE  GRAZIE E SALUTI TOBIAI CANT ADD MY SIGNATURE AUTOMATICALLY ON MY MAILHALLO   COULD YOU CREATE ME A OUTLOOK EMAIL SIGNATURE PLEASE THANK YOU TOMAS

Result 1:
PREGO AGGIUNGERE ALLA FIRMA EMAIL IN FONDO IL SEGUENTE TESTO INFO WARENEINGANG SIEMENSSTRAE 11082023  18082023 WEGEN FERIEN GESCHLOSSENENTRATA MERCI VIA SIEMENS 11082023  18082023 CHIUSO PER FERIEGOODS RECEIPT VIA SIEMENS 11082023  18082023 CLOSED FOR HOLID

['HI\xa0 I TRIED TO UPDATE MY EMAIL SIGNATURE TO REMOVE MY MOBILE PHONE NUMBER AND ADD THE OFFICE NUMBER BUT I AM GETTING THIS ERROR CAN YOU FIX MY PHONE NUMBER TO OFFICE 7208952340 AND REMOVE MY MOBILETHAT IS MY PERSONAL CELL PHONE NUMBER\xa0IN PROPOSITO DEL NOSTRO NUOVO NOME AZIENDALE STIAMO PREPARANDO ANCHE UNA NUOVA FIRMA PER LE NOSTRE EMAIL COME VOGLIAMO FARE PPREPARIAMO UN HTML CHE VIENE IMPORTATO IN OUTLOOK OPPURE OGNI PERSONA SI SALVA LA NUOVA FIRMA DIRETTAMENTE IN OUTLOOK SALUTISALVE SAREBBE DA AGGIUNGERE SU TUTTI GLI UTENTI ENGO QUESTA IMMAGINE NELLA EMAIL SIGNATURE  GRAZIE E SALUTI TOBIAI CANT ADD MY SIGNATURE AUTOMATICALLY ON MY MAILHALLO \xa0 COULD YOU CREATE ME A OUTLOOK EMAIL SIGNATURE PLEASE THANK YOU TOMAS',
 'PREGO AGGIUNGERE ALLA FIRMA EMAIL IN FONDO IL SEGUENTE TESTO INFO WARENEINGANG SIEMENSSTRAE 11082023  18082023 WEGEN FERIEN GESCHLOSSENENTRATA MERCI VIA SIEMENS 11082023  18082023 CHIUSO PER FERIEGOODS RECEIPT VIA SIEMENS 11082023  18082023 CLOSED FOR HOLIDAY  PE

In [59]:
pip install transformers

Note: you may need to restart the kernel to use updated packages.


# df_1_email_phishing

In [60]:
import pandas as pd
import re

In [61]:
related_words = ['Phishing', 'Pesca fraudolenta', 'Inganno online', 'Truffa informatica', 'Frode via email',
    'Phishing', 'Online scam', 'Email fraud', 'Deceptive online tactics', 'Cyber deception',
    'Phishing', 'Online-Betrug', 'Internet-Täuschung', 'E-Mail-Betrug', 'Cyber-Betrug',
    'Inganno informatico', 'Pesca di informazioni', 'Truffa digitale',
    'Digital deception', 'Information harvesting', 'Online fraud',
    'Digitale Täuschung', 'Informationsdiebstahl', 'Online-Betrug','Spam', 'Posta indesiderata', 
    'Messaggi non richiesti', 'Posta spazzatura', 'Invio massivo di email',
    'Spam', 'Unsolicited email', 'Junk mail', 'Email overload', 'Bulk messaging',
    'Spam', 'Unerwünschte E-Mails', 'Junk-Mail', 'E-Mail-Überflutung', 'Massenversand von Nachrichten',
    'Posta non desiderata', 'Messaggi di spam', 'Comunicazioni indesiderate',
    'Unwanted mail', 'Spam messages', 'Unsolicited communications',
    'Unerwünschte Post', 'Spam-Nachrichten', 'Ungebetene Kommunikation']

In [62]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_1_email_phishing = df_1_email[df_1_email['Text'].str.contains(pattern, case=False)]
filtered_df_1_email_phishing = filtered_df_1_email_phishing.reset_index(drop=True)

filtered_df_1_email_phishing

Title  \
0             Cartella Watersolution - Email   
1                         Possibile phishing   
2                                  Phishing    
3                                 SAP Concur   
4              Problema arrivo ed invio mail   
5                                  Mail Spam   
6                                       SPAM   
7                                 Spam Mail?   
8   FW: Rechnung B201303056 Service GmbH WKÖ   
9             Cartella Watersolution - Email   
10                                 Phishing    
11                                SAP Concur   
12  FW: Rechnung B201303056 Service GmbH WKÖ   
13                       E-mail non arrivano   
14                                SAP Concur   
15  FW: Rechnung B201303056 Service GmbH WKÖ   
16  FW: Rechnung B201303056 Service GmbH WKÖ   

                                                Topic  \
0   {"16":"User identity management, Permissions, ...   
1   {"16":"User identity management, Permissions, ...   
2   {"16":"User identity management, Permissions, ...   
3   {"16":"User identity management, Permissions, ...   
4   {"16":"User identity management, Permissions, ...   
5   {"16":"User identity management, Permissions, ...   
6   {"16":"User identity management, Permissions, ...   
7   {"16":"User identity management, Permissions, ...   
8   {"16":"User identity management, Permissions, ...   
9   {"16":"User identity management, Permissions, ...   
10  {"16":"User identity management, Permissions, ...   
11  {"16":"User identity management, Permissions, ...   
12  {"16":"User identity management, Permissions, ...   
13  {"16":"User identity management, Permissions, ...   
14  {"16":"User identity management, Permissions, ...   
15  {"16":"User identity management, Permissions, ...   
16  {"16":"User identity management, Permissions, ...   

                                                 Text  
0   CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI W...  
1   CIAO  DAL CENTRALINO CI HANNO GIRATO QUESTA MA...  
2   CIAO  NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PA...  
3   HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT...  
4   CIAO MICHEL BLANCHOT MI HA INFORMATO DI PROBLE...  
5   CIAO SULLA MAIL FATTURE FORNITORI  ARRIVATA QU...  
6   CIAO VI INFORMO CHE MI  ARRIVATA LA SEGUENTE M...  
7   CIAO VOLEVO SOLO CHIEDERVI  DIRVI CHE IO E ANC...  
8      HALLO  IST OK SPAM     VON MEINEMMEINER GAL...  
9   CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI W...  
10  CIAO  NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PA...  
11  HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT...  
12     HALLO  IST OK SPAM     VON MEINEMMEINER GAL...  
13  NON CI SONO NELLA CARTELLA SPAM IN OUTLOOK MI ...  
14  HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT...  
15     HALLO  IST OK SPAM     VON MEINEMMEINER GAL...  
16     HALLO  IST OK SPAM     VON MEINEMMEINER GAL...

In [63]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_1_email_phishing[i:i+n] for i in range(0,len(filtered_df_1_email_phishing),n)]
    #print(list_df)

In [64]:
len(list_df)

4

In [65]:
list_df[3]

Title  \
15  FW: Rechnung B201303056 Service GmbH WKÖ   
16  FW: Rechnung B201303056 Service GmbH WKÖ   

                                                Topic  \
15  {"16":"User identity management, Permissions, ...   
16  {"16":"User identity management, Permissions, ...   

                                                 Text  
15     HALLO  IST OK SPAM     VON MEINEMMEINER GAL...  
16     HALLO  IST OK SPAM     VON MEINEMMEINER GAL...

In [66]:
def put_together():
    list1=[]
    for index in range(0,3):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


summ_block = put_together()
summ_block

Result 0:
CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI WATERSOLUTION MI ARRIVANO SEMPRE MAIL SPAM E SICCOME NON FACCIO PIU QUEL MESTIERE SAREBBE TEMPO DI TOGLIERLO  GRAZIECIAO  DAL CENTRALINO CI HANNO GIRATO QUESTA MAIL SULLA MAIL FATTURE FORNITORI MA MI SEMBRA MOLTO UN TENTATIVO DI PHISHING VEDENDO LINDIRIZZO FIRMATO EMI CONTROL GRAZIECIAO  NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PARTNER CI HANNO CONTATTATO PERCHE HANNO RICEVUTO DELLE EMAIL PHISHING DALLINIDIRZZO PDANIELSSONEMICONTROLSCOM SE VOLETE POSSO GIRARVI LE EMAIL SALUTI PATRICK  HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO MICHEL BLANCHOT MI HA INFORMATO DI PROBLEMI RIGUARDO ALLINVIO E ALLARRIVO DEI MAIL SIA INTERNI CHE ESTERNI ECCO GLI ERRORIERRORE IN INTERNO CON MESSAGGIO DI VIOLAZIONE DI CONDIVISIONE DEI DATI SENZA DOCUMENTI ANNESSI ERRORE IN INTERNO ED ESTERNO DI VIOLAZIONE DI CONDIV

['CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI WATERSOLUTION MI ARRIVANO SEMPRE MAIL SPAM E SICCOME NON FACCIO PIU QUEL MESTIERE SAREBBE TEMPO DI TOGLIERLO  GRAZIECIAO\xa0 DAL CENTRALINO CI HANNO GIRATO QUESTA MAIL SULLA MAIL FATTURE FORNITORI MA MI SEMBRA MOLTO UN TENTATIVO DI PHISHING VEDENDO LINDIRIZZO FIRMATO EMI CONTROL GRAZIECIAO\xa0 NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PARTNER CI HANNO CONTATTATO PERCHE HANNO RICEVUTO DELLE EMAIL PHISHING DALLINIDIRZZO PDANIELSSONEMICONTROLSCOM SE VOLETE POSSO GIRARVI LE EMAIL SALUTI PATRICK \xa0HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO MICHEL BLANCHOT MI HA INFORMATO DI PROBLEMI RIGUARDO ALLINVIO E ALLARRIVO DEI MAIL SIA INTERNI CHE ESTERNI ECCO GLI ERRORIERRORE IN\xa0INTERNO CON MESSAGGIO DI VIOLAZIONE DI CONDIVISIONE DEI DATI SENZA DOCUMENTI ANNESSI ERRORE IN INTERNO ED ESTERNO\xa0DI VIOLAZIONE DI

In [67]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 3):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [68]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI WATERSOLUTION MI ARRIVANO SEMPRE MAIL SPAM E SICCOME NON FACCIO PIU QUEL MESTIERE SAREBBE TEMPO DI TOGLIERLO  GRAZIECIAO  DAL CENTRALINO CI HANNO GIRATO QUESTA MAIL SULLA MAIL FATTURE FORNITORI MA MI SEMBRA MOLTO UN TENTATIVO DI PHISHING VEDENDO LINDIRIZZO FIRMATO EMI CONTROL GRAZIECIAO  NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PARTNER CI HANNO CONTATTATO PERCHE HANNO RICEVUTO DELLE EMAIL PHISHING DALLINIDIRZZO PDANIELSSONEMICONTROLSCOM SE VOLETE POSSO GIRARVI LE EMAIL SALUTI PATRICK  HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO MICHEL BLANCHOT MI HA INFORMATO DI PROBLEMI RIGUARDO ALLINVIO E ALLARRIVO DEI MAIL SIA INTERNI CHE ESTERNI ECCO GLI ERRORIERRORE IN INTERNO CON MESSAGGIO DI VIOLAZIONE DI CONDIVISIONE DEI DATI SENZA DOCUMENTI ANNESSI ERRORE IN INTERNO ED ESTERNO DI VIOLAZIONE DI CONDIV

In [69]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI WATERSOLUTION MI ARRIVANO SEMPRE MAIL SPAM E SICCOME NON FACCIO PIU QUEL MESTIERE SAREBBE TEMPO DI TOGLIERLO  GRAZIECIAO  DAL CENTRALINO CI HANNO GIRATO QUESTA MAIL SULLA MAIL FATTURE FORNITORI MA MI SEMBRA MOLTO UN TENTATIVO DI PHISHING VEDENDO LINDIRIZZO FIRMATO EMI CONTROL GRAZIECIAO  NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PARTNER CI HANNO CONTATTATO PERCHE HANNO RICEVUTO DELLE EMAIL PHISHING DALLINIDIRZZO PDANIELSSONEMICONTROLSCOM SE VOLETE POSSO GIRARVI LE EMAIL SALUTI PATRICK  HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO MICHEL BLANCHOT MI HA INFORMATO DI PROBLEMI RIGUARDO ALLINVIO E ALLARRIVO DEI MAIL SIA INTERNI CHE ESTERNI ECCO GLI ERRORIERRORE IN INTERNO CON MESSAGGIO DI VIOLAZIONE DI CONDIVISIONE DEI DATI SENZA DOCUMENTI ANNESSI ERRORE IN INTERNO ED ESTERNO DI VIOLAZIONE DI CONDIV

['CIAO MI POTETE TOGLIERE LA CARTELLA EMAIL DI WATERSOLUTION MI ARRIVANO SEMPRE MAIL SPAM E SICCOME NON FACCIO PIU QUEL MESTIERE SAREBBE TEMPO DI TOGLIERLO  GRAZIECIAO\xa0 DAL CENTRALINO CI HANNO GIRATO QUESTA MAIL SULLA MAIL FATTURE FORNITORI MA MI SEMBRA MOLTO UN TENTATIVO DI PHISHING VEDENDO LINDIRIZZO FIRMATO EMI CONTROL GRAZIECIAO\xa0 NEGLI ULTIMI 2 GIORNI VARI DEI NOSTRI PARTNER CI HANNO CONTATTATO PERCHE HANNO RICEVUTO DELLE EMAIL PHISHING DALLINIDIRZZO PDANIELSSONEMICONTROLSCOM SE VOLETE POSSO GIRARVI LE EMAIL SALUTI PATRICK \xa0HELLO I NEED ACCESS TO MY SAPCONCUR BUT I CANT LOGIN BECAUSE I FORGOT MY PASSWORD WHEN I TRY TO RESET MY PASSWORD I GET NO EMAIL TO RESET IT ALSO THE SPAM ORDER IS EMPTY GREETINGS IVANCIAO MICHEL BLANCHOT MI HA INFORMATO DI PROBLEMI RIGUARDO ALLINVIO E ALLARRIVO DEI MAIL SIA INTERNI CHE ESTERNI ECCO GLI ERRORIERRORE IN\xa0INTERNO CON MESSAGGIO DI VIOLAZIONE DI CONDIVISIONE DEI DATI SENZA DOCUMENTI ANNESSI ERRORE IN INTERNO ED ESTERNO\xa0DI VIOLAZIONE DI

# df_1_rights

In [70]:
#df_2_rights
import pandas as pd

words_to_check = ['badge', 'accedere', 'diritti', 'access', 'porte', 'mensa', 'accesso']
# Initialize an empty DataFrame to store the matching rows
df_1_rights = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_rights = df_1_rights.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_rights = df_1_rights.reset_index(drop=True)

df_1_rights

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3570219059.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_rights = df_1_rights.appe

Title  \
0                    Zugänge Badge Patrick Zingerle   
1                                 Badge Adam Altman   
2                                Acesso Via Siemens   
3           Sbloccare il badge per la sede centrale   
4                                  Bage Adam Altman   
..                                              ...   
396  Accesso a cartella con forecast per produzione   
397                       Acesso server Controlling   
398                             Badge Basile HUARD    
399                                             VPN   
400              Richiesta accesso wifi - guest lan   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
396  {"16":"User identity management, Permissions, ...   
397  {"16":"User identity management, Permissions, ...   
398  {"16":"User identity management, Permissions, ...   
399  {"16":"User identity management, Permissions, ...   
400  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE...   
1    CIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENS...   
2    CIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN ...   
3    ATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PR...   
4    CIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE ...   
..                                                 ...   
396  CIAO  SAREBBE POSSIBILE DARMI LACCESSO ALLA CA...   
397  CIAO POTETE DARE PER PIACERE LACCESSO ALLA CAR...   
398  BASILE HUARD SAR A BOLZANO DAL 1 MAGGIO ARRIVA...   
399  SONO CON UN HOTSPOT E MI SERVONO LACCESSO ZU H...   
400  CIAO NOSTRO AGENTE SANTIAGO HARDT CHIEDE UN AC...   

                                                tokens  
0    [beim, badge, gleichen, rechte, wie, stephan, ...  
1          [badge, adam, mensa, pagare, riesce, porte]  
2    [ragazzi, domani, tutto, giornata, training, c...  
3    [attualmente, accesso, sede, badge, sbloccate,...  
4    [abilitare, badge, 1083, porte, altri, slovacc...  
..                                                 ...  
396  [sarebbe, darmi, fs01diskgproduktionproduktion...  
397  [piacere, controlling, server, giacomo, giubilei]  
398  [basile, huard, sar, maggio, arriva, italia, v...  
399  [hotspot, servono, h, conesso, vpn, conettano,...  
400  [nostro, agente, santiago, hardt, chiede, acce...  

[401 rows x 4 columns]

In [71]:
df_1_rights

Title  \
0                    Zugänge Badge Patrick Zingerle   
1                                 Badge Adam Altman   
2                                Acesso Via Siemens   
3           Sbloccare il badge per la sede centrale   
4                                  Bage Adam Altman   
..                                              ...   
396  Accesso a cartella con forecast per produzione   
397                       Acesso server Controlling   
398                             Badge Basile HUARD    
399                                             VPN   
400              Richiesta accesso wifi - guest lan   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
396  {"16":"User identity management, Permissions, ...   
397  {"16":"User identity management, Permissions, ...   
398  {"16":"User identity management, Permissions, ...   
399  {"16":"User identity management, Permissions, ...   
400  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0    HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE...   
1    CIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENS...   
2    CIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN ...   
3    ATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PR...   
4    CIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE ...   
..                                                 ...   
396  CIAO  SAREBBE POSSIBILE DARMI LACCESSO ALLA CA...   
397  CIAO POTETE DARE PER PIACERE LACCESSO ALLA CAR...   
398  BASILE HUARD SAR A BOLZANO DAL 1 MAGGIO ARRIVA...   
399  SONO CON UN HOTSPOT E MI SERVONO LACCESSO ZU H...   
400  CIAO NOSTRO AGENTE SANTIAGO HARDT CHIEDE UN AC...   

                                                tokens  
0    [beim, badge, gleichen, rechte, wie, stephan, ...  
1          [badge, adam, mensa, pagare, riesce, porte]  
2    [ragazzi, domani, tutto, giornata, training, c...  
3    [attualmente, accesso, sede, badge, sbloccate,...  
4    [abilitare, badge, 1083, porte, altri, slovacc...  
..                                                 ...  
396  [sarebbe, darmi, fs01diskgproduktionproduktion...  
397  [piacere, controlling, server, giacomo, giubilei]  
398  [basile, huard, sar, maggio, arriva, italia, v...  
399  [hotspot, servono, h, conesso, vpn, conettano,...  
400  [nostro, agente, santiago, hardt, chiede, acce...  

[401 rows x 4 columns]

In [72]:
df_1_rights = df_1_rights.drop(columns='tokens')
df_1_rights

Title  \
0                    Zugänge Badge Patrick Zingerle   
1                                 Badge Adam Altman   
2                                Acesso Via Siemens   
3           Sbloccare il badge per la sede centrale   
4                                  Bage Adam Altman   
..                                              ...   
396  Accesso a cartella con forecast per produzione   
397                       Acesso server Controlling   
398                             Badge Basile HUARD    
399                                             VPN   
400              Richiesta accesso wifi - guest lan   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
396  {"16":"User identity management, Permissions, ...   
397  {"16":"User identity management, Permissions, ...   
398  {"16":"User identity management, Permissions, ...   
399  {"16":"User identity management, Permissions, ...   
400  {"16":"User identity management, Permissions, ...   

                                                  Text  
0    HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE...  
1    CIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENS...  
2    CIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN ...  
3    ATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PR...  
4    CIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE ...  
..                                                 ...  
396  CIAO  SAREBBE POSSIBILE DARMI LACCESSO ALLA CA...  
397  CIAO POTETE DARE PER PIACERE LACCESSO ALLA CAR...  
398  BASILE HUARD SAR A BOLZANO DAL 1 MAGGIO ARRIVA...  
399  SONO CON UN HOTSPOT E MI SERVONO LACCESSO ZU H...  
400  CIAO NOSTRO AGENTE SANTIAGO HARDT CHIEDE UN AC...  

[401 rows x 3 columns]

# df_1_computer

In [73]:
#df_3_computer
import pandas as pd

words_to_check = ['pc', 'laptop', 'computer', 'phone', 'password']
# Initialize an empty DataFrame to store the matching rows
df_1_computer = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_computer = df_1_computer.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_computer = df_1_computer.reset_index(drop=True)

df_1_computer

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df_1_computer.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df_1_computer.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df_1_computer.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3462105897.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_computer = df

Title  \
0            FW: I: Delayed Mail (still being retried)   
1    FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
2     Nuovo utente per Francesco Bernard Vicenzi Vesco   
3                                     Materiale Armin    
4                            PASSWORD WINDOWS bloccato   
..                                                 ...   
117                                Acess to SAP concur   
118                              Can't send out emails   
119                                     New Technician   
120                                   Active the email   
121                                   Active the email   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
117  {"16":"User identity management, Permissions, ...   
118  {"16":"User identity management, Permissions, ...   
119  {"16":"User identity management, Permissions, ...   
120  {"16":"User identity management, Permissions, ...   
121  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...   
1        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...   
2    QUESTO  UN COLLEGA CHE LAVORA NELLA PRODUZIONE...   
3     CIAO MANUEL   PER IL MATERIALE CHE ARMIN DEVE...   
4    CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA P...   
..                                                 ...   
117  HELLO PLEASE SET ME UP WITH SAP CONCUR AND LET...   
118  DEAR COLLEAGUE GRACELIUTECHNOALPINCOM CAN SEND...   
119  HELLO COULD YOU SEND THE ID AND PASSWORD OF BL...   
120  DEAR COLLEAGUE CAN YOU PLEASE HELP TO CHECK IF...   
121  HELLO MANUEL THEN CAN YOU PLEASE ACTIVATE THE ...   

                                                tokens  
0    [verificare, miei, clienti, riescono, contarmi...  
1    [jiri, krticka, east, europe, sro, sk, 010, 01...  
2    [collega, lavora, xelom, primo, piano, utente,...  
3    [materiale, armin, deve, restituire, volevo, c...  
4    [penso, yu, yang, cambiato, password, tempo, e...  
..                                                 ...  
117  [set, up, sap, concur, let, know, what, login,...  
118  [dear, colleague, graceliutechnoalpincom, send...  
119        [send, password, blandine, karine, jaillet]  
120  [dear, colleague, check, email, activated, res...  
121       [then, activate, email, send, password, lot]  

[122 rows x 4 columns]

In [74]:
df_1_computer

Title  \
0            FW: I: Delayed Mail (still being retried)   
1    FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
2     Nuovo utente per Francesco Bernard Vicenzi Vesco   
3                                     Materiale Armin    
4                            PASSWORD WINDOWS bloccato   
..                                                 ...   
117                                Acess to SAP concur   
118                              Can't send out emails   
119                                     New Technician   
120                                   Active the email   
121                                   Active the email   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
117  {"16":"User identity management, Permissions, ...   
118  {"16":"User identity management, Permissions, ...   
119  {"16":"User identity management, Permissions, ...   
120  {"16":"User identity management, Permissions, ...   
121  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...   
1        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...   
2    QUESTO  UN COLLEGA CHE LAVORA NELLA PRODUZIONE...   
3     CIAO MANUEL   PER IL MATERIALE CHE ARMIN DEVE...   
4    CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA P...   
..                                                 ...   
117  HELLO PLEASE SET ME UP WITH SAP CONCUR AND LET...   
118  DEAR COLLEAGUE GRACELIUTECHNOALPINCOM CAN SEND...   
119  HELLO COULD YOU SEND THE ID AND PASSWORD OF BL...   
120  DEAR COLLEAGUE CAN YOU PLEASE HELP TO CHECK IF...   
121  HELLO MANUEL THEN CAN YOU PLEASE ACTIVATE THE ...   

                                                tokens  
0    [verificare, miei, clienti, riescono, contarmi...  
1    [jiri, krticka, east, europe, sro, sk, 010, 01...  
2    [collega, lavora, xelom, primo, piano, utente,...  
3    [materiale, armin, deve, restituire, volevo, c...  
4    [penso, yu, yang, cambiato, password, tempo, e...  
..                                                 ...  
117  [set, up, sap, concur, let, know, what, login,...  
118  [dear, colleague, graceliutechnoalpincom, send...  
119        [send, password, blandine, karine, jaillet]  
120  [dear, colleague, check, email, activated, res...  
121       [then, activate, email, send, password, lot]  

[122 rows x 4 columns]

In [75]:
df_1_computer = df_1_computer.drop(columns='tokens')
df_1_computer

Title  \
0            FW: I: Delayed Mail (still being retried)   
1    FW: TECHNOALPIN USA INC- TEDJUCTS900 : Upcomin...   
2     Nuovo utente per Francesco Bernard Vicenzi Vesco   
3                                     Materiale Armin    
4                            PASSWORD WINDOWS bloccato   
..                                                 ...   
117                                Acess to SAP concur   
118                              Can't send out emails   
119                                     New Technician   
120                                   Active the email   
121                                   Active the email   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
117  {"16":"User identity management, Permissions, ...   
118  {"16":"User identity management, Permissions, ...   
119  {"16":"User identity management, Permissions, ...   
120  {"16":"User identity management, Permissions, ...   
121  {"16":"User identity management, Permissions, ...   

                                                  Text  
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...  
1        JIRI KRTICKA SALES TECHNOALPIN EAST EUROPE...  
2    QUESTO  UN COLLEGA CHE LAVORA NELLA PRODUZIONE...  
3     CIAO MANUEL   PER IL MATERIALE CHE ARMIN DEVE...  
4    CIAO PENSO CHE LE YU YANG NON HA CAMBIATO LA P...  
..                                                 ...  
117  HELLO PLEASE SET ME UP WITH SAP CONCUR AND LET...  
118  DEAR COLLEAGUE GRACELIUTECHNOALPINCOM CAN SEND...  
119  HELLO COULD YOU SEND THE ID AND PASSWORD OF BL...  
120  DEAR COLLEAGUE CAN YOU PLEASE HELP TO CHECK IF...  
121  HELLO MANUEL THEN CAN YOU PLEASE ACTIVATE THE ...  

[122 rows x 3 columns]

# df_1_software

In [76]:
#df_1_software
import pandas as pd

words_to_check = ['server', 'nav', 'vpn', 'crm', 'sap', 'concur']
# Initialize an empty DataFrame to store the matching rows
df_1_software = pd.DataFrame(columns=df_1.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_1['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_1_software = df_1_software.append(df_1[word_mask])

# Reset the index of the new DataFrame
df_1_software = df_1_software.reset_index(drop=True)

df_1_software

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_software.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_software.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_software.append(df_1[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\369636750.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_1_software = df_1_s

Title  \
0            FW: I: Delayed Mail (still being retried)   
1                      ENGO Mail esterne non arrivano    
2    Sostenibilitá - Servizio esterno config. STEP ...   
3                          permesso scrittura server L   
4                               Connsessione al server   
..                                                 ...   
166                               SAP for Basile HUARD   
167                                Acess to SAP concur   
168                   Profilo Dietmar Mair  SAP Concur   
169                           Concur Andrej Mladenoski   
170                                             Concur   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
166  {"16":"User identity management, Permissions, ...   
167  {"16":"User identity management, Permissions, ...   
168  {"16":"User identity management, Permissions, ...   
169  {"16":"User identity management, Permissions, ...   
170  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...   
1    THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPI...   
2    BUONGIORNO PREGO PASSARE DA M PRIMA DI INIZIAR...   
3    CIAO NON RIESCO A SCRIVERE PI NEL SERVER L CHI...   
4    BUONGIORNO STO LAVORANDO DA REMOTO CON IL PORT...   
..                                                 ...   
166  PLEASE CAN YOU GIVE ACCESS TO BASILE HUARD FOR...   
167  HELLO PLEASE SET ME UP WITH SAP CONCUR AND LET...   
168  PREGO AGGIUNGERE DIVON BETREFF ERHALTEN GRE KA...   
169  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...   
170  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...   

                                                tokens  
0    [verificare, miei, clienti, riescono, contarmi...  
1    [mail, system, host, mailtechnoalpincom, warni...  
2    [passare, prima, iniziare, lavoro, giorgio, st...  
3    [scrivere, server, l, vengano, ridati, diritti...  
4    [sto, lavorando, remoto, portatile, prima, vol...  
..                                                 ...  
166  [give, access, basile, huard, sap, concur, sof...  
167  [set, up, sap, concur, let, know, what, login,...  
168  [divon, erhalten, kategorien, philip, rainer, ...  
169  [impostare, lutente, andrej, mladenoski, utent...  
170  [dear, all, create, concur, account, employee,...  

[171 rows x 4 columns]

In [77]:
df_1_software

Title  \
0            FW: I: Delayed Mail (still being retried)   
1                      ENGO Mail esterne non arrivano    
2    Sostenibilitá - Servizio esterno config. STEP ...   
3                          permesso scrittura server L   
4                               Connsessione al server   
..                                                 ...   
166                               SAP for Basile HUARD   
167                                Acess to SAP concur   
168                   Profilo Dietmar Mair  SAP Concur   
169                           Concur Andrej Mladenoski   
170                                             Concur   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
166  {"16":"User identity management, Permissions, ...   
167  {"16":"User identity management, Permissions, ...   
168  {"16":"User identity management, Permissions, ...   
169  {"16":"User identity management, Permissions, ...   
170  {"16":"User identity management, Permissions, ...   

                                                  Text  \
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...   
1    THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPI...   
2    BUONGIORNO PREGO PASSARE DA M PRIMA DI INIZIAR...   
3    CIAO NON RIESCO A SCRIVERE PI NEL SERVER L CHI...   
4    BUONGIORNO STO LAVORANDO DA REMOTO CON IL PORT...   
..                                                 ...   
166  PLEASE CAN YOU GIVE ACCESS TO BASILE HUARD FOR...   
167  HELLO PLEASE SET ME UP WITH SAP CONCUR AND LET...   
168  PREGO AGGIUNGERE DIVON BETREFF ERHALTEN GRE KA...   
169  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...   
170  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...   

                                                tokens  
0    [verificare, miei, clienti, riescono, contarmi...  
1    [mail, system, host, mailtechnoalpincom, warni...  
2    [passare, prima, iniziare, lavoro, giorgio, st...  
3    [scrivere, server, l, vengano, ridati, diritti...  
4    [sto, lavorando, remoto, portatile, prima, vol...  
..                                                 ...  
166  [give, access, basile, huard, sap, concur, sof...  
167  [set, up, sap, concur, let, know, what, login,...  
168  [divon, erhalten, kategorien, philip, rainer, ...  
169  [impostare, lutente, andrej, mladenoski, utent...  
170  [dear, all, create, concur, account, employee,...  

[171 rows x 4 columns]

In [78]:
df_1_software = df_1_software.drop(columns='tokens')
df_1_software

Title  \
0            FW: I: Delayed Mail (still being retried)   
1                      ENGO Mail esterne non arrivano    
2    Sostenibilitá - Servizio esterno config. STEP ...   
3                          permesso scrittura server L   
4                               Connsessione al server   
..                                                 ...   
166                               SAP for Basile HUARD   
167                                Acess to SAP concur   
168                   Profilo Dietmar Mair  SAP Concur   
169                           Concur Andrej Mladenoski   
170                                             Concur   

                                                 Topic  \
0    {"16":"User identity management, Permissions, ...   
1    {"16":"User identity management, Permissions, ...   
2    {"16":"User identity management, Permissions, ...   
3    {"16":"User identity management, Permissions, ...   
4    {"16":"User identity management, Permissions, ...   
..                                                 ...   
166  {"16":"User identity management, Permissions, ...   
167  {"16":"User identity management, Permissions, ...   
168  {"16":"User identity management, Permissions, ...   
169  {"16":"User identity management, Permissions, ...   
170  {"16":"User identity management, Permissions, ...   

                                                  Text  
0     POTETE VERIFICARE COME MAI I MIEI CLIENTI NON...  
1    THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPI...  
2    BUONGIORNO PREGO PASSARE DA M PRIMA DI INIZIAR...  
3    CIAO NON RIESCO A SCRIVERE PI NEL SERVER L CHI...  
4    BUONGIORNO STO LAVORANDO DA REMOTO CON IL PORT...  
..                                                 ...  
166  PLEASE CAN YOU GIVE ACCESS TO BASILE HUARD FOR...  
167  HELLO PLEASE SET ME UP WITH SAP CONCUR AND LET...  
168  PREGO AGGIUNGERE DIVON BETREFF ERHALTEN GRE KA...  
169  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...  
170  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...  

[171 rows x 3 columns]

# df_2
{"12":"Standard Software: Operating systems, Microsoft Office, Citrix clients, CRM Plugin, Acrobat Reader etc."}

In [79]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('punkt')

# custom list of words to remove (greetings and articles)
custom_stopwords = ['hello', 'hi', 'a', 'an', 'the', 'is', 'di','per','grazie', 'e', 'il', 'ciao','non', 'che','la','da', 'bitte', 'mi', 'hallo', 
                    'die','come','le', 'un', 'saluti','al','technoalpin','prego', 'von', 'danke', 'please','con', 'favore', '39', 'und',
                    'fr', 'una', 'ha', 'via', 'intended', 'ich','potete','mille', 'anche', 'der', '2', 'nicht','ho', '1', 'se', '0471', 
                    'sono', 'use', 'den', 'manuel', 'del','si', 'vi','hi','id', 'ta','das', 'nuovo',
                    'ad', 'agostini','im','information','pi','0', 'buongiorno','mit','f', 'horst',
                    'action','bei','ihr', 'including', 'contains','confidential', 'individual','purpose', 
                    'protected', 'law', 'notify','taking', 'based', 'strictly','prohibited',  
                    'martin', 'thanks', 'solo','in', 'i', 'and', 'you', 'this', 'to', 'it',
                    'for', 'any', 'of', 'not','on', 'my', 'can', 'me','or', 'if', 'by','are', 'ma', 'at', 't', 
                    'have', 'should','might','am', 'delete', 'm','mio', 'alle', 'ancora', 'alla','daniele', 
                    'wwwtechnoalpincom','bolzano','from','fare','tutti','new','mir', 'hanno', 'kann','thank',
                    'matthias', '2023','zu', 'nel', 'auf', 'nella', '39100', 'bozen', 'with','hat','gi',
                    'questo', 'gli', 'sul','o', 'p', 'sie', 'teamviewer','knnt', 'lo','aggiungere', 
                    'dei', 'spa', 'help','specific', 'assegnare', 'team', 'ticket','laccesso', 
                    'serve','gre','della', 'stefan', 'service','betreff', 'n','perch', 
                    'but','suo','habe','firma','ok','no','could','oggi','su', 'ore', 'siemens',
                    'dare','pagostinistrae','200','43','posso' ,'ts','bisogno','delle', 'need', 
                    'produzione','dal','funziona','chiedo','riesco', '441', 'ist', 'neuen', 
                    'questa', 'ti','gruppo', 'that', 'regards', 'when', 'ci', 'so', 'essere', 'aprire',
                    'um','due','mai', 'usa', 'hier', 'we', 'dalle', 'de', 'en', 'zugang', 'noi', 
                    'quando', 'be','auch', 'wir', 'li' ,'cambiare', 'possibile', 'togliere',
                    'mitarbeiter','thomas', 'egregi', 'signori', 'creare', 'patrick', 'adesso',
                    'sales', 'manager','dass','gentilmente', 'mehr','gmbh', 'ept','gesendet', 'entrare', 
                    'cartella', 'problem', 'poi', 'digitale','also','du', 'problema', 'io', 
                    'es', 'here', 'pdf', 'devo', 'as','marco','41', 'provato', 'install', 
                    'tutto', 'eine','va', 'sempre', 'open','work','do','programma','one']

# Tokenize and remove stopwords from the 'Text' column
df_2['tokens'] = df_2['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in custom_stopwords])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_2['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(30)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('outlook', 62), ('email', 62), ('pc', 59), ('pw', 41), ('mail', 38), ('nav', 35), ('password', 35), ('teams', 33), ('laptop', 29), ('office', 27), ('installare', 27), ('microsoft', 27), ('computer', 25), ('prfprotokoll', 23), ('vpn', 22), ('br', 22), ('accedere', 22), ('accesso', 21), ('message', 21), ('find', 20), ('our', 20), ('citrix', 20), ('errore', 18), ('server', 18), ('excel', 18), ('passwort', 18), ('acrobat', 18), ('vdi', 18), ('file', 17), ('adobe', 17)]


# df_2_pc

In [80]:
#df_2_pc
import pandas as pd

words_to_check = ['pc', 'computer', 'accedere', 'pw', 'password',
                  'laptop', 'passwort', 'pwd', 'login', 'accesso']

# Initialize an empty DataFrame to store the matching rows
df_2_pc = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_pc = df_2_pc.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_pc = df_2_pc.reset_index(drop=True)

df_2_pc

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3194719117.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_pc = df_2_pc.append(df_2[word_mask])
C:\Users\Mat

Title  \
0    Stefano Salzburger / Solid Edge / Versione sba...   
1     Im Outlook Office 365 ist keine Signatur möglich   
2    Install Adobe Reader as Defalut PDF reader Wei...   
3                           Probleme connection to all   
4                                           Spam Mails   
..                                                 ...   
282              Microsoft Teams non effettua il login   
283                                     Accesso Folder   
284                                     Citrix non va?   
285                                     Citrix non va?   
286                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
282  {"12":"Standard Software: Operating systems, M...   
283  {"12":"Standard Software: Operating systems, M...   
284  {"12":"Standard Software: Operating systems, M...   
285  {"12":"Standard Software: Operating systems, M...   
286  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURG...   
1    IN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIG...   
2    PLEASE INSTALL THE ADOBE READER ON WEIWEI WANG...   
3     HELLO   CAN YOU HAVE A LOOK ON MY PC CAN NO C...   
4    CIAO LE ULTIME SETTIMANE HO FATTO UNA LISTA DI...   
..                                                 ...   
282              CIAO HO PROBLEMI CON LACCESSO A TEAMS   
283                                    ACCESSO FOLDER    
284  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...   
285  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   
286  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   

                                                tokens  
0    [pc, collega, stefano, salzburger, stata, inst...  
1    [meinem, outlook, office, 365, keine, signatur...  
2    [adobe, reader, weiwei, wangs, pc, set, defaul...  
3    [look, pc, connect, all, navcrm, intranetect, ...  
4    [ultime, settimane, fatto, lista, indirizzi, m...  
..                                                 ...  
282                                  [problemi, teams]  
283                                  [accesso, folder]  
284  [sto, provando, lavorare, citrix, accedere, mi...  
285  [documenti, salvato, locale, pc, voi, avr, acc...  
286  [documenti, salvato, locale, pc, voi, avr, acc...  

[287 rows x 4 columns]

In [81]:
df_2_pc

Title  \
0    Stefano Salzburger / Solid Edge / Versione sba...   
1     Im Outlook Office 365 ist keine Signatur möglich   
2    Install Adobe Reader as Defalut PDF reader Wei...   
3                           Probleme connection to all   
4                                           Spam Mails   
..                                                 ...   
282              Microsoft Teams non effettua il login   
283                                     Accesso Folder   
284                                     Citrix non va?   
285                                     Citrix non va?   
286                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
282  {"12":"Standard Software: Operating systems, M...   
283  {"12":"Standard Software: Operating systems, M...   
284  {"12":"Standard Software: Operating systems, M...   
285  {"12":"Standard Software: Operating systems, M...   
286  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURG...   
1    IN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIG...   
2    PLEASE INSTALL THE ADOBE READER ON WEIWEI WANG...   
3     HELLO   CAN YOU HAVE A LOOK ON MY PC CAN NO C...   
4    CIAO LE ULTIME SETTIMANE HO FATTO UNA LISTA DI...   
..                                                 ...   
282              CIAO HO PROBLEMI CON LACCESSO A TEAMS   
283                                    ACCESSO FOLDER    
284  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...   
285  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   
286  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   

                                                tokens  
0    [pc, collega, stefano, salzburger, stata, inst...  
1    [meinem, outlook, office, 365, keine, signatur...  
2    [adobe, reader, weiwei, wangs, pc, set, defaul...  
3    [look, pc, connect, all, navcrm, intranetect, ...  
4    [ultime, settimane, fatto, lista, indirizzi, m...  
..                                                 ...  
282                                  [problemi, teams]  
283                                  [accesso, folder]  
284  [sto, provando, lavorare, citrix, accedere, mi...  
285  [documenti, salvato, locale, pc, voi, avr, acc...  
286  [documenti, salvato, locale, pc, voi, avr, acc...  

[287 rows x 4 columns]

In [82]:
df_2_pc = df_2_pc.drop(columns='tokens')
df_2_pc

Title  \
0    Stefano Salzburger / Solid Edge / Versione sba...   
1     Im Outlook Office 365 ist keine Signatur möglich   
2    Install Adobe Reader as Defalut PDF reader Wei...   
3                           Probleme connection to all   
4                                           Spam Mails   
..                                                 ...   
282              Microsoft Teams non effettua il login   
283                                     Accesso Folder   
284                                     Citrix non va?   
285                                     Citrix non va?   
286                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
282  {"12":"Standard Software: Operating systems, M...   
283  {"12":"Standard Software: Operating systems, M...   
284  {"12":"Standard Software: Operating systems, M...   
285  {"12":"Standard Software: Operating systems, M...   
286  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURG...  
1    IN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIG...  
2    PLEASE INSTALL THE ADOBE READER ON WEIWEI WANG...  
3     HELLO   CAN YOU HAVE A LOOK ON MY PC CAN NO C...  
4    CIAO LE ULTIME SETTIMANE HO FATTO UNA LISTA DI...  
..                                                 ...  
282              CIAO HO PROBLEMI CON LACCESSO A TEAMS  
283                                    ACCESSO FOLDER   
284  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...  
285  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  
286  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  

[287 rows x 3 columns]

# df_2_email

In [83]:
#df_2_email
import pandas as pd

words_to_check = ['message', 'email', 'outlook', 'emails', 
                  'mail', 'accedere', 'pw', 'password', 'passwort', 
                  'recipient', 'attachments', 'pwd', 'microsoft', 'office', 'app', 'login', 'accesso']


# Initialize an empty DataFrame to store the matching rows
df_2_email = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_email = df_2_email.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_email = df_2_email.reset_index(drop=True)

df_2_email

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\698636073.py:18: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_email = df_2_email.append(df_2[word

Title  \
0                       Error to Login in the Internet   
1    Notification for the alert 'New-InboxRule Crea...   
2                                    WG: Fehlermeldung   
3                     Virtual Machine can`t be started   
4    WG: Non remis : FW: FR0042-23-06A POA Tête dou...   
..                                                 ...   
500              Microsoft Teams non effettua il login   
501                                     Accesso Folder   
502                                     Citrix non va?   
503                                     Citrix non va?   
504                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
500  {"12":"Standard Software: Operating systems, M...   
501  {"12":"Standard Software: Operating systems, M...   
502  {"12":"Standard Software: Operating systems, M...   
503  {"12":"Standard Software: Operating systems, M...   
504  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    HELLO  I NEED TO RENEW THIS CERTIFICATE BUT I ...   
1     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE...   
2     BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN W...   
3    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...   
4     ULTIMAMENTE ABBIAMO DEI PROBLEMI GROSSI CON L...   
..                                                 ...   
500              CIAO HO PROBLEMI CON LACCESSO A TEAMS   
501                                    ACCESSO FOLDER    
502  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...   
503  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   
504  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   

                                                tokens  
0    [renew, certificate, get, error, message, belo...  
1    [caution, external, email, take, care, clickin...  
2    [absender, whitelist, setzen, wichtig, fehlerm...  
3    [press, cirtix, remote, desktop, symbol, conne...  
4    [ultimamente, abbiamo, problemi, grossi, mail,...  
..                                                 ...  
500                                  [problemi, teams]  
501                                  [accesso, folder]  
502  [sto, provando, lavorare, citrix, accedere, mi...  
503  [documenti, salvato, locale, pc, voi, avr, acc...  
504  [documenti, salvato, locale, pc, voi, avr, acc...  

[505 rows x 4 columns]

In [84]:
df_2_email

Title  \
0                       Error to Login in the Internet   
1    Notification for the alert 'New-InboxRule Crea...   
2                                    WG: Fehlermeldung   
3                     Virtual Machine can`t be started   
4    WG: Non remis : FW: FR0042-23-06A POA Tête dou...   
..                                                 ...   
500              Microsoft Teams non effettua il login   
501                                     Accesso Folder   
502                                     Citrix non va?   
503                                     Citrix non va?   
504                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
500  {"12":"Standard Software: Operating systems, M...   
501  {"12":"Standard Software: Operating systems, M...   
502  {"12":"Standard Software: Operating systems, M...   
503  {"12":"Standard Software: Operating systems, M...   
504  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    HELLO  I NEED TO RENEW THIS CERTIFICATE BUT I ...   
1     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE...   
2     BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN W...   
3    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...   
4     ULTIMAMENTE ABBIAMO DEI PROBLEMI GROSSI CON L...   
..                                                 ...   
500              CIAO HO PROBLEMI CON LACCESSO A TEAMS   
501                                    ACCESSO FOLDER    
502  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...   
503  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   
504  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...   

                                                tokens  
0    [renew, certificate, get, error, message, belo...  
1    [caution, external, email, take, care, clickin...  
2    [absender, whitelist, setzen, wichtig, fehlerm...  
3    [press, cirtix, remote, desktop, symbol, conne...  
4    [ultimamente, abbiamo, problemi, grossi, mail,...  
..                                                 ...  
500                                  [problemi, teams]  
501                                  [accesso, folder]  
502  [sto, provando, lavorare, citrix, accedere, mi...  
503  [documenti, salvato, locale, pc, voi, avr, acc...  
504  [documenti, salvato, locale, pc, voi, avr, acc...  

[505 rows x 4 columns]

In [85]:
df_2_email = df_2_email.drop(columns = 'tokens')
df_2_email

Title  \
0                       Error to Login in the Internet   
1    Notification for the alert 'New-InboxRule Crea...   
2                                    WG: Fehlermeldung   
3                     Virtual Machine can`t be started   
4    WG: Non remis : FW: FR0042-23-06A POA Tête dou...   
..                                                 ...   
500              Microsoft Teams non effettua il login   
501                                     Accesso Folder   
502                                     Citrix non va?   
503                                     Citrix non va?   
504                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
500  {"12":"Standard Software: Operating systems, M...   
501  {"12":"Standard Software: Operating systems, M...   
502  {"12":"Standard Software: Operating systems, M...   
503  {"12":"Standard Software: Operating systems, M...   
504  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    HELLO  I NEED TO RENEW THIS CERTIFICATE BUT I ...  
1     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE...  
2     BITTE DEN ABSENDER AUF DIE WHITELIST SETZEN W...  
3    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...  
4     ULTIMAMENTE ABBIAMO DEI PROBLEMI GROSSI CON L...  
..                                                 ...  
500              CIAO HO PROBLEMI CON LACCESSO A TEAMS  
501                                    ACCESSO FOLDER   
502  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...  
503  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  
504  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  

[505 rows x 3 columns]

# Further refinement

## look for df_2_email 'access'

In [86]:
import pandas as pd
import re

In [87]:
related_words = ['access', 'accessing', 'accessible', 'accessed', 'accesses', 'entry', 
                 'approach', 'admission', 'entrance', 'reach', 'open', 'connect', 
                 'visit', 'retrieve', 'use','Zugang', 'Zugriff', 'zugänglich',
                 'zugriffen', 'Zugänge', 'Eingang', 'Herangehensweise', 'Zulassung',
                 'Eingang', 'erreichen', 'öffnen', 'verbinden', 'besuchen', 'abrufen', 'benutzen',
                 'accesso', 'accesso', 'accessibile', 'accesso', 'accessi', 
                 'entrata', 'approccio', 'ammissione', 'ingresso', 'raggiungere', 
                 'aprire', 'collegare', 'visitare', 'recuperare', 'usare']

In [88]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_2_email = df_2_email[df_2_email['Text'].str.contains(pattern, case=False)]
filtered_df_2_email = filtered_df_2_email.reset_index(drop=True)

filtered_df_2_email

Title  \
0                     Virtual Machine can`t be started   
1                                        Outlook issue   
2    Linda Zhang - Excel is not working over Citrix...   
3           can't open contracts in d.3 smart explorer   
4                           Collaborazione EmiControls   
..                                                 ...   
101                                     Setup nuovo PC   
102                                     Accesso Folder   
103                                     Citrix non va?   
104                                     Citrix non va?   
105                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
101  {"12":"Standard Software: Operating systems, M...   
102  {"12":"Standard Software: Operating systems, M...   
103  {"12":"Standard Software: Operating systems, M...   
104  {"12":"Standard Software: Operating systems, M...   
105  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...  
1    HELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ...  
2    CIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN...  
3    HI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY ...  
4     DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBR...  
..                                                 ...  
101  POSSIAMO ANCHE AGGIUNGERE ACCESSO AL DRIVE XMO...  
102                                    ACCESSO FOLDER   
103  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...  
104  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  
105  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  

[106 rows x 3 columns]

In [89]:
filtered_df_2_email

Title  \
0                     Virtual Machine can`t be started   
1                                        Outlook issue   
2    Linda Zhang - Excel is not working over Citrix...   
3           can't open contracts in d.3 smart explorer   
4                           Collaborazione EmiControls   
..                                                 ...   
101                                     Setup nuovo PC   
102                                     Accesso Folder   
103                                     Citrix non va?   
104                                     Citrix non va?   
105                                     Citrix non va?   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
101  {"12":"Standard Software: Operating systems, M...   
102  {"12":"Standard Software: Operating systems, M...   
103  {"12":"Standard Software: Operating systems, M...   
104  {"12":"Standard Software: Operating systems, M...   
105  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP ...  
1    HELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ...  
2    CIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN...  
3    HI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY ...  
4     DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBR...  
..                                                 ...  
101  POSSIAMO ANCHE AGGIUNGERE ACCESSO AL DRIVE XMO...  
102                                    ACCESSO FOLDER   
103  CIAO STO PROVANDO DI LAVORARE CON CITRIX MA NO...  
104  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  
105  TUTTI I DOCUMENTI CHE HO SALVATO IN LOCALE SUL...  

[106 rows x 3 columns]

In [90]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_2_email[i:i+n] for i in range(0,len(filtered_df_2_email),n)]
    #print(list_df)

In [91]:
len(list_df)

22

In [92]:
list_df[18]

Title  \
90                      Camera non funziona da casa   
91                              Accesso Teamviewer    
92                              Accesso Teamviewer    
93  Ticket system - raggiunto max prove per entrare   
94  Ticket system - raggiunto max prove per entrare   

                                                Topic  \
90  {"12":"Standard Software: Operating systems, M...   
91  {"12":"Standard Software: Operating systems, M...   
92  {"12":"Standard Software: Operating systems, M...   
93  {"12":"Standard Software: Operating systems, M...   
94  {"12":"Standard Software: Operating systems, M...   

                                                 Text  
90  CIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA C...  
91                   DIFFICOLT CON ACCESSO TEAMVIEWER  
92  CIAO MANUEL NON RIESCO AD ACCEDERE A TEAMVIEWE...  
93  CIAO VOLEVO FARE IL PRIMO ACCESSO AL TICKET SY...  
94  FATTOCON ACCESSO AL RD MECH OUTDOOR  SALUTI GE...

In [93]:
def put_together():
    list1=[]
    for index in range(0,18):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [94]:
summ_block = put_together()
summ_block

Result 0:
HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP SYMBOL TO CONNECT TO MY VIRTUAL MACHINE THIS MESSAGE SHOWS UP AN THE VIRTUAL MACHINE DOESNT OPENS I CANT REALLY WORK WITHOUT THE VIRTUAL MACHINE SO PLEASE TRY TO FIX IT SOONHELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ME TO OUTLOOK I HAVE AN ERROR MESSAGE COULD YOU DO SOMETHING PLEASE  BEST REGARDS VINCENT GADOISCIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN SYSTEM VIA CITRIX VDI DESKTOP SHE HAS TO DOWNLOAD EXCEL LISTS FROM NAV EDIT AND LINK THEM TO NAV CLAIMSWHEN SHE TRIES TO OPEN AND EDIT THE EXCEL LIST IT LOGS ON WITH HER USER LINDA ZHANG BUT AN ERROR MESSAGE APPEARS AND SAYS THAT WHITH THIS ACCOUNT IT IS NOT POSSIBLE TO USE EXCEL IN VDI IS THIS A LICENSING PROBLEM BR MARTINHI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY TO OPEN AN CONTRACT DXIG THIS MESSAGE IS DISPLAYED IT SAYS I SHOULD ACTIVATE D3 VIEW VERWENDEN BUT IT IS ACTIVATED CAN YOU HELP ME HERE PLEASE DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FU

['HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP SYMBOL TO CONNECT TO MY VIRTUAL MACHINE THIS MESSAGE SHOWS UP AN THE VIRTUAL MACHINE DOESNT OPENS I CANT REALLY WORK WITHOUT THE VIRTUAL MACHINE SO PLEASE TRY TO FIX IT SOONHELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ME TO OUTLOOK I HAVE AN ERROR MESSAGE COULD YOU DO SOMETHING PLEASE  BEST REGARDS VINCENT GADOISCIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN SYSTEM VIA CITRIX VDI DESKTOP SHE HAS TO DOWNLOAD EXCEL LISTS FROM NAV EDIT AND LINK THEM TO NAV CLAIMSWHEN SHE TRIES TO OPEN AND EDIT THE EXCEL LIST IT LOGS ON WITH HER USER LINDA ZHANG BUT AN ERROR MESSAGE APPEARS AND SAYS THAT WHITH THIS ACCOUNT IT IS NOT POSSIBLE TO USE EXCEL IN VDI IS THIS A LICENSING PROBLEM BR MARTINHI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY TO OPEN AN CONTRACT DXIG THIS MESSAGE IS DISPLAYED IT SAYS I SHOULD ACTIVATE\xa0D3 VIEW VERWENDEN BUT IT IS ACTIVATED CAN YOU HELP ME HERE PLEASE DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTT

In [95]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 18):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [96]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP SYMBOL TO CONNECT TO MY VIRTUAL MACHINE THIS MESSAGE SHOWS UP AN THE VIRTUAL MACHINE DOESNT OPENS I CANT REALLY WORK WITHOUT THE VIRTUAL MACHINE SO PLEASE TRY TO FIX IT SOONHELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ME TO OUTLOOK I HAVE AN ERROR MESSAGE COULD YOU DO SOMETHING PLEASE  BEST REGARDS VINCENT GADOISCIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN SYSTEM VIA CITRIX VDI DESKTOP SHE HAS TO DOWNLOAD EXCEL LISTS FROM NAV EDIT AND LINK THEM TO NAV CLAIMSWHEN SHE TRIES TO OPEN AND EDIT THE EXCEL LIST IT LOGS ON WITH HER USER LINDA ZHANG BUT AN ERROR MESSAGE APPEARS AND SAYS THAT WHITH THIS ACCOUNT IT IS NOT POSSIBLE TO USE EXCEL IN VDI IS THIS A LICENSING PROBLEM BR MARTINHI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY TO OPEN AN CONTRACT DXIG THIS MESSAGE IS DISPLAYED IT SAYS I SHOULD ACTIVATE D3 VIEW VERWENDEN BUT IT IS ACTIVATED CAN YOU HELP ME HERE PLEASE DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FU

In [97]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP SYMBOL TO CONNECT TO MY VIRTUAL MACHINE THIS MESSAGE SHOWS UP AN THE VIRTUAL MACHINE DOESNT OPENS I CANT REALLY WORK WITHOUT THE VIRTUAL MACHINE SO PLEASE TRY TO FIX IT SOONHELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ME TO OUTLOOK I HAVE AN ERROR MESSAGE COULD YOU DO SOMETHING PLEASE  BEST REGARDS VINCENT GADOISCIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN SYSTEM VIA CITRIX VDI DESKTOP SHE HAS TO DOWNLOAD EXCEL LISTS FROM NAV EDIT AND LINK THEM TO NAV CLAIMSWHEN SHE TRIES TO OPEN AND EDIT THE EXCEL LIST IT LOGS ON WITH HER USER LINDA ZHANG BUT AN ERROR MESSAGE APPEARS AND SAYS THAT WHITH THIS ACCOUNT IT IS NOT POSSIBLE TO USE EXCEL IN VDI IS THIS A LICENSING PROBLEM BR MARTINHI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY TO OPEN AN CONTRACT DXIG THIS MESSAGE IS DISPLAYED IT SAYS I SHOULD ACTIVATE D3 VIEW VERWENDEN BUT IT IS ACTIVATED CAN YOU HELP ME HERE PLEASE DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FU

['HELLO IF I PRESS ON THE CIRTIX REMOTE DESKTOP SYMBOL TO CONNECT TO MY VIRTUAL MACHINE THIS MESSAGE SHOWS UP AN THE VIRTUAL MACHINE DOESNT OPENS I CANT REALLY WORK WITHOUT THE VIRTUAL MACHINE SO PLEASE TRY TO FIX IT SOONHELLOAFTER CHANGED MY PASSWORD I CANT CONNECT ME TO OUTLOOK I HAVE AN ERROR MESSAGE COULD YOU DO SOMETHING PLEASE  BEST REGARDS VINCENT GADOISCIAO WHEN LINDA ZHANG IS ACCESSING THE ITALIAN SYSTEM VIA CITRIX VDI DESKTOP SHE HAS TO DOWNLOAD EXCEL LISTS FROM NAV EDIT AND LINK THEM TO NAV CLAIMSWHEN SHE TRIES TO OPEN AND EDIT THE EXCEL LIST IT LOGS ON WITH HER USER LINDA ZHANG BUT AN ERROR MESSAGE APPEARS AND SAYS THAT WHITH THIS ACCOUNT IT IS NOT POSSIBLE TO USE EXCEL IN VDI IS THIS A LICENSING PROBLEM BR MARTINHI GUYS I HAVE A PROBLEM WITH MY DMS IF I TRY TO OPEN AN CONTRACT DXIG THIS MESSAGE IS DISPLAYED IT SAYS I SHOULD ACTIVATE\xa0D3 VIEW VERWENDEN BUT IT IS ACTIVATED CAN YOU HELP ME HERE PLEASE DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTT

In [98]:
pip install transformers

Note: you may need to restart the kernel to use updated packages.


In [99]:
import pickle

# picklefile = "filtered_df_2_email.pkl"
with open(picklefile, "rb") as pkl_rb_obj:
	summ_block = pickle.load(pkl_rb_obj)
print(summ_block)

# df_2_email_signature

In [100]:
import pandas as pd
import re

In [101]:
related_words = [
    'Firma', 'Autografo', 'Sottoscrizione', 'Segno distintivo', 'Sigla', 'Marcatura',
    'Ratifica', 'Apposizione di firma', 'Sigillo', 'Atto autografo',
    'Signature', 'Autograph', 'Mark', 'Seal', 'Sign-off',
    'Inked mark', 'Signatory', 'Handwriting', 'Personal mark',
    'Unterschrift', 'Autogramm', 'Kennzeichen', 'Siegel', 'Namenszug', 'Paraphe',
    'Besiegelung', 'Unterzeichnung', 'Handschrift', 'Eigenhändige Unterschrift'
]

In [102]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_2_email_signature = df_2_email[df_1_email['Text'].str.contains(pattern, case=False)]
filtered_df_2_email_signature = filtered_df_2_email_signature.reset_index(drop=True)

filtered_df_2_email_signature

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2694673618.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  filtered_df_2_email_signature = df_2_email[df_1_email['Text'].str.contains(pattern, case=False)]


Title  \
0                                      archivio email   
1                                      Email to TA CN   
2             Email Massenversandt funktioniert nicht   
3                                            outlook    
4                     Collegamento MS TEAMS e OUTLOOK   
5                     Mads Mörch / Mattias Hakansson    
6       Accesso all'indirizzo mail 3Dplanning via web   
7              Pacchetto office- prodotto disattivato   
8                 Creare un Teams meeting via Outlook   
9       Avvio lentissimo dei sistemi PC Verena Pattis   
10                                  Outlook signature   
11                                Outlook on computer   
12               Mails weiterleiten an Daniela Harder   
13                      Outlook Mails kommen nicht an   
14                                              Spam?   
15                                     Email to TA CN   
16                                         VPN Zugang   
17                              Outlook missing Mails   
18                                     accesso server   
19             Pacchetto office- prodotto disattivato   
20                         One Drive non funziona piu   
21                                             Smap3D   
22                                         ECtiClient   
23                               G and S Drive access   
24                                   Zugriff Netwerke   
25     Patrick Danielsson - Install ECM Webintegraion   
26          unable to install Microsoft Authenticator   
27           problemi account / software con nuovo PC   
28  Notification for the alert 'New-InboxRule Crea...   
29                          Microsoft suite not legal   
30                   CRM with Microsoft Authenticator   
31                                  WG: Fehlermeldung   
32                                   Microsoft office   
33      Avvio lentissimo dei sistemi PC Verena Pattis   
34                                        viva engage   
35           problemi account / software con nuovo PC   
36                                     Accesso Citrix   
37                            Cambio di Arnold Siller   
38      Accesso all'indirizzo mail 3Dplanning via web   

                                                Topic  \
0   {"12":"Standard Software: Operating systems, M...   
1   {"12":"Standard Software: Operating systems, M...   
2   {"12":"Standard Software: Operating systems, M...   
3   {"12":"Standard Software: Operating systems, M...   
4   {"12":"Standard Software: Operating systems, M...   
5   {"12":"Standard Software: Operating systems, M...   
6   {"12":"Standard Software: Operating systems, M...   
7   {"12":"Standard Software: Operating systems, M...   
8   {"12":"Standard Software: Operating systems, M...   
9   {"12":"Standard Software: Operating systems, M...   
10  {"12":"Standard Software: Operating systems, M...   
11  {"12":"Standard Software: Operating systems, M...   
12  {"12":"Standard Software: Operating systems, M...   
13  {"12":"Standard Software: Operating systems, M...   
14  {"12":"Standard Software: Operating systems, M...   
15  {"12":"Standard Software: Operating systems, M...   
16  {"12":"Standard Software: Operating systems, M...   
17  {"12":"Standard Software: Operating systems, M...   
18  {"12":"Standard Software: Operating systems, M...   
19  {"12":"Standard Software: Operating systems, M...   
20  {"12":"Standard Software: Operating systems, M...   
21  {"12":"Standard Software: Operating systems, M...   
22  {"12":"Standard Software: Operating systems, M...   
23  {"12":"Standard Software: Operating systems, M...   
24  {"12":"Standard Software: Operating systems, M...   
25  {"12":"Standard Software: Operating systems, M...   
26  {"12":"Standard Software: Operating systems, M...   
27  {"12":"Standard Software: Operating systems, M...   
28  {"12":"Standard Software: Operating systems, M...   
29  {"12":"Standard Software: Operating systems, M...   


In [103]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_2_email_signature[i:i+n] for i in range(0,len(filtered_df_2_email_signature),n)]
    #print(list_df)

In [104]:
len(list_df)

8

In [105]:
list_df[7]

Title  \
35       problemi account / software con nuovo PC   
36                                 Accesso Citrix   
37                        Cambio di Arnold Siller   
38  Accesso all'indirizzo mail 3Dplanning via web   

                                                Topic  \
35  {"12":"Standard Software: Operating systems, M...   
36  {"12":"Standard Software: Operating systems, M...   
37  {"12":"Standard Software: Operating systems, M...   
38  {"12":"Standard Software: Operating systems, M...   

                                                 Text  
35  BUONGIORNO  SUL NUOVO PC HO PROBLEMI DI ACCOUN...  
36  SALVE VOLEVO CHIEDERE SE LACCESSO AL CITRIX  D...  
37  ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VEND...  
38  CIAO A TUTTI QUANDO LAVORO IN SMARTWORKING UTI...

In [106]:
def put_together():
    list1=[]
    for index in range(0,7):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


summ_block = put_together()
summ_block

Result 0:
SU OUTLOOK NON VEDO PI LARCHIVIO DELLE VECCHIE EMAIL COME PROCEDIAMO  GRAZIE SALUTI ICH KANN DIESES EMAIL NICHT AN UNSERE KOLLEGEN VON TACN SCHICKEN EMAILS OHNE DOKUMENT IN ANLAGE FUNKTIONIEREN VIELE GRE MICHAELHALLO WOLLTE NUN DIE ADRESSNDERUNG VERSCHICKEN BER INFOCH  UND ES HAT 45 MAL NICHT FUNKTIONIERT  ZUERST DACHTE ICH ES LIEGT DARAN DASS ZU VIELE EMAIL ADRESSEN DRIN SIND ABER DAS KANN NICHT SEIN ICH HABE EINMAL EINS MIT 80 VERSCHICKT DAS GING  DANN MIT 60 50 UND 20 EMAIL ADRESSEN DAS GING ALLES NICHT MEHR ZUM VERSCHICKEN WO LIEGT DAS PROBLEM DAS MSSTE HEUTE NOCH RAUS DANKE UND GRSSEHELLO COULD YOU PLEASE HELP ME WITH OUTLOOK IT IS NOT POSSIBLE TO SIGH IN AND I DO NOT RECEIVE ANY EMAILS THERE IS ACCESS TO INTERNET BUT NO CONNECTION WITH OUTLOOK THEREFORE I CAN NOT WORK  THANK YOUBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRA

['SU OUTLOOK NON VEDO PI LARCHIVIO DELLE VECCHIE EMAIL COME PROCEDIAMO  GRAZIE SALUTI ICH KANN DIESES EMAIL NICHT AN UNSERE KOLLEGEN VON TACN SCHICKEN EMAILS OHNE DOKUMENT IN ANLAGE FUNKTIONIEREN VIELE GRE MICHAELHALLO WOLLTE NUN DIE ADRESSNDERUNG VERSCHICKEN BER INFOCH  UND ES HAT 45 MAL NICHT FUNKTIONIERT\xa0 ZUERST DACHTE ICH ES LIEGT DARAN DASS ZU VIELE\xa0EMAIL ADRESSEN DRIN SIND ABER DAS KANN NICHT SEIN ICH HABE EINMAL EINS MIT 80 VERSCHICKT DAS GING  DANN MIT 60 50 UND 20 EMAIL ADRESSEN DAS GING ALLES NICHT MEHR ZUM VERSCHICKEN WO LIEGT DAS PROBLEM DAS MSSTE HEUTE NOCH RAUS DANKE UND GRSSEHELLO COULD YOU PLEASE HELP ME WITH OUTLOOK IT IS NOT POSSIBLE TO SIGH IN AND I DO NOT RECEIVE ANY EMAILS THERE IS ACCESS TO INTERNET BUT NO CONNECTION WITH OUTLOOK THEREFORE I CAN NOT WORK\xa0 THANK YOUBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS\xa0

In [107]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 7):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [108]:
blocks_to_skip = [1]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
SU OUTLOOK NON VEDO PI LARCHIVIO DELLE VECCHIE EMAIL COME PROCEDIAMO  GRAZIE SALUTI ICH KANN DIESES EMAIL NICHT AN UNSERE KOLLEGEN VON TACN SCHICKEN EMAILS OHNE DOKUMENT IN ANLAGE FUNKTIONIEREN VIELE GRE MICHAELHALLO WOLLTE NUN DIE ADRESSNDERUNG VERSCHICKEN BER INFOCH  UND ES HAT 45 MAL NICHT FUNKTIONIERT  ZUERST DACHTE ICH ES LIEGT DARAN DASS ZU VIELE EMAIL ADRESSEN DRIN SIND ABER DAS KANN NICHT SEIN ICH HABE EINMAL EINS MIT 80 VERSCHICKT DAS GING  DANN MIT 60 50 UND 20 EMAIL ADRESSEN DAS GING ALLES NICHT MEHR ZUM VERSCHICKEN WO LIEGT DAS PROBLEM DAS MSSTE HEUTE NOCH RAUS DANKE UND GRSSEHELLO COULD YOU PLEASE HELP ME WITH OUTLOOK IT IS NOT POSSIBLE TO SIGH IN AND I DO NOT RECEIVE ANY EMAILS THERE IS ACCESS TO INTERNET BUT NO CONNECTION WITH OUTLOOK THEREFORE I CAN NOT WORK  THANK YOUBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRA

In [109]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
SU OUTLOOK NON VEDO PI LARCHIVIO DELLE VECCHIE EMAIL COME PROCEDIAMO  GRAZIE SALUTI ICH KANN DIESES EMAIL NICHT AN UNSERE KOLLEGEN VON TACN SCHICKEN EMAILS OHNE DOKUMENT IN ANLAGE FUNKTIONIEREN VIELE GRE MICHAELHALLO WOLLTE NUN DIE ADRESSNDERUNG VERSCHICKEN BER INFOCH  UND ES HAT 45 MAL NICHT FUNKTIONIERT  ZUERST DACHTE ICH ES LIEGT DARAN DASS ZU VIELE EMAIL ADRESSEN DRIN SIND ABER DAS KANN NICHT SEIN ICH HABE EINMAL EINS MIT 80 VERSCHICKT DAS GING  DANN MIT 60 50 UND 20 EMAIL ADRESSEN DAS GING ALLES NICHT MEHR ZUM VERSCHICKEN WO LIEGT DAS PROBLEM DAS MSSTE HEUTE NOCH RAUS DANKE UND GRSSEHELLO COULD YOU PLEASE HELP ME WITH OUTLOOK IT IS NOT POSSIBLE TO SIGH IN AND I DO NOT RECEIVE ANY EMAILS THERE IS ACCESS TO INTERNET BUT NO CONNECTION WITH OUTLOOK THEREFORE I CAN NOT WORK  THANK YOUBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRA

['SU OUTLOOK NON VEDO PI LARCHIVIO DELLE VECCHIE EMAIL COME PROCEDIAMO  GRAZIE SALUTI ICH KANN DIESES EMAIL NICHT AN UNSERE KOLLEGEN VON TACN SCHICKEN EMAILS OHNE DOKUMENT IN ANLAGE FUNKTIONIEREN VIELE GRE MICHAELHALLO WOLLTE NUN DIE ADRESSNDERUNG VERSCHICKEN BER INFOCH  UND ES HAT 45 MAL NICHT FUNKTIONIERT\xa0 ZUERST DACHTE ICH ES LIEGT DARAN DASS ZU VIELE\xa0EMAIL ADRESSEN DRIN SIND ABER DAS KANN NICHT SEIN ICH HABE EINMAL EINS MIT 80 VERSCHICKT DAS GING  DANN MIT 60 50 UND 20 EMAIL ADRESSEN DAS GING ALLES NICHT MEHR ZUM VERSCHICKEN WO LIEGT DAS PROBLEM DAS MSSTE HEUTE NOCH RAUS DANKE UND GRSSEHELLO COULD YOU PLEASE HELP ME WITH OUTLOOK IT IS NOT POSSIBLE TO SIGH IN AND I DO NOT RECEIVE ANY EMAILS THERE IS ACCESS TO INTERNET BUT NO CONNECTION WITH OUTLOOK THEREFORE I CAN NOT WORK\xa0 THANK YOUBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS\xa0

# df_2_email_phishing

In [110]:
import pandas as pd
import re

In [111]:
related_words = ['Phishing', 'Pesca fraudolenta', 'Inganno online', 'Truffa informatica', 'Frode via email',
    'Phishing', 'Online scam', 'Email fraud', 'Deceptive online tactics', 'Cyber deception',
    'Phishing', 'Online-Betrug', 'Internet-Täuschung', 'E-Mail-Betrug', 'Cyber-Betrug',
    'Inganno informatico', 'Pesca di informazioni', 'Truffa digitale',
    'Digital deception', 'Information harvesting', 'Online fraud',
    'Digitale Täuschung', 'Informationsdiebstahl', 'Online-Betrug','Spam', 'Posta indesiderata', 
    'Messaggi non richiesti', 'Posta spazzatura', 'Invio massivo di email',
    'Spam', 'Unsolicited email', 'Junk mail', 'Email overload', 'Bulk messaging',
    'Spam', 'Unerwünschte E-Mails', 'Junk-Mail', 'E-Mail-Überflutung', 'Massenversand von Nachrichten',
    'Posta non desiderata', 'Messaggi di spam', 'Comunicazioni indesiderate',
    'Unwanted mail', 'Spam messages', 'Unsolicited communications',
    'Unerwünschte Post', 'Spam-Nachrichten', 'Ungebetene Kommunikation']

In [112]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_2_email_phishing = df_2_email[df_2_email['Text'].str.contains(pattern, case=False)]
filtered_df_2_email_phishing = filtered_df_2_email_phishing.reset_index(drop=True)

filtered_df_2_email_phishing

Title  \
0                         Collaborazione EmiControls   
1                         Collaborazione EmiControls   
2                                         Spam Mails   
3                                 impostazioni SPAM    
4                                              Spam?   
5  Important mails in Outlook go all to Spam sinc...   
6                                              Spam?   

                                               Topic  \
0  {"12":"Standard Software: Operating systems, M...   
1  {"12":"Standard Software: Operating systems, M...   
2  {"12":"Standard Software: Operating systems, M...   
3  {"12":"Standard Software: Operating systems, M...   
4  {"12":"Standard Software: Operating systems, M...   
5  {"12":"Standard Software: Operating systems, M...   
6  {"12":"Standard Software: Operating systems, M...   

                                                Text  
0   DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBR...  
1   DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBR...  
2  CIAO LE ULTIME SETTIMANE HO FATTO UNA LISTA DI...  
3  CIAO TANTI DOMAIN VENGONO TRATTATI COME SPAM A...  
4  CIAO HO APPENA RICEVUTO QUESTA MAIL CREDO SIA ...  
5  HELLO MANY IMPORTANT MAILS COMING FROM SUPPLIE...  
6  CIAO HO APPENA RICEVUTO QUESTA MAIL CREDO SIA ...

In [113]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_2_email_phishing[i:i+n] for i in range(0,len(filtered_df_2_email_phishing),n)]
    #print(list_df)

In [114]:
len(list_df)

2

In [115]:
list_df[0]

Title  \
0  Collaborazione EmiControls   
1  Collaborazione EmiControls   
2                  Spam Mails   
3          impostazioni SPAM    
4                       Spam?   

                                               Topic  \
0  {"12":"Standard Software: Operating systems, M...   
1  {"12":"Standard Software: Operating systems, M...   
2  {"12":"Standard Software: Operating systems, M...   
3  {"12":"Standard Software: Operating systems, M...   
4  {"12":"Standard Software: Operating systems, M...   

                                                Text  
0   DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBR...  
1   DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBR...  
2  CIAO LE ULTIME SETTIMANE HO FATTO UNA LISTA DI...  
3  CIAO TANTI DOMAIN VENGONO TRATTATI COME SPAM A...  
4  CIAO HO APPENA RICEVUTO QUESTA MAIL CREDO SIA ...

In [116]:
def put_together():
    list1=[]
    for index in range(0,1):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


summ_block = put_together()
summ_block

Result 0:
 DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM     TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO      HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM     A PRESTO MATTEO          DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE 

[' DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS   \xa0 CIAO MANUEL  \xa0 UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE \xa0 NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE \xa0 VEDI SOTTO \xa0 GRAZIE DOMINIK  \xa0 \xa0  NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM  \xa0  TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO   \xa0  HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM  \xa0  A PRESTO MATTEO  \xa0       DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS   \xa0 CIAO MANUEL  \xa0 UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE \xa0 NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE \xa0 VEDI SOTTO \xa0 GRAZIE DOMINIK  \xa0 \xa0  NEL FRATTEMPO TI AVVER

In [117]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 1):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [118]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
 DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM     TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO      HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM     A PRESTO MATTEO          DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE 

In [119]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
 DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM     TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO      HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM     A PRESTO MATTEO          DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE 

[' DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS   \xa0 CIAO MANUEL  \xa0 UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE \xa0 NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE \xa0 VEDI SOTTO \xa0 GRAZIE DOMINIK  \xa0 \xa0  NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM  \xa0  TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO   \xa0  HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM  \xa0  A PRESTO MATTEO  \xa0       DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS   \xa0 CIAO MANUEL  \xa0 UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE \xa0 NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE \xa0 VEDI SOTTO \xa0 GRAZIE DOMINIK  \xa0 \xa0  NEL FRATTEMPO TI AVVER

# df_2_access

In [120]:
#df_2_access
import pandas as pd

words_to_check = ['teams', 'login', 'accesso', 'accedere', 'pw', 'password']


# Initialize an empty DataFrame to store the matching rows
df_2_access = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_access = df_2_access.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_access = df_2_access.reset_index(drop=True)

df_2_access

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\981805679.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_access = df_2_access.append(d

Title  \
0                    One Drive non funziona piu   
1    Microsoft Teams non funziona correttamente   
2                      TEAMS Audio non funziona   
3              Outlook  Termine erstellen TEams   
4               Collegamento MS TEAMS e OUTLOOK   
..                                          ...   
183                              ACROBAT WRITER   
184                       Downloading adobe pro   
185            ONE DRIVE TECHNOALPIN EPOWERTRAC   
186                              Setup nuovo PC   
187                              Update Windows   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
183  {"12":"Standard Software: Operating systems, M...   
184  {"12":"Standard Software: Operating systems, M...   
185  {"12":"Standard Software: Operating systems, M...   
186  {"12":"Standard Software: Operating systems, M...   
187  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0                ANCHE NEL TEAMS NON SONO PIU LE DATI    
1    CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRE...   
2    COMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO...   
3    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...   
4    BUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI...   
..                                                 ...   
183  LUTENZA  STATA COMPRATA DALLA DITTA EPOWERTRAC...   
184  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...   
185  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...   
186  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...   
187  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...   

                                                tokens  
0                                   [teams, piu, dati]  
1    [microsoft, teams, correttamente, miei, colleg...  
2    [computer, c405, teams, persona, chiama, suona...  
3    [vedo, piu, link, teams, meeting, creo, appunt...  
4    [collegamento, tra, programmi, sopracitati, fi...  
..                                                 ...  
183  [lutenza, stata, comprata, dalla, ditta, epowe...  
184  [trying, adobe, pro, will, let, had, old, inst...  
185  [accesso, vedo, 10, cartelle, drive, epowertra...  
186  [lid, rimane, password, aveva, timeout, qui, q...  
187  [update, windows, viewer, 545, 489, 361passwor...  

[188 rows x 4 columns]

In [121]:
df_2_access

Title  \
0                    One Drive non funziona piu   
1    Microsoft Teams non funziona correttamente   
2                      TEAMS Audio non funziona   
3              Outlook  Termine erstellen TEams   
4               Collegamento MS TEAMS e OUTLOOK   
..                                          ...   
183                              ACROBAT WRITER   
184                       Downloading adobe pro   
185            ONE DRIVE TECHNOALPIN EPOWERTRAC   
186                              Setup nuovo PC   
187                              Update Windows   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
183  {"12":"Standard Software: Operating systems, M...   
184  {"12":"Standard Software: Operating systems, M...   
185  {"12":"Standard Software: Operating systems, M...   
186  {"12":"Standard Software: Operating systems, M...   
187  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0                ANCHE NEL TEAMS NON SONO PIU LE DATI    
1    CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRE...   
2    COMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO...   
3    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...   
4    BUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI...   
..                                                 ...   
183  LUTENZA  STATA COMPRATA DALLA DITTA EPOWERTRAC...   
184  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...   
185  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...   
186  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...   
187  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...   

                                                tokens  
0                                   [teams, piu, dati]  
1    [microsoft, teams, correttamente, miei, colleg...  
2    [computer, c405, teams, persona, chiama, suona...  
3    [vedo, piu, link, teams, meeting, creo, appunt...  
4    [collegamento, tra, programmi, sopracitati, fi...  
..                                                 ...  
183  [lutenza, stata, comprata, dalla, ditta, epowe...  
184  [trying, adobe, pro, will, let, had, old, inst...  
185  [accesso, vedo, 10, cartelle, drive, epowertra...  
186  [lid, rimane, password, aveva, timeout, qui, q...  
187  [update, windows, viewer, 545, 489, 361passwor...  

[188 rows x 4 columns]

In [122]:
df_2_access = df_2_access.drop(columns = 'tokens')
df_2_access

Title  \
0                    One Drive non funziona piu   
1    Microsoft Teams non funziona correttamente   
2                      TEAMS Audio non funziona   
3              Outlook  Termine erstellen TEams   
4               Collegamento MS TEAMS e OUTLOOK   
..                                          ...   
183                              ACROBAT WRITER   
184                       Downloading adobe pro   
185            ONE DRIVE TECHNOALPIN EPOWERTRAC   
186                              Setup nuovo PC   
187                              Update Windows   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
183  {"12":"Standard Software: Operating systems, M...   
184  {"12":"Standard Software: Operating systems, M...   
185  {"12":"Standard Software: Operating systems, M...   
186  {"12":"Standard Software: Operating systems, M...   
187  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0                ANCHE NEL TEAMS NON SONO PIU LE DATI   
1    CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRE...  
2    COMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO...  
3    CIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS...  
4    BUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI...  
..                                                 ...  
183  LUTENZA  STATA COMPRATA DALLA DITTA EPOWERTRAC...  
184  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...  
185  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...  
186  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...  
187  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...  

[188 rows x 3 columns]

# df_2_software

In [123]:
#df_2_software
import pandas as pd

words_to_check = ['installare', 'nav', 'citrix', 'vpn', 'edge', 'acrobat', 'prfprotokoll', 'vdi', 'server']

# Initialize an empty DataFrame to store the matching rows
df_2_software = pd.DataFrame(columns=df_2.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_2['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_2_software = df_2_software.append(df_2[word_mask])

# Reset the index of the new DataFrame
df_2_software = df_2_software.reset_index(drop=True)

df_2_software

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df_2_software.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df_2_software.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df_2_software.append(df_2[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2289260216.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_2_software = df

Title  \
0    Patrick Danielsson - Install ECM Webintegraion   
1                        Problemi Acesso Teamviewer   
2                                     DWG TRUE view   
3                            Accesso amministratore   
4                                  Office365 x C255   
..                                              ...   
196                Outlook Synchroisierungsprobleme   
197                               Foxxit PDF Viewer   
198                               Solid Edge Lizenz   
199                                  Setup nuovo PC   
200                              Solide Edge Lizenz   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
196  {"12":"Standard Software: Operating systems, M...   
197  {"12":"Standard Software: Operating systems, M...   
198  {"12":"Standard Software: Operating systems, M...   
199  {"12":"Standard Software: Operating systems, M...   
200  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATI...   
1    HO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI...   
2         CIAO MANUEL    AVREI BISOGNO DI INSTALLAR...   
3    MI SERVE IL PERMESSO DEL AMMINISTRATORE PER IN...   
4    PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA M...   
..                                                 ...   
196  HALLO HABE AM FREITAG MEIN LAPTOP GEWECHSELT H...   
197  HELLO IS THE FOXXIT PDF VIEWER INSTALLEREXE SO...   
198  GUTEN NACHMITTAG MEIN SOLID EDGE FOUNDATION FU...   
199  UPDATE NON DOBBIAMO INSTALLARLO MA C DA SISTEM...   
200  ERA IL SERVER DI LICENZA GRAZIE ADESSA FUNZION...   

                                                tokens  
0    [installare, ecm, webintegration, danielsson, ...  
1                      [reinstallare, risolto, niente]  
2    [avrei, installare, oggetto, posto, attuale, d...  
3    [permesso, amministratore, installare, codesys...  
4    [installare, word, excel, ed, outlook, macchin...  
..                                                 ...  
196  [freitag, mein, laptop, gewechselt, seidem, pr...  
197  [foxxit, viewer, installerexe, somewhere, serv...  
198  [guten, nachmittag, mein, solid, edge, foundat...  
199  [update, dobbiamo, installarlo, c, sistemare, ...  
200                     [era, server, licenza, adessa]  

[201 rows x 4 columns]

In [124]:
df_2_software

Title  \
0    Patrick Danielsson - Install ECM Webintegraion   
1                        Problemi Acesso Teamviewer   
2                                     DWG TRUE view   
3                            Accesso amministratore   
4                                  Office365 x C255   
..                                              ...   
196                Outlook Synchroisierungsprobleme   
197                               Foxxit PDF Viewer   
198                               Solid Edge Lizenz   
199                                  Setup nuovo PC   
200                              Solide Edge Lizenz   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
196  {"12":"Standard Software: Operating systems, M...   
197  {"12":"Standard Software: Operating systems, M...   
198  {"12":"Standard Software: Operating systems, M...   
199  {"12":"Standard Software: Operating systems, M...   
200  {"12":"Standard Software: Operating systems, M...   

                                                  Text  \
0    CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATI...   
1    HO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI...   
2         CIAO MANUEL    AVREI BISOGNO DI INSTALLAR...   
3    MI SERVE IL PERMESSO DEL AMMINISTRATORE PER IN...   
4    PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA M...   
..                                                 ...   
196  HALLO HABE AM FREITAG MEIN LAPTOP GEWECHSELT H...   
197  HELLO IS THE FOXXIT PDF VIEWER INSTALLEREXE SO...   
198  GUTEN NACHMITTAG MEIN SOLID EDGE FOUNDATION FU...   
199  UPDATE NON DOBBIAMO INSTALLARLO MA C DA SISTEM...   
200  ERA IL SERVER DI LICENZA GRAZIE ADESSA FUNZION...   

                                                tokens  
0    [installare, ecm, webintegration, danielsson, ...  
1                      [reinstallare, risolto, niente]  
2    [avrei, installare, oggetto, posto, attuale, d...  
3    [permesso, amministratore, installare, codesys...  
4    [installare, word, excel, ed, outlook, macchin...  
..                                                 ...  
196  [freitag, mein, laptop, gewechselt, seidem, pr...  
197  [foxxit, viewer, installerexe, somewhere, serv...  
198  [guten, nachmittag, mein, solid, edge, foundat...  
199  [update, dobbiamo, installarlo, c, sistemare, ...  
200                     [era, server, licenza, adessa]  

[201 rows x 4 columns]

In [125]:
df_2_software = df_2_software.drop(columns = 'tokens')
df_2_software

Title  \
0    Patrick Danielsson - Install ECM Webintegraion   
1                        Problemi Acesso Teamviewer   
2                                     DWG TRUE view   
3                            Accesso amministratore   
4                                  Office365 x C255   
..                                              ...   
196                Outlook Synchroisierungsprobleme   
197                               Foxxit PDF Viewer   
198                               Solid Edge Lizenz   
199                                  Setup nuovo PC   
200                              Solide Edge Lizenz   

                                                 Topic  \
0    {"12":"Standard Software: Operating systems, M...   
1    {"12":"Standard Software: Operating systems, M...   
2    {"12":"Standard Software: Operating systems, M...   
3    {"12":"Standard Software: Operating systems, M...   
4    {"12":"Standard Software: Operating systems, M...   
..                                                 ...   
196  {"12":"Standard Software: Operating systems, M...   
197  {"12":"Standard Software: Operating systems, M...   
198  {"12":"Standard Software: Operating systems, M...   
199  {"12":"Standard Software: Operating systems, M...   
200  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
0    CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATI...  
1    HO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI...  
2         CIAO MANUEL    AVREI BISOGNO DI INSTALLAR...  
3    MI SERVE IL PERMESSO DEL AMMINISTRATORE PER IN...  
4    PREGO INSTALLARE WORD EXCEL ED OUTLOOK SU LA M...  
..                                                 ...  
196  HALLO HABE AM FREITAG MEIN LAPTOP GEWECHSELT H...  
197  HELLO IS THE FOXXIT PDF VIEWER INSTALLEREXE SO...  
198  GUTEN NACHMITTAG MEIN SOLID EDGE FOUNDATION FU...  
199  UPDATE NON DOBBIAMO INSTALLARLO MA C DA SISTEM...  
200  ERA IL SERVER DI LICENZA GRAZIE ADESSA FUNZION...  

[201 rows x 3 columns]

# df_3
{"11":"Hardware, Telephony, Smartphones, Monitor, Printer,  etc"}

In [126]:
import pandas as pd
from nltk.tokenize import word_tokenize
from nltk.corpus import stopwords
from collections import Counter

import nltk
nltk.download('punkt')

# custom list of words to remove (greetings and articles)
custom_stopwords = ['hello', 'hi', 'a', 'an', 'the', 'is', 'di','per','grazie', 'e', 'il', 'ciao','non', 'che','la','da', 'bitte', 'mi', 'hallo', 
                    'die','come','le', 'un', 'saluti','al','technoalpin','prego', 'von', 'danke', 'please','con', 'favore', '39', 'und',
                    'fr', 'una', 'ha', 'via', 'intended', 'ich','potete','mille', 'anche', 'der', '2', 'nicht','ho', '1', 'se', '0471', 
                    'sono', 'use', 'den', 'manuel', 'del','si', 'vi','hi','id', 'ta','das', 'nuovo',
                    'ad', 'agostini','im','information','pi','0', 'buongiorno','mit','f', 'horst',
                    'action','bei','ihr', 'including', 'contains','confidential', 'individual','purpose', 
                    'protected', 'law', 'notify','taking', 'based', 'strictly','prohibited',  
                    'martin', 'thanks', 'solo','in', 'i', 'and', 'you', 'this', 'to', 'it',
                    'for', 'any', 'of', 'not','on', 'my', 'can', 'me','or', 'if', 'by','are', 'ma', 'at', 't', 
                    'have', 'should','might','am', 'delete', 'm','mio', 'alle', 'ancora', 'alla','daniele', 
                    'wwwtechnoalpincom','bolzano','from','fare','tutti','new','mir', 'hanno', 'kann','thank',
                    'matthias', '2023','zu', 'nel', 'auf', 'nella', '39100', 'bozen', 'with','hat','gi',
                    'questo', 'gli', 'sul','o', 'p', 'sie', 'teamviewer','knnt', 'lo','aggiungere', 
                    'dei', 'spa', 'help','specific', 'assegnare', 'team', 'ticket','laccesso', 
                    'serve','gre','della', 'stefan', 'service','betreff', 'n','perch', 
                    'but','suo','habe','firma','ok','no','could','oggi','su', 'ore', 'siemens',
                    'dare','pagostinistrae','200','43','posso' ,'ts','bisogno','delle', 'need', 
                    'produzione','dal','funziona','chiedo','riesco', '441', 'ist', 'neuen', 
                    'questa', 'ti','gruppo', 'that', 'regards', 'when', 'ci', 'so', 'essere', 'aprire',
                    'um','due','mai', 'usa', 'hier', 'we', 'dalle', 'de', 'en', 'zugang', 'noi', 
                    'quando', 'be','auch', 'wir', 'li' ,'cambiare', 'possibile', 'togliere',
                    'mitarbeiter','thomas', 'egregi', 'signori', 'creare', 'patrick', 'adesso',
                    'sales', 'manager','dass','gentilmente', 'mehr','gmbh', 'ept','gesendet', 'entrare', 
                    'cartella', 'problem', 'poi', 'digitale','also','du', 'problema', 'io', 
                    'es', 'here', 'pdf', 'devo', 'as','marco','41', 'provato', 'install', 
                    'tutto', 'eine','va', 'sempre', 'open','work','do','programma','one', 
                    'verificare','message','installato', '3306', 'high','ufficio', 'problemi', 
                    'uno','prone','t41', 'netprodclientsofficewlan','abbiamo', 'avere', 
                    'vulnerability', 'fa', 'francesco', 'sarebbe', 'installare', 'purtroppo', 'avete',
                    '75', 'fatto', 'multiple', 'dos', 'funktioniert','vecchio', 'domani','qualche',
                    'numero', 'piu', 'volta']

# Tokenize and remove stopwords from the 'Text' column
df_3['tokens'] = df_3['Text'].apply(lambda x: [word.lower() for word in word_tokenize(x) if word.isalnum() and word.lower() not in custom_stopwords])

# Flatten the tokenized words into a single list
all_words = [word for sublist in df_3['tokens'].tolist() for word in sublist]

# Count the occurrences of each word
word_counts = Counter(all_words)

# Find the most common words
most_common_words = word_counts.most_common(30)  # Change 10 to the desired number of top words
print(most_common_words)


[nltk_data] Downloading package punkt to
[nltk_data]     C:\Users\MattiaA\AppData\Roaming\nltk_data...
[nltk_data]   Package punkt is already up-to-date!


[('stampante', 106), ('pc', 86), ('laptop', 81), ('telefono', 49), ('monitor', 36), ('drucker', 35), ('stampare', 34), ('docking', 33), ('rete', 29), ('cellulare', 27), ('printer', 26), ('usb', 23), ('settimana', 22), ('stampa', 22), ('station', 22), ('cavo', 21), ('fisso', 20), ('zebra', 20), ('voi', 20), ('computer', 19), ('ein', 19), ('password', 19), ('nuova', 19), ('era', 19), ('mia', 19), ('bene', 18), ('prima', 18), ('mail', 18), ('possiamo', 18), ('hp', 18)]


# df_3_telephony

In [127]:
import pandas as pd

In [128]:
words_to_check= ['telefono', 'cellulare', 'smartphone', 'phone', 'Mobile device', 'cell phone', 'mobile'
                 , 'mobile phone', 'cellulare', 'Dispositivo mobile','Mobilgerät', 'Handy','Mobiltelefon',
                 'Handgerät']

In [129]:
df_3_telephony = pd.DataFrame(columns= df_3.columns)

for words in words_to_check:
    word_mask= df_3['Text'].str.contains(word,case=False)
    
    df_3_telephony= df_3_telephony.append(df_3[word_mask])
    
df_3_telephony= df_3_telephony.reset_index(drop= True)
df_3_telephony
    

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\395342756.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_telephony= df_3_telephony.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\395342756.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_telephony= df_3_telephony.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\395342756.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_telephony= df_3_telephony.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\395342756.py:6: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_telephony= df_3_te

Title  \
0                Panasonic Telephone has no connection   
1                                     Modula Scaffale    
2                  Kein Zugriff auf Server für Telefon   
3                                               IP KNX   
4                              Nuovi Uffici Epowertrac   
..                                                 ...   
135              WG: Fernzugriff Visualisierungsserver   
136  für die elektronische Übermittlung statistisch...   
137                                         Server MFD   
138                                         Server MFD   
139                                         Server MFD   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
135  {"11":"Hardware, Telephony, Smartphones, Monit...   
136  {"11":"Hardware, Telephony, Smartphones, Monit...   
137  {"11":"Hardware, Telephony, Smartphones, Monit...   
138  {"11":"Hardware, Telephony, Smartphones, Monit...   
139  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY ...   
1    SI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCC...   
2    SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BE...   
3    OK IT IS THE 105803 FROM THE GIRA SERVER THIS ...   
4    BUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICAR...   
..                                                 ...   
135   HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   ...   
136   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   
137  CIAO  POSSIBILE CONNETERMI AL SERVER IN FRANCI...   
138  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...   
139  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...   

                                                tokens  
0    [dhcp, server, found, errore, display, errore,...  
1    [georg, riunione, georg, occupa, degli, pc, re...  
2    [sehr, geehrte, damen, herren, msste, benutzer...  
3    [105803, gira, server, our, control, building,...  
4    [anticipato, dobbiamo, pianificare, lattivazio...  
..                                                 ...  
135  [wer, erstellen, beste, grsse, albiez, leiter,...  
136  [entschuldigung, aber, diese, seite, verfgbar,...  
137  [connetermi, server, francia, istallarmi, stam...  
138  [server, stampante, stampante, lavorare, dover...  
139  [server, stampante, stampante, lavorare, dover...  

[140 rows x 4 columns]

In [130]:
df_3_telephony = df_3_telephony.drop(columns= 'tokens')
df_3_telephony

Title  \
0                Panasonic Telephone has no connection   
1                                     Modula Scaffale    
2                  Kein Zugriff auf Server für Telefon   
3                                               IP KNX   
4                              Nuovi Uffici Epowertrac   
..                                                 ...   
135              WG: Fernzugriff Visualisierungsserver   
136  für die elektronische Übermittlung statistisch...   
137                                         Server MFD   
138                                         Server MFD   
139                                         Server MFD   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
135  {"11":"Hardware, Telephony, Smartphones, Monit...   
136  {"11":"Hardware, Telephony, Smartphones, Monit...   
137  {"11":"Hardware, Telephony, Smartphones, Monit...   
138  {"11":"Hardware, Telephony, Smartphones, Monit...   
139  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY ...  
1    SI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCC...  
2    SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BE...  
3    OK IT IS THE 105803 FROM THE GIRA SERVER THIS ...  
4    BUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICAR...  
..                                                 ...  
135   HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   ...  
136   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...  
137  CIAO  POSSIBILE CONNETERMI AL SERVER IN FRANCI...  
138  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...  
139  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...  

[140 rows x 3 columns]

In [131]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_3_telephony[i:i+n] for i in range(0,len(df_3_telephony),n)]
    #print(list_df)

In [132]:
len(list_df)

24

In [133]:
list_df[23]

Title                                              Topic  \
138  Server MFD  {"11":"Hardware, Telephony, Smartphones, Monit...   
139  Server MFD  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
138  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...  
139  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...

In [134]:
def put_together():
    list1=[]
    for index in range(0,24):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY IL ERRORE  ARRIVATO OGGI DOPO PRANZOSI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCCUPA DEGLI PC OR DELLA RETE NON MI SA SPIEGARE BENE COME  INTESO IL COLLEGAMENTO E CON QUALE SERVER ETC  MI SAPEVA SOLO DIRE CHE SERVE LIP DELLO SCAFFALE E CHE SERVE UN PC HO PARLATO CON I LAVORATORI CHE HANNO MONTATO LO SCAFFALE INTANTO DOBBIAMO METTERE UN SECONDO CAVO ETHERNET PER COLLEGARE IL PCCLIENT E IL SCAFFALE SAREBBE IDEALE SE CI SENTIAMO DOMANI VERSO LE 10 COS POSSIAMO CHIARIRE TUTTO PENSO CHE AVEVA PARLATO CON MANUEL LULTIMA VOLTA SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BENUTZERNAMEN BEI EINEM FIXTELEFON ABNDERN HABE ABER KEINEN ZUGRIFF AUF DEN SERVER 1921682710  GRE HORSTOK IT IS THE 105803 FROM THE GIRA SERVER THIS IS OUR CONTROL FOR THE BUILDING AT FIRST I THOUGHT THAT WE HAD OUR OWN ACCESS TO THE BUS SYSTEM KNX BUT I THINK THATS ALL ABOUT GIRABUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICARE LATTIVAZIONE DEGLI NUOVI UFFICI EPOWERTRAC 

['DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY IL ERRORE  ARRIVATO OGGI DOPO PRANZOSI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCCUPA DEGLI PC OR DELLA RETE NON MI SA SPIEGARE BENE COME  INTESO IL COLLEGAMENTO E CON QUALE SERVER ETC\xa0 MI SAPEVA SOLO DIRE CHE SERVE LIP DELLO SCAFFALE E CHE SERVE UN PC HO PARLATO CON I LAVORATORI CHE HANNO MONTATO LO SCAFFALE INTANTO DOBBIAMO METTERE UN SECONDO CAVO ETHERNET PER COLLEGARE IL PCCLIENT E IL SCAFFALE SAREBBE IDEALE SE CI SENTIAMO DOMANI VERSO LE 10 COS POSSIAMO CHIARIRE TUTTO PENSO CHE AVEVA PARLATO CON MANUEL LULTIMA VOLTA SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BENUTZERNAMEN BEI EINEM FIXTELEFON ABNDERN HABE ABER KEINEN ZUGRIFF AUF DEN SERVER 1921682710  GRE HORSTOK IT IS THE 105803 FROM THE GIRA SERVER\xa0THIS IS OUR CONTROL FOR THE BUILDING AT FIRST I THOUGHT THAT WE HAD OUR OWN ACCESS TO THE BUS SYSTEM KNX BUT I THINK THATS ALL ABOUT GIRABUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICARE LATTIVAZIONE DEGLI NUOVI UFFICI EPOWERTRAC IL

In [135]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0,24):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [136]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY IL ERRORE  ARRIVATO OGGI DOPO PRANZOSI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCCUPA DEGLI PC OR DELLA RETE NON MI SA SPIEGARE BENE COME  INTESO IL COLLEGAMENTO E CON QUALE SERVER ETC  MI SAPEVA SOLO DIRE CHE SERVE LIP DELLO SCAFFALE E CHE SERVE UN PC HO PARLATO CON I LAVORATORI CHE HANNO MONTATO LO SCAFFALE INTANTO DOBBIAMO METTERE UN SECONDO CAVO ETHERNET PER COLLEGARE IL PCCLIENT E IL SCAFFALE SAREBBE IDEALE SE CI SENTIAMO DOMANI VERSO LE 10 COS POSSIAMO CHIARIRE TUTTO PENSO CHE AVEVA PARLATO CON MANUEL LULTIMA VOLTA SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BENUTZERNAMEN BEI EINEM FIXTELEFON ABNDERN HABE ABER KEINEN ZUGRIFF AUF DEN SERVER 1921682710  GRE HORSTOK IT IS THE 105803 FROM THE GIRA SERVER THIS IS OUR CONTROL FOR THE BUILDING AT FIRST I THOUGHT THAT WE HAD OUR OWN ACCESS TO THE BUS SYSTEM KNX BUT I THINK THATS ALL ABOUT GIRABUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICARE LATTIVAZIONE DEGLI NUOVI UFFICI EPOWERTRAC 

In [137]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY IL ERRORE  ARRIVATO OGGI DOPO PRANZOSI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCCUPA DEGLI PC OR DELLA RETE NON MI SA SPIEGARE BENE COME  INTESO IL COLLEGAMENTO E CON QUALE SERVER ETC  MI SAPEVA SOLO DIRE CHE SERVE LIP DELLO SCAFFALE E CHE SERVE UN PC HO PARLATO CON I LAVORATORI CHE HANNO MONTATO LO SCAFFALE INTANTO DOBBIAMO METTERE UN SECONDO CAVO ETHERNET PER COLLEGARE IL PCCLIENT E IL SCAFFALE SAREBBE IDEALE SE CI SENTIAMO DOMANI VERSO LE 10 COS POSSIAMO CHIARIRE TUTTO PENSO CHE AVEVA PARLATO CON MANUEL LULTIMA VOLTA SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BENUTZERNAMEN BEI EINEM FIXTELEFON ABNDERN HABE ABER KEINEN ZUGRIFF AUF DEN SERVER 1921682710  GRE HORSTOK IT IS THE 105803 FROM THE GIRA SERVER THIS IS OUR CONTROL FOR THE BUILDING AT FIRST I THOUGHT THAT WE HAD OUR OWN ACCESS TO THE BUS SYSTEM KNX BUT I THINK THATS ALL ABOUT GIRABUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICARE LATTIVAZIONE DEGLI NUOVI UFFICI EPOWERTRAC 

['DHCP SERVER NOT FOUND E IL ERRORE SUL DISPLAY IL ERRORE  ARRIVATO OGGI DOPO PRANZOSI GEORG HA FATTO RIUNIONE MA GEORG NON SI OCCUPA DEGLI PC OR DELLA RETE NON MI SA SPIEGARE BENE COME  INTESO IL COLLEGAMENTO E CON QUALE SERVER ETC\xa0 MI SAPEVA SOLO DIRE CHE SERVE LIP DELLO SCAFFALE E CHE SERVE UN PC HO PARLATO CON I LAVORATORI CHE HANNO MONTATO LO SCAFFALE INTANTO DOBBIAMO METTERE UN SECONDO CAVO ETHERNET PER COLLEGARE IL PCCLIENT E IL SCAFFALE SAREBBE IDEALE SE CI SENTIAMO DOMANI VERSO LE 10 COS POSSIAMO CHIARIRE TUTTO PENSO CHE AVEVA PARLATO CON MANUEL LULTIMA VOLTA SEHR GEEHRTE DAMEN UND HERREN ICH MSSTE DEN BENUTZERNAMEN BEI EINEM FIXTELEFON ABNDERN HABE ABER KEINEN ZUGRIFF AUF DEN SERVER 1921682710  GRE HORSTOK IT IS THE 105803 FROM THE GIRA SERVER\xa0THIS IS OUR CONTROL FOR THE BUILDING AT FIRST I THOUGHT THAT WE HAD OUR OWN ACCESS TO THE BUS SYSTEM KNX BUT I THINK THATS ALL ABOUT GIRABUONGIORNO COME ANTICIPATO DOBBIAMO PIANIFICARE LATTIVAZIONE DEGLI NUOVI UFFICI EPOWERTRAC IL

In [138]:
from transformers import pipeline
# Create a summarization pipeline with the specified model.
summarizer = pipeline("summarization", model="philschmid/bart-large-cnn-samsum")

# Define a function to perform summarization.
def final_summ():
    my_list = []

    # Iterate through the comments in 'summ_block'
    for index in range(len(summ_block_test)):
        comment = summ_block_test[index]
        prova = summarizer(comment)
        my_list.append(prova)

    return my_list

# Call the 'final_summ' function to generate summaries.
summ_block_test = final_summ()
summ_block_test


Your max_length is set to 142, but you input_length is only 100. You might consider decreasing max_length manually, e.g. summarizer('...', max_length=50)


[[{'summary_text': "HDPI SERVER is not found. It is the 105803 from the GIRA SERVER. It's the control for the building. It gives them access to the Bus System KNX. It also gives them control to the Internet Protocol Add-ons."}],
 [{'summary_text': 'ENTSCHULDIGUNG ABER DIESE SEITE, VERBINDUNG WURDE ZURCKGESETZT, VERSUCHEN BERPRFUNG, VERbINDUJEN, PROXYSERVER UND FIREWALLSTEUERUNG, WINDOWSNETZWERKDIAGNOSE, POSSIBILE CONNETERMI AL SERVER IN FRANCIA, LA STAMPANTE LOCALE GRAZIEIL SERVER PER AVERE LA STAMPTANTE E LA STampantE PER LAVORARE, QUALCOSAIL SER'}],
 [{'summary_text': "It's the 105803 from the GIRA SERVERVERVER. It's our control for the building. It is an EXTERNAL EMAIL. Caution is taken when clicking links or opening attachments. It will be delivered on 25 April 2023 1516."}],
 [{'summary_text': 'IL SERVER PER AVERE E LA STAMPANTE PER LAVORARE E NON DOVER. IL ERRORE SUL DISPLAY  ARRIVATO OGGI DOPO PRANZOSI GEORG HA FATTO RIUNIONE MA GEorG.'}],
 [{'summary_text': 'This is an EXTERNAL

In [139]:
import pickle


# df_3_printer

In [140]:
#df_3_printer
import pandas as pd

words_to_check = ['stampante', 'stampare', 'printer', 'drucker', 'zebra', 'stampa']

# Initialize an empty DataFrame to store the matching rows
df_3_printer = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_printer = df_3_printer.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_printer = df_3_printer.reset_index(drop=True)

df_3_printer

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\245910723.py:15: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_printer = df_3_printer.

Title  \
0                        Deviazione delle chiamate   
1    Errore di stampa Stampante ufficio QHSE - PDF   
2                                        Stampante   
3                Stampante da Ernesto non funziona   
4                    Installazione stampante su PC   
..                                             ...   
320                                     Server MFD   
321                                     Server MFD   
322                    stampante ufficio logistica   
323                  TATN - Collegamento Stampante   
324                  Formati di stampa del plotter   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
320  {"11":"Hardware, Telephony, Smartphones, Monit...   
321  {"11":"Hardware, Telephony, Smartphones, Monit...   
322  {"11":"Hardware, Telephony, Smartphones, Monit...   
323  {"11":"Hardware, Telephony, Smartphones, Monit...   
324  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    BUON D DA QUALCHE TEMPO ORMAI CHE HO NOTATO UN...   
1    CIAO A VOI QUANDO MANDO IN STAMPA UN PDF SULLA...   
2    BUONGIORNO NON RIESCO A STAMPARE MERANER MI DI...   
3    LA STAMPANTE DI ERNESTO NON FUNZIONA RIMANE OF...   
4    PER FAVORE INSTALLARE LA STAMPANTE DELLUFFICIO...   
..                                                 ...   
320  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...   
321  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...   
322  NON RIUSCIAMO PI A STAMPARE E FARE SCANSIONI P...   
323  BUONGIORNO NECESSITO COLLEGAMENTO A STAMPANTE ...   
324  BUON POMERIGGIOCAPITA CHE PER INTERI POMERIGGI...   

                                                tokens  
0    [buon, d, tempo, ormai, notato, riduzione, tem...  
1    [voi, mando, stampa, sulla, stampante, hp, las...  
2    [stampare, meraner, dice, stampante, dovrebbe,...  
3                [stampante, ernesto, rimane, offline]  
4    [stampante, dellufficio, invoicing, anita, k, pc]  
..                                                 ...  
320  [server, stampante, stampante, lavorare, dover...  
321  [server, stampante, stampante, lavorare, dover...  
322         [riusciamo, stampare, scansioni, potreste]  
323  [necessito, collegamento, stampante, presso, t...  
324  [buon, pomeriggiocapita, interi, pomeriggi, pl...  

[325 rows x 4 columns]

In [141]:
df_3_printer

Title  \
0                        Deviazione delle chiamate   
1    Errore di stampa Stampante ufficio QHSE - PDF   
2                                        Stampante   
3                Stampante da Ernesto non funziona   
4                    Installazione stampante su PC   
..                                             ...   
320                                     Server MFD   
321                                     Server MFD   
322                    stampante ufficio logistica   
323                  TATN - Collegamento Stampante   
324                  Formati di stampa del plotter   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
320  {"11":"Hardware, Telephony, Smartphones, Monit...   
321  {"11":"Hardware, Telephony, Smartphones, Monit...   
322  {"11":"Hardware, Telephony, Smartphones, Monit...   
323  {"11":"Hardware, Telephony, Smartphones, Monit...   
324  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    BUON D DA QUALCHE TEMPO ORMAI CHE HO NOTATO UN...   
1    CIAO A VOI QUANDO MANDO IN STAMPA UN PDF SULLA...   
2    BUONGIORNO NON RIESCO A STAMPARE MERANER MI DI...   
3    LA STAMPANTE DI ERNESTO NON FUNZIONA RIMANE OF...   
4    PER FAVORE INSTALLARE LA STAMPANTE DELLUFFICIO...   
..                                                 ...   
320  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...   
321  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...   
322  NON RIUSCIAMO PI A STAMPARE E FARE SCANSIONI P...   
323  BUONGIORNO NECESSITO COLLEGAMENTO A STAMPANTE ...   
324  BUON POMERIGGIOCAPITA CHE PER INTERI POMERIGGI...   

                                                tokens  
0    [buon, d, tempo, ormai, notato, riduzione, tem...  
1    [voi, mando, stampa, sulla, stampante, hp, las...  
2    [stampare, meraner, dice, stampante, dovrebbe,...  
3                [stampante, ernesto, rimane, offline]  
4    [stampante, dellufficio, invoicing, anita, k, pc]  
..                                                 ...  
320  [server, stampante, stampante, lavorare, dover...  
321  [server, stampante, stampante, lavorare, dover...  
322         [riusciamo, stampare, scansioni, potreste]  
323  [necessito, collegamento, stampante, presso, t...  
324  [buon, pomeriggiocapita, interi, pomeriggi, pl...  

[325 rows x 4 columns]

In [142]:
df_3_printer = df_3_printer.drop(columns = 'tokens')
df_3_printer

Title  \
0                        Deviazione delle chiamate   
1    Errore di stampa Stampante ufficio QHSE - PDF   
2                                        Stampante   
3                Stampante da Ernesto non funziona   
4                    Installazione stampante su PC   
..                                             ...   
320                                     Server MFD   
321                                     Server MFD   
322                    stampante ufficio logistica   
323                  TATN - Collegamento Stampante   
324                  Formati di stampa del plotter   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
320  {"11":"Hardware, Telephony, Smartphones, Monit...   
321  {"11":"Hardware, Telephony, Smartphones, Monit...   
322  {"11":"Hardware, Telephony, Smartphones, Monit...   
323  {"11":"Hardware, Telephony, Smartphones, Monit...   
324  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    BUON D DA QUALCHE TEMPO ORMAI CHE HO NOTATO UN...  
1    CIAO A VOI QUANDO MANDO IN STAMPA UN PDF SULLA...  
2    BUONGIORNO NON RIESCO A STAMPARE MERANER MI DI...  
3    LA STAMPANTE DI ERNESTO NON FUNZIONA RIMANE OF...  
4    PER FAVORE INSTALLARE LA STAMPANTE DELLUFFICIO...  
..                                                 ...  
320  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...  
321  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...  
322  NON RIUSCIAMO PI A STAMPARE E FARE SCANSIONI P...  
323  BUONGIORNO NECESSITO COLLEGAMENTO A STAMPANTE ...  
324  BUON POMERIGGIOCAPITA CHE PER INTERI POMERIGGI...  

[325 rows x 3 columns]

# df_3_docking

In [143]:
#df_3_docking
import pandas as pd
words_to_check = ['docking', 'cavo', 'rete', 'lan', 'station']

# Initialize an empty DataFrame to store the matching rows
df_3_docking = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_docking = df_3_docking.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_docking = df_3_docking.reset_index(drop=True)

df_3_docking

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\770040326.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_docking = df_3_docking.

Title  \
0                                           Bildschirm   
1                                   Verificare la rete   
2                       External Monitor not connected   
3                                 Problemi con Monitor   
4             Porte USB Dockingstation non funzionano.   
..                                                 ...   
142  Cavo USB-C per collegare portatile a docking s...   
143                                    docking station   
144         Stazione di lavoro da Christian Tschimben    
145                        Docking station no ethernet   
146      PC che fa rumore. Microfono o audio difettoso   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
142  {"11":"Hardware, Telephony, Smartphones, Monit...   
143  {"11":"Hardware, Telephony, Smartphones, Monit...   
144  {"11":"Hardware, Telephony, Smartphones, Monit...   
145  {"11":"Hardware, Telephony, Smartphones, Monit...   
146  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ...   
1    CIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBB...   
2    DEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH ...   
3    CIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MO...   
4    CIAO  LE PORTE DELLA MIA NUOVA DOCKINGSTATION ...   
..                                                 ...   
142  BUONGIORNO  SAREBBE POSSIBILE AVERE UN CAVO US...   
143  LA MIA DOCKING STATION FA UN FLICKERING DEGLI ...   
144  CON DOCKINGSTATION DUE MONITOR PI TASTIERA  GR...   
145  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
146  CIAO ARASH  HO SEMPRE QUEL PROBLEMA DEL RUMORE...   

                                                tokens  
0    [stndiges, flimmern, des, bildschirmes, iiyama...  
1    [nostra, rete, dobbiamo, lavorare, usando, wif...  
2    [dear, emicontrols, today, think, pad, docking...  
3    [voi, portatile, vede, monitor, avevo, staccat...  
4    [porte, mia, nuova, dockingstation, comunicano...  
..                                                 ...  
142  [cavo, usbc, lungo, poter, collegare, portatil...  
143  [mia, docking, station, flickering, degli, sch...  
144       [dockingstation, monitor, tastiera, giorgio]  
145  [473713, avevamo, aggiornato, driver, sia, tra...  
146  [arash, quel, rumore, pc, appena, scollego, da...  

[147 rows x 4 columns]

In [144]:
df_3_docking

Title  \
0                                           Bildschirm   
1                                   Verificare la rete   
2                       External Monitor not connected   
3                                 Problemi con Monitor   
4             Porte USB Dockingstation non funzionano.   
..                                                 ...   
142  Cavo USB-C per collegare portatile a docking s...   
143                                    docking station   
144         Stazione di lavoro da Christian Tschimben    
145                        Docking station no ethernet   
146      PC che fa rumore. Microfono o audio difettoso   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
142  {"11":"Hardware, Telephony, Smartphones, Monit...   
143  {"11":"Hardware, Telephony, Smartphones, Monit...   
144  {"11":"Hardware, Telephony, Smartphones, Monit...   
145  {"11":"Hardware, Telephony, Smartphones, Monit...   
146  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ...   
1    CIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBB...   
2    DEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH ...   
3    CIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MO...   
4    CIAO  LE PORTE DELLA MIA NUOVA DOCKINGSTATION ...   
..                                                 ...   
142  BUONGIORNO  SAREBBE POSSIBILE AVERE UN CAVO US...   
143  LA MIA DOCKING STATION FA UN FLICKERING DEGLI ...   
144  CON DOCKINGSTATION DUE MONITOR PI TASTIERA  GR...   
145  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
146  CIAO ARASH  HO SEMPRE QUEL PROBLEMA DEL RUMORE...   

                                                tokens  
0    [stndiges, flimmern, des, bildschirmes, iiyama...  
1    [nostra, rete, dobbiamo, lavorare, usando, wif...  
2    [dear, emicontrols, today, think, pad, docking...  
3    [voi, portatile, vede, monitor, avevo, staccat...  
4    [porte, mia, nuova, dockingstation, comunicano...  
..                                                 ...  
142  [cavo, usbc, lungo, poter, collegare, portatil...  
143  [mia, docking, station, flickering, degli, sch...  
144       [dockingstation, monitor, tastiera, giorgio]  
145  [473713, avevamo, aggiornato, driver, sia, tra...  
146  [arash, quel, rumore, pc, appena, scollego, da...  

[147 rows x 4 columns]

In [145]:
df_3_docking = df_3_docking.drop(columns = 'tokens')
df_3_docking

Title  \
0                                           Bildschirm   
1                                   Verificare la rete   
2                       External Monitor not connected   
3                                 Problemi con Monitor   
4             Porte USB Dockingstation non funzionano.   
..                                                 ...   
142  Cavo USB-C per collegare portatile a docking s...   
143                                    docking station   
144         Stazione di lavoro da Christian Tschimben    
145                        Docking station no ethernet   
146      PC che fa rumore. Microfono o audio difettoso   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
142  {"11":"Hardware, Telephony, Smartphones, Monit...   
143  {"11":"Hardware, Telephony, Smartphones, Monit...   
144  {"11":"Hardware, Telephony, Smartphones, Monit...   
145  {"11":"Hardware, Telephony, Smartphones, Monit...   
146  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ...  
1    CIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBB...  
2    DEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH ...  
3    CIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MO...  
4    CIAO  LE PORTE DELLA MIA NUOVA DOCKINGSTATION ...  
..                                                 ...  
142  BUONGIORNO  SAREBBE POSSIBILE AVERE UN CAVO US...  
143  LA MIA DOCKING STATION FA UN FLICKERING DEGLI ...  
144  CON DOCKINGSTATION DUE MONITOR PI TASTIERA  GR...  
145  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
146  CIAO ARASH  HO SEMPRE QUEL PROBLEMA DEL RUMORE...  

[147 rows x 3 columns]

# df_3_tcp

In [146]:
#df_3_tcp
import pandas as pd
words_to_check = ['tcp', 'windows']

# Initialize an empty DataFrame to store the matching rows
df_3_tcp = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_tcp = df_3_tcp.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_tcp = df_3_tcp.reset_index(drop=True)

df_3_tcp

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\589532251.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_tcp = df_3_tcp.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\589532251.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_tcp = df_3_tcp.append(df_3[word_mask])


Title  \
0                                         Stampante    
1             neuer printer einbindung nicht möglich   
2                              PC per ATASS-Schulung   
3         Stampanti non funzionanti (accesso negato)   
4  Drucker Einstellung Doppelseitig und Farbe nic...   
5                                  cambio smartphone   
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0     SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWS   
1  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
2  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
3  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
4  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
5   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   

                                              tokens  
0              [scusa, dove, farlo, update, windows]  
1  [servus, haben, unserem, bro, saviese, tach, e...  
2  [daccordo, faccio, poter, ricevere, pc, fisso,...  
3  [parte, windows, 11, resto, ora, appuntamento,...  
4  [meinem, drucker, einstellungen, festlegen, do...  
5  [furlotti, first, line, support, holding, 1959...  
6  [able, log, into, computer, username, password...  
7  [473713, avevamo, aggiornato, driver, sia, tra...  
8  [entschuldigung, aber, diese, seite, verfgbar,...

In [147]:
df_3_tcp

Title  \
0                                         Stampante    
1             neuer printer einbindung nicht möglich   
2                              PC per ATASS-Schulung   
3         Stampanti non funzionanti (accesso negato)   
4  Drucker Einstellung Doppelseitig und Farbe nic...   
5                                  cambio smartphone   
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0     SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWS   
1  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
2  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
3  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
4  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
5   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   

                                              tokens  
0              [scusa, dove, farlo, update, windows]  
1  [servus, haben, unserem, bro, saviese, tach, e...  
2  [daccordo, faccio, poter, ricevere, pc, fisso,...  
3  [parte, windows, 11, resto, ora, appuntamento,...  
4  [meinem, drucker, einstellungen, festlegen, do...  
5  [furlotti, first, line, support, holding, 1959...  
6  [able, log, into, computer, username, password...  
7  [473713, avevamo, aggiornato, driver, sia, tra...  
8  [entschuldigung, aber, diese, seite, verfgbar,...

In [148]:
df_3_tcp = df_3_tcp.drop(columns= 'tokens')
df_3_tcp

Title  \
0                                         Stampante    
1             neuer printer einbindung nicht möglich   
2                              PC per ATASS-Schulung   
3         Stampanti non funzionanti (accesso negato)   
4  Drucker Einstellung Doppelseitig und Farbe nic...   
5                                  cambio smartphone   
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0     SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWS  
1  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...  
2  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...  
3  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...  
4  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...  
5   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...  
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...  
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...

# df_3_db 

In [149]:
#df_3_db
import pandas as pd
words_to_check = ['oracle', 'mysql', 'windows', 'mariadb']

# Initialize an empty DataFrame to store the matching rows
df_3_db = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_db = df_3_db.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_db = df_3_db.reset_index(drop=True)

df_3_db

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\2774121526.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_db = df_3_db.append(df_3[word_mask])


Title  \
0                                         Stampante    
1             neuer printer einbindung nicht möglich   
2                              PC per ATASS-Schulung   
3         Stampanti non funzionanti (accesso negato)   
4  Drucker Einstellung Doppelseitig und Farbe nic...   
5                                  cambio smartphone   
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0     SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWS   
1  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
2  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
3  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
4  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
5   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   

                                              tokens  
0              [scusa, dove, farlo, update, windows]  
1  [servus, haben, unserem, bro, saviese, tach, e...  
2  [daccordo, faccio, poter, ricevere, pc, fisso,...  
3  [parte, windows, 11, resto, ora, appuntamento,...  
4  [meinem, drucker, einstellungen, festlegen, do...  
5  [furlotti, first, line, support, holding, 1959...  
6  [able, log, into, computer, username, password...  
7  [473713, avevamo, aggiornato, driver, sia, tra...  
8  [entschuldigung, aber, diese, seite, verfgbar,...

In [150]:
df_3_db

Title  \
0                                         Stampante    
1             neuer printer einbindung nicht möglich   
2                              PC per ATASS-Schulung   
3         Stampanti non funzionanti (accesso negato)   
4  Drucker Einstellung Doppelseitig und Farbe nic...   
5                                  cambio smartphone   
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  \
0     SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWS   
1  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...   
2  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...   
3  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...   
4  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...   
5   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...   
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...   
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...   
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...   

                                              tokens  
0              [scusa, dove, farlo, update, windows]  
1  [servus, haben, unserem, bro, saviese, tach, e...  
2  [daccordo, faccio, poter, ricevere, pc, fisso,...  
3  [parte, windows, 11, resto, ora, appuntamento,...  
4  [meinem, drucker, einstellungen, festlegen, do...  
5  [furlotti, first, line, support, holding, 1959...  
6  [able, log, into, computer, username, password...  
7  [473713, avevamo, aggiornato, driver, sia, tra...  
8  [entschuldigung, aber, diese, seite, verfgbar,...

In [151]:
df_3_db = df_3_db.drop(columns = 'tokens')
df_3_db

Title  \
0                                         Stampante    
1             neuer printer einbindung nicht möglich   
2                              PC per ATASS-Schulung   
3         Stampanti non funzionanti (accesso negato)   
4  Drucker Einstellung Doppelseitig und Farbe nic...   
5                                  cambio smartphone   
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   
3  {"11":"Hardware, Telephony, Smartphones, Monit...   
4  {"11":"Hardware, Telephony, Smartphones, Monit...   
5  {"11":"Hardware, Telephony, Smartphones, Monit...   
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0     SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWS  
1  SERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIES...  
2  CIAO COME DACCORDO CON FRANCESCO FACCIO IL TIC...  
3  A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN A...  
4  HALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINST...  
5   MANUEL FURLOTTI IT FIRST LINE SUPPORT TECHNOA...  
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...  
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...

# df_3_pc

In [152]:
#df_3_pc
import pandas as pd
words_to_check = ['laptop', 'pc', 'schermo', 'fisso', 'tastiera', 'monitor', 
                  'computer', 'cavo', 'pw', 'usb', 'telefono']


# Initialize an empty DataFrame to store the matching rows
df_3_pc = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_pc = df_3_pc.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_pc = df_3_pc.reset_index(drop=True)

df_3_pc

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\3327546749.py:16: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_pc = df_3_pc.append(df_3[word_mask])
C:\Users\Mat

Title  \
0                               HP Zbook for Gabriela    
1               Laptop per fiera Aquanale per technica   
2               Richiesta Urgente: Laptop per la fiera   
3                                Laptop per foramzione   
4                           drucken funktioniert nicht   
..                                                 ...   
354                                 Telefono portatile   
355  Telefono interno per Alexander Ganthaler/Trist...   
356                  Nuovo telefono montatori svizzera   
357                                Cambio nome sul 537   
358                          Suono - Pro Call - cuffie   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
354  {"11":"Hardware, Telephony, Smartphones, Monit...   
355  {"11":"Hardware, Telephony, Smartphones, Monit...   
356  {"11":"Hardware, Telephony, Smartphones, Monit...   
357  {"11":"Hardware, Telephony, Smartphones, Monit...   
358  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASE...   
1    CIAO PER LA FIERA AQUANALE CI SERVE UN LAPTOP ...   
2    CIAO  CI SERVE UN LAPTOP PER LA FIERA PER COLL...   
3    CIAO MANUEL  COME CONCORDATO APPENA AL TELEFON...   
4    DRUCKER SIND AM NEUEN LAPTOP NICHT RICHTIG INS...   
..                                                 ...   
354  MICHELE DELLA VECCHIA PREGO PREPARARE UN TELEF...   
355  CIAO MI SERVIREBBE UN TELEFONO INTERNO CON UN ...   
356  CI SERVE UN TELEFONO DI SOSTITUZIONE PER UNO P...   
357  CIAO  QUANDO CHIAMO DAL MIO TELEFONO CON IL 53...   
358  CIAO ARASHDEEP PURTROPPO CON IL NR 832 LA CHIA...   

                                                tokens  
0    [arashdeep, hereby, answer, alexa, email, inqu...  
1    [fiera, aquanale, laptop, technica, econsow, p...  
2    [laptop, fiera, collegarlo, touch, screen, pot...  
3    [concordato, appena, telefono, nostri, 4, lapt...  
4    [drucker, sind, laptop, richtig, installiert, ...  
..                                                 ...  
354  [michele, vecchia, preparare, telefono, portat...  
355  [servirebbe, telefono, interno, tra, 500, 699,...  
356  [telefono, sostituzione, pixner, markus, monta...  
357  [chiamo, telefono, 537, altir, vedono, arno, h...  
358  [arashdeep, nr, 832, chiamata, viene, deviata,...  

[359 rows x 4 columns]

In [153]:
df_3_pc

Title  \
0                               HP Zbook for Gabriela    
1               Laptop per fiera Aquanale per technica   
2               Richiesta Urgente: Laptop per la fiera   
3                                Laptop per foramzione   
4                           drucken funktioniert nicht   
..                                                 ...   
354                                 Telefono portatile   
355  Telefono interno per Alexander Ganthaler/Trist...   
356                  Nuovo telefono montatori svizzera   
357                                Cambio nome sul 537   
358                          Suono - Pro Call - cuffie   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
354  {"11":"Hardware, Telephony, Smartphones, Monit...   
355  {"11":"Hardware, Telephony, Smartphones, Monit...   
356  {"11":"Hardware, Telephony, Smartphones, Monit...   
357  {"11":"Hardware, Telephony, Smartphones, Monit...   
358  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  \
0    HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASE...   
1    CIAO PER LA FIERA AQUANALE CI SERVE UN LAPTOP ...   
2    CIAO  CI SERVE UN LAPTOP PER LA FIERA PER COLL...   
3    CIAO MANUEL  COME CONCORDATO APPENA AL TELEFON...   
4    DRUCKER SIND AM NEUEN LAPTOP NICHT RICHTIG INS...   
..                                                 ...   
354  MICHELE DELLA VECCHIA PREGO PREPARARE UN TELEF...   
355  CIAO MI SERVIREBBE UN TELEFONO INTERNO CON UN ...   
356  CI SERVE UN TELEFONO DI SOSTITUZIONE PER UNO P...   
357  CIAO  QUANDO CHIAMO DAL MIO TELEFONO CON IL 53...   
358  CIAO ARASHDEEP PURTROPPO CON IL NR 832 LA CHIA...   

                                                tokens  
0    [arashdeep, hereby, answer, alexa, email, inqu...  
1    [fiera, aquanale, laptop, technica, econsow, p...  
2    [laptop, fiera, collegarlo, touch, screen, pot...  
3    [concordato, appena, telefono, nostri, 4, lapt...  
4    [drucker, sind, laptop, richtig, installiert, ...  
..                                                 ...  
354  [michele, vecchia, preparare, telefono, portat...  
355  [servirebbe, telefono, interno, tra, 500, 699,...  
356  [telefono, sostituzione, pixner, markus, monta...  
357  [chiamo, telefono, 537, altir, vedono, arno, h...  
358  [arashdeep, nr, 832, chiamata, viene, deviata,...  

[359 rows x 4 columns]

In [154]:
df_3_pc = df_3_pc.drop(columns = 'tokens')
df_3_pc

Title  \
0                               HP Zbook for Gabriela    
1               Laptop per fiera Aquanale per technica   
2               Richiesta Urgente: Laptop per la fiera   
3                                Laptop per foramzione   
4                           drucken funktioniert nicht   
..                                                 ...   
354                                 Telefono portatile   
355  Telefono interno per Alexander Ganthaler/Trist...   
356                  Nuovo telefono montatori svizzera   
357                                Cambio nome sul 537   
358                          Suono - Pro Call - cuffie   

                                                 Topic  \
0    {"11":"Hardware, Telephony, Smartphones, Monit...   
1    {"11":"Hardware, Telephony, Smartphones, Monit...   
2    {"11":"Hardware, Telephony, Smartphones, Monit...   
3    {"11":"Hardware, Telephony, Smartphones, Monit...   
4    {"11":"Hardware, Telephony, Smartphones, Monit...   
..                                                 ...   
354  {"11":"Hardware, Telephony, Smartphones, Monit...   
355  {"11":"Hardware, Telephony, Smartphones, Monit...   
356  {"11":"Hardware, Telephony, Smartphones, Monit...   
357  {"11":"Hardware, Telephony, Smartphones, Monit...   
358  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
0    HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASE...  
1    CIAO PER LA FIERA AQUANALE CI SERVE UN LAPTOP ...  
2    CIAO  CI SERVE UN LAPTOP PER LA FIERA PER COLL...  
3    CIAO MANUEL  COME CONCORDATO APPENA AL TELEFON...  
4    DRUCKER SIND AM NEUEN LAPTOP NICHT RICHTIG INS...  
..                                                 ...  
354  MICHELE DELLA VECCHIA PREGO PREPARARE UN TELEF...  
355  CIAO MI SERVIREBBE UN TELEFONO INTERNO CON UN ...  
356  CI SERVE UN TELEFONO DI SOSTITUZIONE PER UNO P...  
357  CIAO  QUANDO CHIAMO DAL MIO TELEFONO CON IL 53...  
358  CIAO ARASHDEEP PURTROPPO CON IL NR 832 LA CHIA...  

[359 rows x 3 columns]

# df_3_vulnerabilities

In [155]:
#df_3_vulnerabilities
import pandas as pd
words_to_check = ['vulnerabilities']

# Initialize an empty DataFrame to store the matching rows
df_3_vulnerabilities = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_vulnerabilities = df_3_vulnerabilities.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_vulnerabilities = df_3_vulnerabilities.reset_index(drop=True)
df_3_vulnerabilities= df_3_vulnerabilities.drop(columns = 'tokens')
df_3_vulnerabilities

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\155574697.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_vulnerabilities = df_3_vulnerabilities.append(df_3[word_mask])


Empty DataFrame
Columns: [Title, Topic, Text]
Index: []

In [156]:
df_3_vulnerabilities

Empty DataFrame
Columns: [Title, Topic, Text]
Index: []

# df_3_email

In [157]:
#df_3_email
import pandas as pd
words_to_check = ['mail']

# Initialize an empty DataFrame to store the matching rows
df_3_email = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_email = df_3_email.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_email = df_3_email.reset_index(drop=True)
df_3_email= df_3_email.drop(columns = 'tokens')
df_3_email

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\750117258.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_email = df_3_email.append(df_3[word_mask])


Title  \
0                  Computerprobleme Robert Kramberger   
1                              HP Zbook for Gabriela    
2                                     Nuovo Portatile   
3                                    new printer user   
4                                    Scannen an Email   
5             Drucker sendet Scan nicht an die E-Mail   
6                              Scanner neu einrichten   
7   Configurazione Microsoft Exchange ActiveSync c...   
8                                   Telefono dual sim   
9                                             scanner   
10                               Connessione - server   
11                                  Numero telefonico   
12                                       Nr telefono    
13                            Info for ticket 582224    
14                                    Screen blackout   
15                        Toner stampante ACS 1247109   
16                        Cellulare e ProCall a Laura   
17                                     Neues ThinkPad   
18                                         Smartphone   
19                                         Smartphone   
20                        e-mail salvata su stampante   
21                                    Nuova Stampante   
22         scansione collegata alla mail non funziona   
23        Mobile email access / technician Aldo Lauri   
24                               Outlook su cellulare   
25                 Cellulare perso Roessler Christian   
26                          mails in entrata bloccati   
27                                  cambio smartphone   
28                  ADD email to Printer for scanning   
29                               App Concur Cellulare   
30             E-mail Adresse e PC per Bruno Campaner   
31              WG: Fernzugriff Visualisierungsserver   
32                                      Problemi ENGO   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   
27  {"11":"Hardware, Telephony, Smartphones, Monit...   
28  {"11":"Hardware, Telephony, Smartphones, Monit...   
29  {"11":"Hardware, Telephony, Smartphones, Monit...   
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   
32  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
0    LIEBE KOLLEGINNEN UND KOLLEGEN   BEI MEINEM C...  
1   HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASE...  
2 

In [158]:
df_3_email

Title  \
0                  Computerprobleme Robert Kramberger   
1                              HP Zbook for Gabriela    
2                                     Nuovo Portatile   
3                                    new printer user   
4                                    Scannen an Email   
5             Drucker sendet Scan nicht an die E-Mail   
6                              Scanner neu einrichten   
7   Configurazione Microsoft Exchange ActiveSync c...   
8                                   Telefono dual sim   
9                                             scanner   
10                               Connessione - server   
11                                  Numero telefonico   
12                                       Nr telefono    
13                            Info for ticket 582224    
14                                    Screen blackout   
15                        Toner stampante ACS 1247109   
16                        Cellulare e ProCall a Laura   
17                                     Neues ThinkPad   
18                                         Smartphone   
19                                         Smartphone   
20                        e-mail salvata su stampante   
21                                    Nuova Stampante   
22         scansione collegata alla mail non funziona   
23        Mobile email access / technician Aldo Lauri   
24                               Outlook su cellulare   
25                 Cellulare perso Roessler Christian   
26                          mails in entrata bloccati   
27                                  cambio smartphone   
28                  ADD email to Printer for scanning   
29                               App Concur Cellulare   
30             E-mail Adresse e PC per Bruno Campaner   
31              WG: Fernzugriff Visualisierungsserver   
32                                      Problemi ENGO   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   
27  {"11":"Hardware, Telephony, Smartphones, Monit...   
28  {"11":"Hardware, Telephony, Smartphones, Monit...   
29  {"11":"Hardware, Telephony, Smartphones, Monit...   
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   
32  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
0    LIEBE KOLLEGINNEN UND KOLLEGEN   BEI MEINEM C...  
1   HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASE...  
2 

# Further refinement

## look for df_3_email access

In [159]:
import pandas as pd
import re

In [160]:
related_words = ['access', 'accessing', 'accessible', 'accessed', 'accesses', 'entry', 
                 'approach', 'admission', 'entrance', 'reach', 'open', 'connect', 
                 'visit', 'retrieve', 'use','Zugang', 'Zugriff', 'zugänglich',
                 'zugriffen', 'Zugänge', 'Eingang', 'Herangehensweise', 'Zulassung',
                 'Eingang', 'erreichen', 'öffnen', 'verbinden', 'besuchen', 'abrufen', 'benutzen',
                 'accesso', 'accesso', 'accessibile', 'accesso', 'accessi', 
                 'entrata', 'approccio', 'ammissione', 'ingresso', 'raggiungere', 
                 'aprire', 'collegare', 'visitare', 'recuperare', 'usare']

In [161]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_3_email = df_3_email[df_3_email['Text'].str.contains(pattern, case=False)]
filtered_df_3_email = filtered_df_3_email.reset_index(drop=True)

filtered_df_3_email

Title  \
0  Mobile email access / technician Aldo Lauri   
1                    mails in entrata bloccati   
2        WG: Fernzugriff Visualisierungsserver   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  I AM WRITING TO YOU IN THE NAME OF MY COLLEAGU...  
1  MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICE...  
2   HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   ...

In [162]:
filtered_df_3_email

Title  \
0  Mobile email access / technician Aldo Lauri   
1                    mails in entrata bloccati   
2        WG: Fernzugriff Visualisierungsserver   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  I AM WRITING TO YOU IN THE NAME OF MY COLLEAGU...  
1  MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICE...  
2   HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   ...

In [163]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_3_email[i:i+n] for i in range(0,len(filtered_df_3_email),n)]
    #print(list_df)

In [164]:
len(list_df)

1

In [165]:
list_df[0]


Title  \
0  Mobile email access / technician Aldo Lauri   
1                    mails in entrata bloccati   
2        WG: Fernzugriff Visualisierungsserver   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   
1  {"11":"Hardware, Telephony, Smartphones, Monit...   
2  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  I AM WRITING TO YOU IN THE NAME OF MY COLLEAGU...  
1  MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICE...  
2   HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   ...

In [166]:
def put_together():
    list1=[]
    for index in range(0,1):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


summ_block = put_together()
summ_block

Result 0:
I AM WRITING TO YOU IN THE NAME OF MY COLLEAGUE ALDO LAURI WHOS CURRENTLY OUT IN A CUSTOMERS PUMPSTATION SINCE HE CHANGED HIS GENERAL LOGIN PASSWORD HE IS NOT ABLE TO HAVE PROPER EMAIL ACCESS ON HIS MOBILE NO 41 79 347 86 95 SINCE HE IS ALSO NOT ABLE TO CREATE A IT TICKET ANYMORE I AM DOING IT ON HIS BEHALF KINDLY ASKING YOU TO GET IN TOUCH WITH HIM TO SOLVE THIS PROBLEM MANY THANKS FOR YOUR HELP AND SUPPORT CHEERS PASCALMAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   BESTE GRSSE MARCO   MARCO ALBIEZ SERVICE LEITER TECHNOALPIN SCHWEIZ AG  CH  6467  SCHATTDORF  ROSSGIESSENSTRASSE 1 T 41 418745 000  M 41 78 845 28 32  WWWTECHNOALPINCOM           VON DARIO CASU  GESENDET DIENSTAG 25 APRIL 2023 1516 AN MARCO ALBIEZ  BETREFF FERNZUGRIFF VISUALISIERUNGSSERVER     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPE

['I AM WRITING TO YOU IN THE NAME OF MY COLLEAGUE ALDO LAURI WHOS CURRENTLY OUT IN A CUSTOMERS PUMPSTATION SINCE HE CHANGED HIS GENERAL LOGIN PASSWORD HE IS NOT ABLE TO HAVE PROPER EMAIL ACCESS ON HIS MOBILE NO 41 79 347 86 95 SINCE HE IS ALSO NOT ABLE TO CREATE A IT TICKET ANYMORE I AM DOING IT ON HIS BEHALF KINDLY ASKING YOU TO GET IN TOUCH WITH HIM TO SOLVE THIS PROBLEM MANY THANKS FOR YOUR HELP AND SUPPORT CHEERS PASCALMAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY HALLO \xa0 WER KANN HIER DEN ZUGANG ERSTELLEN \xa0 BESTE GRSSE MARCO \xa0 MARCO ALBIEZ SERVICE LEITER TECHNOALPIN SCHWEIZ AG  CH  6467  SCHATTDORF  ROSSGIESSENSTRASSE 1 T 41 418745 000  M 41 78 845 28 32  WWWTECHNOALPINCOM           VON DARIO CASU  GESENDET DIENSTAG 25 APRIL 2023 1516 AN MARCO ALBIEZ  BETREFF FERNZUGRIFF VISUALISIERUNGSSERVER   \xa0 CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR

In [167]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 1):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [168]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
I AM WRITING TO YOU IN THE NAME OF MY COLLEAGUE ALDO LAURI WHOS CURRENTLY OUT IN A CUSTOMERS PUMPSTATION SINCE HE CHANGED HIS GENERAL LOGIN PASSWORD HE IS NOT ABLE TO HAVE PROPER EMAIL ACCESS ON HIS MOBILE NO 41 79 347 86 95 SINCE HE IS ALSO NOT ABLE TO CREATE A IT TICKET ANYMORE I AM DOING IT ON HIS BEHALF KINDLY ASKING YOU TO GET IN TOUCH WITH HIM TO SOLVE THIS PROBLEM MANY THANKS FOR YOUR HELP AND SUPPORT CHEERS PASCALMAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   BESTE GRSSE MARCO   MARCO ALBIEZ SERVICE LEITER TECHNOALPIN SCHWEIZ AG  CH  6467  SCHATTDORF  ROSSGIESSENSTRASSE 1 T 41 418745 000  M 41 78 845 28 32  WWWTECHNOALPINCOM           VON DARIO CASU  GESENDET DIENSTAG 25 APRIL 2023 1516 AN MARCO ALBIEZ  BETREFF FERNZUGRIFF VISUALISIERUNGSSERVER     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPE

In [169]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
I AM WRITING TO YOU IN THE NAME OF MY COLLEAGUE ALDO LAURI WHOS CURRENTLY OUT IN A CUSTOMERS PUMPSTATION SINCE HE CHANGED HIS GENERAL LOGIN PASSWORD HE IS NOT ABLE TO HAVE PROPER EMAIL ACCESS ON HIS MOBILE NO 41 79 347 86 95 SINCE HE IS ALSO NOT ABLE TO CREATE A IT TICKET ANYMORE I AM DOING IT ON HIS BEHALF KINDLY ASKING YOU TO GET IN TOUCH WITH HIM TO SOLVE THIS PROBLEM MANY THANKS FOR YOUR HELP AND SUPPORT CHEERS PASCALMAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   BESTE GRSSE MARCO   MARCO ALBIEZ SERVICE LEITER TECHNOALPIN SCHWEIZ AG  CH  6467  SCHATTDORF  ROSSGIESSENSTRASSE 1 T 41 418745 000  M 41 78 845 28 32  WWWTECHNOALPINCOM           VON DARIO CASU  GESENDET DIENSTAG 25 APRIL 2023 1516 AN MARCO ALBIEZ  BETREFF FERNZUGRIFF VISUALISIERUNGSSERVER     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPE

['I AM WRITING TO YOU IN THE NAME OF MY COLLEAGUE ALDO LAURI WHOS CURRENTLY OUT IN A CUSTOMERS PUMPSTATION SINCE HE CHANGED HIS GENERAL LOGIN PASSWORD HE IS NOT ABLE TO HAVE PROPER EMAIL ACCESS ON HIS MOBILE NO 41 79 347 86 95 SINCE HE IS ALSO NOT ABLE TO CREATE A IT TICKET ANYMORE I AM DOING IT ON HIS BEHALF KINDLY ASKING YOU TO GET IN TOUCH WITH HIM TO SOLVE THIS PROBLEM MANY THANKS FOR YOUR HELP AND SUPPORT CHEERS PASCALMAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY HALLO \xa0 WER KANN HIER DEN ZUGANG ERSTELLEN \xa0 BESTE GRSSE MARCO \xa0 MARCO ALBIEZ SERVICE LEITER TECHNOALPIN SCHWEIZ AG  CH  6467  SCHATTDORF  ROSSGIESSENSTRASSE 1 T 41 418745 000  M 41 78 845 28 32  WWWTECHNOALPINCOM           VON DARIO CASU  GESENDET DIENSTAG 25 APRIL 2023 1516 AN MARCO ALBIEZ  BETREFF FERNZUGRIFF VISUALISIERUNGSSERVER   \xa0 CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR

# df_3_email_signature

In [170]:
import pandas as pd
import re

In [171]:
related_words = [
    'Firma', 'Autografo', 'Sottoscrizione', 'Segno distintivo', 'Sigla', 'Marcatura',
    'Ratifica', 'Apposizione di firma', 'Sigillo', 'Atto autografo',
    'Signature', 'Autograph', 'Mark', 'Seal', 'Sign-off',
    'Inked mark', 'Signatory', 'Handwriting', 'Personal mark',
    'Unterschrift', 'Autogramm', 'Kennzeichen', 'Siegel', 'Namenszug', 'Paraphe',
    'Besiegelung', 'Unterzeichnung', 'Handschrift', 'Eigenhändige Unterschrift'
]

In [172]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_3_email_signature = df_3_email[df_3_email['Text'].str.contains(pattern, case=False)]
filtered_df_3_email_signature = filtered_df_3_email_signature.reset_index(drop=True)

filtered_df_3_email_signature

Empty DataFrame
Columns: [Title, Topic, Text]
Index: []

In [173]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_3_email_signature[i:i+n] for i in range(0,len(filtered_df_3_email_signature),n)]
    #print(list_df)

In [174]:
len(list_df)

0

# df_3_email_phishing

In [175]:
import pandas as pd
import re

In [176]:
related_words = ['Phishing', 'Pesca fraudolenta', 'Inganno online', 'Truffa informatica', 'Frode via email',
    'Phishing', 'Online scam', 'Email fraud', 'Deceptive online tactics', 'Cyber deception',
    'Phishing', 'Online-Betrug', 'Internet-Täuschung', 'E-Mail-Betrug', 'Cyber-Betrug',
    'Inganno informatico', 'Pesca di informazioni', 'Truffa digitale',
    'Digital deception', 'Information harvesting', 'Online fraud',
    'Digitale Täuschung', 'Informationsdiebstahl', 'Online-Betrug','Spam', 'Posta indesiderata', 
    'Messaggi non richiesti', 'Posta spazzatura', 'Invio massivo di email',
    'Spam', 'Unsolicited email', 'Junk mail', 'Email overload', 'Bulk messaging',
    'Spam', 'Unerwünschte E-Mails', 'Junk-Mail', 'E-Mail-Überflutung', 'Massenversand von Nachrichten',
    'Posta non desiderata', 'Messaggi di spam', 'Comunicazioni indesiderate',
    'Unwanted mail', 'Spam messages', 'Unsolicited communications',
    'Unerwünschte Post', 'Spam-Nachrichten', 'Ungebetene Kommunikation']

In [177]:
pattern = r'\b(?:' + '|'.join(related_words) + r')\b'

# Filter the DataFrame to keep only rows containing the related words
filtered_df_3_email_phishing = df_3_email[df_3_email['Text'].str.contains(pattern, case=False)]
filtered_df_3_email_phishing = filtered_df_3_email_phishing.reset_index(drop=True)

filtered_df_3_email_phishing

Title  \
0  mails in entrata bloccati   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICE...

In [178]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [filtered_df_3_email_phishing[i:i+n] for i in range(0,len(filtered_df_3_email_phishing),n)]

In [179]:
len(list_df)

1

In [180]:
list_df[0]

Title  \
0  mails in entrata bloccati   

                                               Topic  \
0  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
0  MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICE...

In [181]:
def put_together():
    list1=[]
    for index in range(0,1):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


summ_block = put_together()
summ_block

Result 0:
MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY



['MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY']

In [182]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 1):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [183]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY



In [184]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY



['MAILS IN ENTRATA VENGONO BLOCCATI NON GLI RICEVO NEANCHE NEL SPAM PREGO VERIFICARE  DPAPADOPOULOSGPAPADOPOULOSCOMCY GPAPADOPOULOSGPAPADOPOULOSCOMCY']

# df_3_software

In [185]:
#df_3_software
import pandas as pd
words_to_check = ['software', 'server']

# Initialize an empty DataFrame to store the matching rows
df_3_software = pd.DataFrame(columns=df_3.columns)

# Iterate through the words to check
for word in words_to_check:
    # Create a boolean mask for the current word
    word_mask = df_3['Text'].str.contains(word, case=False)
    
    # Append rows containing the current word to the new DataFrame
    df_3_software = df_3_software.append(df_3[word_mask])

# Reset the index of the new DataFrame
df_3_software = df_3_software.reset_index(drop=True)
df_3_software= df_3_software.drop(columns = 'tokens')
df_3_software

C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\916185259.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_software = df_3_software.append(df_3[word_mask])
C:\Users\MattiaA\AppData\Local\Temp\ipykernel_16656\916185259.py:14: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df_3_software = df_3_software.append(df_3[word_mask])


Title  \
0                                    PC running slow.   
1             Monitor non si collega con il portatile   
2                                    Modula Scaffale    
3                                    Modula Scaffale    
4   Neues Notebook SPS-Programmierer TAEE Peter Št...   
5                                     Sostituzione PC   
6                      PC   C 238  startet nicht mehr   
7                                         PC Showroom   
8                                      Scanner defekt   
9                                      Scanner defekt   
10                                     Vecchio Laptop   
11                               Laptop LCU TestBench   
12                               Laptop LCU TestBench   
13                               Support per altro PC   
14                   2 old laptops for emergency duty   
15   Two old Laptops for Data Tracking/ Measurements    
16                  laptop for Test Bench lance pipes   
17              Panasonic Telephone has no connection   
18                                   Modula Scaffale    
19                Kein Zugriff auf Server für Telefon   
20                                             IP KNX   
21                            Nuovi Uffici Epowertrac   
22              WG: Fernzugriff Visualisierungsserver   
23  für die elektronische Übermittlung statistisch...   
24                                         Server MFD   
25                                         Server MFD   
26                                         Server MFD   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
0   MY PC HAS BEEN RUNNING VERY SLOW FOR THE PAST ...  
1   CIAO STAMATTINA NON RIESCO A COLLEGARMI COL MO...  
2   SALVE SE POSSIBILE CHIEDEREI CHE FRANCESCO O M...  
3   PER ME VA BENE PER DOMANI VIENE CONCLUSO LA CO...  
4     WIE VON HANNES SIMONINI ANGEFORDERT BESTELLE...  
5   BUONGIORNO CHIEDO GENTILMENTE LA SOSTITUZIONE ...  
6   NAVISION TEAMVIEWER DIE WEETECH SOFTWARE MSSEN...  
7   CIAOPOTRESTE PER FAVORE METTERE A DISPOSIZIONE...  
8   GLI SCANNER CON LA STAZIONE DI FRANZ SONO TUTT...  
9   GLI SCANNER CON LA STAZIONE DI FRANZ SONO TUTT...  
10  CIAO  VI SCRIVO QUESTO TICKET PER INFORMARVI C...  
11  CIAO WE ONLY NEED A DISTANT ACCES FOR SOFTWARE...  
12  CIAO ARASHDEEP NO I ONLY NEED A DISTANT ACCES ...  
13  NON MI FACEVA VEDERE I DRIVER PROBABILMENTE NO...  
14  2 VECCHI X

In [186]:
df_3_software

Title  \
0                                    PC running slow.   
1             Monitor non si collega con il portatile   
2                                    Modula Scaffale    
3                                    Modula Scaffale    
4   Neues Notebook SPS-Programmierer TAEE Peter Št...   
5                                     Sostituzione PC   
6                      PC   C 238  startet nicht mehr   
7                                         PC Showroom   
8                                      Scanner defekt   
9                                      Scanner defekt   
10                                     Vecchio Laptop   
11                               Laptop LCU TestBench   
12                               Laptop LCU TestBench   
13                               Support per altro PC   
14                   2 old laptops for emergency duty   
15   Two old Laptops for Data Tracking/ Measurements    
16                  laptop for Test Bench lance pipes   
17              Panasonic Telephone has no connection   
18                                   Modula Scaffale    
19                Kein Zugriff auf Server für Telefon   
20                                             IP KNX   
21                            Nuovi Uffici Epowertrac   
22              WG: Fernzugriff Visualisierungsserver   
23  für die elektronische Übermittlung statistisch...   
24                                         Server MFD   
25                                         Server MFD   
26                                         Server MFD   

                                                Topic  \
0   {"11":"Hardware, Telephony, Smartphones, Monit...   
1   {"11":"Hardware, Telephony, Smartphones, Monit...   
2   {"11":"Hardware, Telephony, Smartphones, Monit...   
3   {"11":"Hardware, Telephony, Smartphones, Monit...   
4   {"11":"Hardware, Telephony, Smartphones, Monit...   
5   {"11":"Hardware, Telephony, Smartphones, Monit...   
6   {"11":"Hardware, Telephony, Smartphones, Monit...   
7   {"11":"Hardware, Telephony, Smartphones, Monit...   
8   {"11":"Hardware, Telephony, Smartphones, Monit...   
9   {"11":"Hardware, Telephony, Smartphones, Monit...   
10  {"11":"Hardware, Telephony, Smartphones, Monit...   
11  {"11":"Hardware, Telephony, Smartphones, Monit...   
12  {"11":"Hardware, Telephony, Smartphones, Monit...   
13  {"11":"Hardware, Telephony, Smartphones, Monit...   
14  {"11":"Hardware, Telephony, Smartphones, Monit...   
15  {"11":"Hardware, Telephony, Smartphones, Monit...   
16  {"11":"Hardware, Telephony, Smartphones, Monit...   
17  {"11":"Hardware, Telephony, Smartphones, Monit...   
18  {"11":"Hardware, Telephony, Smartphones, Monit...   
19  {"11":"Hardware, Telephony, Smartphones, Monit...   
20  {"11":"Hardware, Telephony, Smartphones, Monit...   
21  {"11":"Hardware, Telephony, Smartphones, Monit...   
22  {"11":"Hardware, Telephony, Smartphones, Monit...   
23  {"11":"Hardware, Telephony, Smartphones, Monit...   
24  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
0   MY PC HAS BEEN RUNNING VERY SLOW FOR THE PAST ...  
1   CIAO STAMATTINA NON RIESCO A COLLEGARMI COL MO...  
2   SALVE SE POSSIBILE CHIEDEREI CHE FRANCESCO O M...  
3   PER ME VA BENE PER DOMANI VIENE CONCLUSO LA CO...  
4     WIE VON HANNES SIMONINI ANGEFORDERT BESTELLE...  
5   BUONGIORNO CHIEDO GENTILMENTE LA SOSTITUZIONE ...  
6   NAVISION TEAMVIEWER DIE WEETECH SOFTWARE MSSEN...  
7   CIAOPOTRESTE PER FAVORE METTERE A DISPOSIZIONE...  
8   GLI SCANNER CON LA STAZIONE DI FRANZ SONO TUTT...  
9   GLI SCANNER CON LA STAZIONE DI FRANZ SONO TUTT...  
10  CIAO  VI SCRIVO QUESTO TICKET PER INFORMARVI C...  
11  CIAO WE ONLY NEED A DISTANT ACCES FOR SOFTWARE...  
12  CIAO ARASHDEEP NO I ONLY NEED A DISTANT ACCES ...  
13  NON MI FACEVA VEDERE I DRIVER PROBABILMENTE NO...  
14  2 VECCHI X

# SUMMARIZATION

# Creation of blocks 

## df_1_email

In [187]:
pip install --upgrade requests


Note: you may need to restart the kernel to use updated packages.


In [188]:
pip install transformers


Note: you may need to restart the kernel to use updated packages.


In [189]:
#specify number of rows in each chunk
n=2
#split DataFrame into chunks
list_df = [df_1_email[i:i+n] for i in range(0,len(df_1_email),n)]
    #print(list_df)

In [190]:
len(list_df)

281

In [191]:
list_df[274]

Title                                              Topic  \
548  Licenze CRM  {"16":"User identity management, Permissions, ...   
549  Licenze CRM  {"16":"User identity management, Permissions, ...   

                                                  Text  
548  CIAOPOSSIAMO PER FAVORE ASSEGNARE UNA LICENZA ...  
549  CIAOPOTETE PER FAVORE ASSEGNARE LA LICENZA DI ...

In [192]:
def put_together():
    list1=[]
    for index in range(0,274):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [193]:
summ_block = put_together()
summ_block

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

[' POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN\xa0 KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO \xa0 RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY\xa0

In [194]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 274):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [195]:
blocks_to_skip = [4,5,47,110,140,168,169,173,174,176,195,204,234,241,242,244,248,250]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

In [196]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

[' POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN\xa0 KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO \xa0 RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY\xa0

In [197]:
!pip install torch
!pip install transformers

In [198]:
import pickle

# df_1_rights

In [199]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_1_rights[i:i+n] for i in range(0,len(df_1_rights),n)]
    #print(list_df)

In [200]:
len(list_df)

67

In [201]:
list_df[62]

Title  \
372  PREISLISTE DIGITAL => Olivier Chapelle hinzufügen   
373                      Epowertrac - ingresso piano I   
374          Accesso, lettura e modifica cartella su G   
375                     new Entries - Johannes & Mario   
376                                           server Z   
377                                  Mattia Riccadonna   

                                                 Topic  \
372  {"16":"User identity management, Permissions, ...   
373  {"16":"User identity management, Permissions, ...   
374  {"16":"User identity management, Permissions, ...   
375  {"16":"User identity management, Permissions, ...   
376  {"16":"User identity management, Permissions, ...   
377  {"16":"User identity management, Permissions, ...   

                                                  Text  
372  BITTE BENUTZER HINZUFGENSAMACCOUNTNAME OLIVIER...  
373  CIAO LA PORTA AL I PIANO IN AGOSTINI DI ACCESS...  
374  CIAO CHIEDO CHE SIA DATO IL PERMESSO A MARTIN ...  
375  CIAO VI PREGO DI FARE 2 ACCOUNT PER I NUOVI CO...  
376  HO BISOGNO DELLACCESSO AL SERVER Z SU QUESTA C...  
377  CIAO PER IL SUO BADGE NR 1045 PREGO ABBILITARE...

In [202]:
def put_together():
    list1=[]
    for index in range(0,62):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [203]:
summ_block = put_together()
summ_block

Result 0:
HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE STEPHAN PSENNER BESTEN GRU UND DANKE MARKUSCIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENSA PER PAGARE NON RIESCE AD APRIRE LE PORTE GRAZIECIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN VIA SIEMENS PER UN TRAINING CON UN CLIENTE E VOLEVO SAPERE SE POSSO UTILIZZARE IL MIO BADGE PER ACCEDERE IL PARCHEGGIO  UFFICIO NEL CASO SAREBBE POSSIBILE DI RICEVERE I DIRITTI DATO IL FATTO CHE SAR L PI SPESSO GRAZIE E SALUTI DARIUSATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PRODUZIONE CON IL BADGE PER FAVORE SBLOCCATE LACCESSO ALLA SEDE CENTRALE PER MECIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE IN PRODUZIONE COME GLI ALTRI SLOVACCHI SALUTI HANNESCIAO ALEKSANDRA JANKOVIC FUORI DAGLI ORARI 700  1800 NON RIESCE AD APRIRE LE PORTE NEL U1 PIANO SOTTERANEO SE ARRIVA CON UNA MACHINA POOL CHE HA LACCESSO NEL GARAGE NON RIESCE PI AD USCIRE POSSIAMO VEDERE IL PROFILO DEL BADGE ASSIEME GRAZIE

Result 1:
BADGE NR 988CIAO IN FUTURO UTILIZZIAMO IL BADGE 969 P

['HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE STEPHAN PSENNER BESTEN GRU UND DANKE MARKUSCIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENSA PER PAGARE NON RIESCE AD APRIRE LE PORTE GRAZIECIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN VIA SIEMENS PER UN TRAINING CON UN CLIENTE\xa0E VOLEVO SAPERE SE POSSO UTILIZZARE IL MIO BADGE PER ACCEDERE IL PARCHEGGIO  UFFICIO NEL CASO SAREBBE POSSIBILE DI RICEVERE I DIRITTI DATO IL FATTO CHE\xa0SAR L PI SPESSO GRAZIE E SALUTI DARIUSATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PRODUZIONE CON IL BADGE PER FAVORE SBLOCCATE LACCESSO ALLA SEDE CENTRALE PER MECIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE IN PRODUZIONE COME GLI ALTRI SLOVACCHI SALUTI HANNESCIAO ALEKSANDRA JANKOVIC FUORI DAGLI ORARI 700  1800 NON RIESCE AD APRIRE LE PORTE NEL U1 PIANO SOTTERANEO SE ARRIVA CON UNA MACHINA POOL CHE HA LACCESSO NEL GARAGE NON RIESCE PI AD USCIRE POSSIAMO VEDERE IL PROFILO DEL BADGE ASSIEME GRAZIE',
 'BADGE NR 988CIAO IN FUTURO UTILIZZIAMO IL BADGE 969 PER PAGARE

In [204]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 62):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [205]:
blocks_to_skip = [12,16,39,43,51,58,61]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE STEPHAN PSENNER BESTEN GRU UND DANKE MARKUSCIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENSA PER PAGARE NON RIESCE AD APRIRE LE PORTE GRAZIECIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN VIA SIEMENS PER UN TRAINING CON UN CLIENTE E VOLEVO SAPERE SE POSSO UTILIZZARE IL MIO BADGE PER ACCEDERE IL PARCHEGGIO  UFFICIO NEL CASO SAREBBE POSSIBILE DI RICEVERE I DIRITTI DATO IL FATTO CHE SAR L PI SPESSO GRAZIE E SALUTI DARIUSATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PRODUZIONE CON IL BADGE PER FAVORE SBLOCCATE LACCESSO ALLA SEDE CENTRALE PER MECIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE IN PRODUZIONE COME GLI ALTRI SLOVACCHI SALUTI HANNESCIAO ALEKSANDRA JANKOVIC FUORI DAGLI ORARI 700  1800 NON RIESCE AD APRIRE LE PORTE NEL U1 PIANO SOTTERANEO SE ARRIVA CON UNA MACHINA POOL CHE HA LACCESSO NEL GARAGE NON RIESCE PI AD USCIRE POSSIAMO VEDERE IL PROFILO DEL BADGE ASSIEME GRAZIE

Result 1:
BADGE NR 988CIAO IN FUTURO UTILIZZIAMO IL BADGE 969 P

In [206]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE STEPHAN PSENNER BESTEN GRU UND DANKE MARKUSCIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENSA PER PAGARE NON RIESCE AD APRIRE LE PORTE GRAZIECIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN VIA SIEMENS PER UN TRAINING CON UN CLIENTE E VOLEVO SAPERE SE POSSO UTILIZZARE IL MIO BADGE PER ACCEDERE IL PARCHEGGIO  UFFICIO NEL CASO SAREBBE POSSIBILE DI RICEVERE I DIRITTI DATO IL FATTO CHE SAR L PI SPESSO GRAZIE E SALUTI DARIUSATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PRODUZIONE CON IL BADGE PER FAVORE SBLOCCATE LACCESSO ALLA SEDE CENTRALE PER MECIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE IN PRODUZIONE COME GLI ALTRI SLOVACCHI SALUTI HANNESCIAO ALEKSANDRA JANKOVIC FUORI DAGLI ORARI 700  1800 NON RIESCE AD APRIRE LE PORTE NEL U1 PIANO SOTTERANEO SE ARRIVA CON UNA MACHINA POOL CHE HA LACCESSO NEL GARAGE NON RIESCE PI AD USCIRE POSSIAMO VEDERE IL PROFILO DEL BADGE ASSIEME GRAZIE

Result 1:
BADGE NR 988CIAO IN FUTURO UTILIZZIAMO IL BADGE 969 P

['HALLO BITTE BEIM BADGE DIE GLEICHEN RECHTE WIE STEPHAN PSENNER BESTEN GRU UND DANKE MARKUSCIAO IL BADGE DI ADAM FUNZIONA SOLO NELLA MENSA PER PAGARE NON RIESCE AD APRIRE LE PORTE GRAZIECIAO RAGAZZI SONO DOMANI TUTTO LA GIORNATA IN VIA SIEMENS PER UN TRAINING CON UN CLIENTE\xa0E VOLEVO SAPERE SE POSSO UTILIZZARE IL MIO BADGE PER ACCEDERE IL PARCHEGGIO  UFFICIO NEL CASO SAREBBE POSSIBILE DI RICEVERE I DIRITTI DATO IL FATTO CHE\xa0SAR L PI SPESSO GRAZIE E SALUTI DARIUSATTUALMENTE HO ACCESSO SOLO ALLA SEDE DELLA PRODUZIONE CON IL BADGE PER FAVORE SBLOCCATE LACCESSO ALLA SEDE CENTRALE PER MECIAO PREGO ABILITARE IL BADGE 1083 ALLE PORTE IN PRODUZIONE COME GLI ALTRI SLOVACCHI SALUTI HANNESCIAO ALEKSANDRA JANKOVIC FUORI DAGLI ORARI 700  1800 NON RIESCE AD APRIRE LE PORTE NEL U1 PIANO SOTTERANEO SE ARRIVA CON UNA MACHINA POOL CHE HA LACCESSO NEL GARAGE NON RIESCE PI AD USCIRE POSSIAMO VEDERE IL PROFILO DEL BADGE ASSIEME GRAZIE',
 'BADGE NR 988CIAO IN FUTURO UTILIZZIAMO IL BADGE 969 PER PAGARE

# df_1_computer


In [207]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_1_computer[i:i+n] for i in range(0,len(df_1_computer),n)]
    #print(list_df)

In [208]:
len(list_df)

21

In [209]:
list_df[20]

Title                                              Topic  \
120  Active the email  {"16":"User identity management, Permissions, ...   
121  Active the email  {"16":"User identity management, Permissions, ...   

                                                  Text  
120  DEAR COLLEAGUE CAN YOU PLEASE HELP TO CHECK IF...  
121  HELLO MANUEL THEN CAN YOU PLEASE ACTIVATE THE ...

In [210]:
def put_together():
    list1=[]
    for index in range(0,20):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [211]:
summ_block = put_together()
summ_block

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

[' POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN\xa0 KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO \xa0 RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY\xa0

In [212]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 20):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [213]:
blocks_to_skip = [2,4,12]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

In [214]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

[' POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN\xa0 KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO \xa0 RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY\xa0

# df_1_software

In [215]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_1_software[i:i+n] for i in range(0,len(df_1_software),n)]
    #print(list_df)

In [216]:
len(list_df)

29

In [217]:
list_df[28]

Title  \
168  Profilo Dietmar Mair  SAP Concur   
169          Concur Andrej Mladenoski   
170                            Concur   

                                                 Topic  \
168  {"16":"User identity management, Permissions, ...   
169  {"16":"User identity management, Permissions, ...   
170  {"16":"User identity management, Permissions, ...   

                                                  Text  
168  PREGO AGGIUNGERE DIVON BETREFF ERHALTEN GRE KA...  
169  CIAO  VI PREGO DI IMPOSTARE LUTENTE ANDREJ MLA...  
170  DEAR ALL COULD YOU CREATE THE CONCUR ACCOUNT F...

In [218]:
def put_together():
    list1=[]
    for index in range(0,28):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [219]:
summ_block = put_together()
summ_block

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

[' POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN\xa0 KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO \xa0 RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY\xa0

In [220]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 28):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [221]:
blocks_to_skip = [3,4,12]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

In [222]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
 POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN  KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO   RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY  

[' POTETE VERIFICARE COME MAI I MIEI CLIENTI NON RIESCONO A CONTARMI ALLA MIA MAIL E NEANCHE A INFOEMICONTROLSCOM   VEDI SOTTO   GRAZIE   DOMINIK CANTONATI SALES    EMICONTROLS GMBH  SRL  IT  39100  BOLZANO  BOZEN\xa0 KOPERNIKUSTRASSE 6A  VIA COPERNICO 6A VATIDNO IT 02721670210 M 39 334 655 7758  F 39 0471 089 110 WWWEMICONTROLSCOM                       MESSAGGIO ORIGINALE  DA SOFIA FITTANTE  DATA 181023 1230 GMT0100  A DOMINIK CANTONATI  OGGETTO I DELAYED MAIL STILL BEING RETRIED     CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT   ING SOFIA FITTANTE UFFICIO TECNICO \xa0 RS  AIRBANK SRL VIA LUIGI BAY SNC  29121 PIACENZA PC T 39 0523 763134  F 39 0523 763144 M 39 388 4234545   MESSAGGIO ORIGINALE DA MAIL DELIVERY SYSTEM  INVIATO MERCOLED 11 OTTOBRE 2023 1101 A SFITTANTEAIRBANKIT OGGETTO DELAYED MAIL STILL BEING RETRIED  THIS IS THE MAIL SYSTEM AT HOST MAILTECHNOALPINCOM    THIS IS A WARNING ONLY\xa0

# df_2_pc

In [223]:
#specify number of rows in each chunk
n=7
#split DataFrame into chunks
list_df = [df_2_pc[i:i+n] for i in range(0,len(df_2_pc),n)]
    #print(list_df)

In [224]:
len(list_df)

41

In [225]:
list_df[39]

Title  \
273                                  Adobe Acrobat   
274                                 Accesso Citrix   
275                        Cambio di Arnold Siller   
276  Accesso all'indirizzo mail 3Dplanning via web   
277                    Nuova cartella su one drive   
278                       Accesso WSCAD via Citrix   
279               ONE DRIVE TECHNOALPIN EPOWERTRAC   

                                                 Topic  \
273  {"12":"Standard Software: Operating systems, M...   
274  {"12":"Standard Software: Operating systems, M...   
275  {"12":"Standard Software: Operating systems, M...   
276  {"12":"Standard Software: Operating systems, M...   
277  {"12":"Standard Software: Operating systems, M...   
278  {"12":"Standard Software: Operating systems, M...   
279  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
273  ADOBE ACROBAT CHIEDE CREDENZIALI DI ACCESSO IN...  
274  SALVE VOLEVO CHIEDERE SE LACCESSO AL CITRIX  D...  
275  ARNOLD IN FUTURO FAR PARTE DELLA EPT COME VEND...  
276  CIAO A TUTTI QUANDO LAVORO IN SMARTWORKING UTI...  
277  BUONGIORNO  HO LA NECESSIT DI CREARE UN NUOVA ...  
278  CIAOMI POTETE SISTEMARE LACCESSO WSCAD VIA CIT...  
279  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...

In [226]:
def put_together():
    list1=[]
    for index in range(0,39):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [227]:
summ_block = put_together()
summ_block

Result 0:
CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURGER  STATA INSTALLATA LA VERSIONE 2021 DI SOLIDEDGE AVREMMO BISOGNO CHE ANCHE LUI AVESSE LA VERSIONE 2023  GRAZIE STEIN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIGNATUR HERGESTELLT WERDEN AUS BOZEN WURDE SCHON MEHRMALS REMOTE PROBIERT DIESES PROBLEM ZU LSEN WIR HABEN ABGEMACHT DAS ICH MICH DAS NCHSTE MAL MELDE WENN ICH IN BOZEN BIN AM KOMMENDEN MONTAG WERDE ICH GEGEN MITTAG IN BOZEN SEIN UND AM DIENSTAGMITTAG WIEDER ZURCK IN DIE SCHWEIZ FAHREN BITTE UM EINPLANUNG FR MEIN PC UND EINE KURZE BERATUNG IN DEPLEASE INSTALL THE ADOBE READER ON WEIWEI WANGS PC AND SET IT AS DEFAULT PDF SOFTWARE PDF REPORTS FORM NAV DEVONO ESSERE GENERATI CON QUESTO PROGRAMMA GRAZIE HELLO   CAN YOU HAVE A LOOK ON MY PC CAN NO CONNECT TO ALL NAVCRM INTRANETECT   WAS THINKING THAT I HAVE TO CHANGE WINDOWS PASSWORD BUT NOT POSSIBLE TO   SORRY WOUD LIKE MAKE A TICKET BUT NOT POSSIBLE                         MY PC IS ONLINE THX     PATRICK VARONIER SITE MANAGER 

['CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURGER  STATA INSTALLATA LA VERSIONE 2021 DI SOLIDEDGE AVREMMO BISOGNO CHE ANCHE LUI AVESSE LA VERSIONE 2023  GRAZIE STEIN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIGNATUR HERGESTELLT WERDEN AUS BOZEN WURDE SCHON MEHRMALS REMOTE PROBIERT DIESES PROBLEM ZU LSEN WIR HABEN ABGEMACHT DAS ICH MICH DAS NCHSTE MAL MELDE WENN ICH IN BOZEN BIN AM KOMMENDEN MONTAG WERDE ICH GEGEN MITTAG IN BOZEN SEIN UND AM DIENSTAGMITTAG WIEDER ZURCK IN DIE SCHWEIZ FAHREN BITTE UM EINPLANUNG FR MEIN PC UND EINE KURZE BERATUNG IN DEPLEASE INSTALL THE ADOBE READER ON WEIWEI WANGS PC AND SET IT AS DEFAULT PDF SOFTWARE PDF REPORTS FORM NAV DEVONO ESSERE GENERATI CON QUESTO PROGRAMMA GRAZIE HELLO \xa0 CAN YOU HAVE A LOOK ON MY PC CAN NO CONNECT TO ALL NAVCRM INTRANETECT \xa0 WAS THINKING THAT I HAVE TO CHANGE WINDOWS PASSWORD BUT NOT POSSIBLE TO \xa0 SORRY WOUD LIKE MAKE A TICKET BUT NOT POSSIBLE \xa0 \xa0\xa0\xa0\xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0 \xa0 \xa0 \xa0

In [228]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 39):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [229]:
blocks_to_skip = [16]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURGER  STATA INSTALLATA LA VERSIONE 2021 DI SOLIDEDGE AVREMMO BISOGNO CHE ANCHE LUI AVESSE LA VERSIONE 2023  GRAZIE STEIN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIGNATUR HERGESTELLT WERDEN AUS BOZEN WURDE SCHON MEHRMALS REMOTE PROBIERT DIESES PROBLEM ZU LSEN WIR HABEN ABGEMACHT DAS ICH MICH DAS NCHSTE MAL MELDE WENN ICH IN BOZEN BIN AM KOMMENDEN MONTAG WERDE ICH GEGEN MITTAG IN BOZEN SEIN UND AM DIENSTAGMITTAG WIEDER ZURCK IN DIE SCHWEIZ FAHREN BITTE UM EINPLANUNG FR MEIN PC UND EINE KURZE BERATUNG IN DEPLEASE INSTALL THE ADOBE READER ON WEIWEI WANGS PC AND SET IT AS DEFAULT PDF SOFTWARE PDF REPORTS FORM NAV DEVONO ESSERE GENERATI CON QUESTO PROGRAMMA GRAZIE HELLO   CAN YOU HAVE A LOOK ON MY PC CAN NO CONNECT TO ALL NAVCRM INTRANETECT   WAS THINKING THAT I HAVE TO CHANGE WINDOWS PASSWORD BUT NOT POSSIBLE TO   SORRY WOUD LIKE MAKE A TICKET BUT NOT POSSIBLE                         MY PC IS ONLINE THX     PATRICK VARONIER SITE MANAGER 

In [230]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURGER  STATA INSTALLATA LA VERSIONE 2021 DI SOLIDEDGE AVREMMO BISOGNO CHE ANCHE LUI AVESSE LA VERSIONE 2023  GRAZIE STEIN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIGNATUR HERGESTELLT WERDEN AUS BOZEN WURDE SCHON MEHRMALS REMOTE PROBIERT DIESES PROBLEM ZU LSEN WIR HABEN ABGEMACHT DAS ICH MICH DAS NCHSTE MAL MELDE WENN ICH IN BOZEN BIN AM KOMMENDEN MONTAG WERDE ICH GEGEN MITTAG IN BOZEN SEIN UND AM DIENSTAGMITTAG WIEDER ZURCK IN DIE SCHWEIZ FAHREN BITTE UM EINPLANUNG FR MEIN PC UND EINE KURZE BERATUNG IN DEPLEASE INSTALL THE ADOBE READER ON WEIWEI WANGS PC AND SET IT AS DEFAULT PDF SOFTWARE PDF REPORTS FORM NAV DEVONO ESSERE GENERATI CON QUESTO PROGRAMMA GRAZIE HELLO   CAN YOU HAVE A LOOK ON MY PC CAN NO CONNECT TO ALL NAVCRM INTRANETECT   WAS THINKING THAT I HAVE TO CHANGE WINDOWS PASSWORD BUT NOT POSSIBLE TO   SORRY WOUD LIKE MAKE A TICKET BUT NOT POSSIBLE                         MY PC IS ONLINE THX     PATRICK VARONIER SITE MANAGER 

['CIAO SUL PC DEL NUOVO COLLEGA STEFANO SALZBURGER  STATA INSTALLATA LA VERSIONE 2021 DI SOLIDEDGE AVREMMO BISOGNO CHE ANCHE LUI AVESSE LA VERSIONE 2023  GRAZIE STEIN MEINEM OUTLOOK IM OFFICE 365 KANN KEINE SIGNATUR HERGESTELLT WERDEN AUS BOZEN WURDE SCHON MEHRMALS REMOTE PROBIERT DIESES PROBLEM ZU LSEN WIR HABEN ABGEMACHT DAS ICH MICH DAS NCHSTE MAL MELDE WENN ICH IN BOZEN BIN AM KOMMENDEN MONTAG WERDE ICH GEGEN MITTAG IN BOZEN SEIN UND AM DIENSTAGMITTAG WIEDER ZURCK IN DIE SCHWEIZ FAHREN BITTE UM EINPLANUNG FR MEIN PC UND EINE KURZE BERATUNG IN DEPLEASE INSTALL THE ADOBE READER ON WEIWEI WANGS PC AND SET IT AS DEFAULT PDF SOFTWARE PDF REPORTS FORM NAV DEVONO ESSERE GENERATI CON QUESTO PROGRAMMA GRAZIE HELLO \xa0 CAN YOU HAVE A LOOK ON MY PC CAN NO CONNECT TO ALL NAVCRM INTRANETECT \xa0 WAS THINKING THAT I HAVE TO CHANGE WINDOWS PASSWORD BUT NOT POSSIBLE TO \xa0 SORRY WOUD LIKE MAKE A TICKET BUT NOT POSSIBLE \xa0 \xa0\xa0\xa0\xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0 \xa0 \xa0 \xa0

In [231]:
import pickle

# df_2_email

In [232]:
#specify number of rows in each chunk
n=5
#split DataFrame into chunks
list_df = [df_2_email[i:i+n] for i in range(0,len(df_2_email),n)]
    #print(list_df)

In [233]:
len(list_df)

101

In [234]:
list_df[93]

Title  \
465  Accesso amministratore   
466  Accesso amministratore   
467           PROCALL ERROR   
468    R&D Ticketing Access   
469                   Login   

                                                 Topic  \
465  {"12":"Standard Software: Operating systems, M...   
466  {"12":"Standard Software: Operating systems, M...   
467  {"12":"Standard Software: Operating systems, M...   
468  {"12":"Standard Software: Operating systems, M...   
469  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
465       TEAMVIEWER LOGIN ID 332020685 PASSW VY2HTUCN  
466       TEAMVIEWER LOGIN ID 332020685 PASSW VY2HTUCN  
467  PROCALL MI DA IL SEGUENTE ERRORE ANCHE FACENDO...  
468   CIAO NON RIESCO A FARE IL LOGIN DEI TICKET PE...  
469  HALLO ICH MSSTE ZWEI RECHNUNGEN FREIGEBEN KOMM...

In [235]:
def put_together():
    list1=[]
    for index in range(0,93):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [236]:
summ_block = put_together()
summ_block

Result 0:
HELLO  I NEED TO RENEW THIS CERTIFICATE BUT I GET THE ERROR MESSAGE BELOW ON THE INTERNET  CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT       WE DETECTED ACTIVITY RELATED TO ONE OF YOUR ALERTS   YOURE GETTING THIS MESSAGE BECAUSE THERES ACTIVITY IN YOUR MICROSOFT 365 ORGANIZATION THAT MATCHES THE ALERT NEWINBOXRULE CREATE INBOX RULE FROM OUTLOOK WEB APP  ACTIVITY NEWINBOXRULE USER THOMASBURGERTECHNOALPINCOM ITEM EURPR07A009PRODOUTLOOKCOMMICROSOFT EXCHANGE HOSTED ORGANIZATIONSTECHNOALPIN0ONMICROSOFTCOMTHOMASBMAGIC CLIENT IP ADDRESS 795410615852879 TIME OF ACTIVITY UTC 9222023 64843 PM  WHATS NEXT SEARCH THE AUDIT LOG FOR THIS USER SEARCH THE AUDIT LOG FOR THIS ITEMSEARCH THE AUDIT LOG FOR THIS ACTIVITY  NOTE THERE MIGHT BE MORE ACTIVITY RELATED TO THIS ALERT SINCE YOU RECEIVED THIS EMAIL SEARCH THE AUDIT LOG TO SHOW ALL RECENT ACTIVITY   NEED HELP SEARCHING THE AUDIT LOG CHECK OUT SEARCH 

['HELLO\xa0 I NEED TO RENEW THIS CERTIFICATE BUT I GET THE ERROR MESSAGE BELOW ON THE INTERNET  CAUTION THIS IS AN EXTERNAL EMAIL PLEASE TAKE CARE WHEN CLICKING LINKS OR OPENING ATTACHMENTS WHEN IN DOUBT CONTACT YOUR IT DEPARTMENT       WE DETECTED ACTIVITY RELATED TO ONE OF YOUR ALERTS   YOURE GETTING THIS MESSAGE BECAUSE THERES ACTIVITY IN YOUR MICROSOFT 365 ORGANIZATION THAT MATCHES THE ALERT NEWINBOXRULE CREATE INBOX RULE FROM OUTLOOK WEB APP  ACTIVITY NEWINBOXRULE USER THOMASBURGERTECHNOALPINCOM ITEM EURPR07A009PRODOUTLOOKCOMMICROSOFT EXCHANGE HOSTED ORGANIZATIONSTECHNOALPIN0ONMICROSOFTCOMTHOMASBMAGIC CLIENT IP ADDRESS 795410615852879 TIME OF ACTIVITY UTC 9222023 64843 PM  WHATS NEXT SEARCH THE AUDIT LOG FOR THIS USER SEARCH THE AUDIT LOG FOR THIS ITEMSEARCH THE AUDIT LOG FOR THIS ACTIVITY  NOTE THERE MIGHT BE MORE ACTIVITY RELATED TO THIS ALERT SINCE YOU RECEIVED THIS EMAIL SEARCH THE AUDIT LOG TO SHOW ALL RECENT ACTIVITY   NEED HELP SEARCHING THE AUDIT LOG CHECK OUT SEARCH THE A

In [237]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 93):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [238]:
blocks_to_skip = [0,1,3,4,12,14,22,25,27,29,47,62,63,66,67,69,70,77]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 2:
 DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM     TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO      HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM     A PRESTO MATTEO         CIAOABBIAMO CAMBIATO IL PASSWORT ORA NON MI LASCIA PI INSERIRE IL MIO INDIRIZZO EMAIL IL CAMPO  BLOCCATOIL PASSWORT POSSO INSERIRECIAO  MI ARRIVANO SPESSO DEI EMAIL DA QUESTO INDIRIZZO QUARANTINEMESSAGINGMICROSOFTCOM E AFFIDABILE O NO SALUTI ALLEGATO ANCORA UNA VOLTA IL LINK CHE AVEVO MANDATO   CORDIALMENTE E GRAZIE    ANNI ERLACHER CORPORATE REAL ESTATE MANAGER TECHNOALPIN HOLDING SPA  IT 

In [239]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 2:
 DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS     CIAO MANUEL    UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE   NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE   VEDI SOTTO   GRAZIE DOMINIK       NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM     TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO      HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM     A PRESTO MATTEO         CIAOABBIAMO CAMBIATO IL PASSWORT ORA NON MI LASCIA PI INSERIRE IL MIO INDIRIZZO EMAIL IL CAMPO  BLOCCATOIL PASSWORT POSSO INSERIRECIAO  MI ARRIVANO SPESSO DEI EMAIL DA QUESTO INDIRIZZO QUARANTINEMESSAGINGMICROSOFTCOM E AFFIDABILE O NO SALUTI ALLEGATO ANCORA UNA VOLTA IL LINK CHE AVEVO MANDATO   CORDIALMENTE E GRAZIE    ANNI ERLACHER CORPORATE REAL ESTATE MANAGER TECHNOALPIN HOLDING SPA  IT 

[' DA DOMINIK CANTONATI  INVIATO LUNED 16 OTTOBRE 2023 0831 A MANUEL FURLOTTI  OGGETTO I COLLABORAZIONE EMICONTROLS   \xa0 CIAO MANUEL  \xa0 UN NS PARTNER CI HA SEGNATO DEI PROBLEMI SUL DOMINIO EC PUOI VERIFICARE \xa0 NON SONO IN AZIENDA E NON RIESCO AD APRIRE TICKET IN QUANTO NON IN RETE AZIENDALE \xa0 VEDI SOTTO \xa0 GRAZIE DOMINIK  \xa0 \xa0  NEL FRATTEMPO TI AVVERTO CHE ENTRAMBE LE TUE EMAIL SONO STATE MESSE IN SPAM DAL MIO PROVIDER DI POSTA GMAILCOM  \xa0  TI CONSIGLIO DI FAR CONTROLLARE AL TUO IT PERCH CI SONO DEI PROBLEMI SUL DOMINIO   \xa0  HTTPSMXTOOLBOXCOMEMAILHEALTHEMICONTROLSCOM  \xa0  A PRESTO MATTEO  \xa0      CIAOABBIAMO CAMBIATO IL PASSWORT ORA NON MI LASCIA PI INSERIRE IL MIO INDIRIZZO EMAIL IL CAMPO  BLOCCATOIL PASSWORT POSSO INSERIRECIAO  MI ARRIVANO SPESSO DEI EMAIL DA QUESTO INDIRIZZO\xa0QUARANTINEMESSAGINGMICROSOFTCOM E AFFIDABILE O NO SALUTI ALLEGATO ANCORA UNA VOLTA IL LINK CHE AVEVO MANDATO \xa0 CORDIALMENTE E GRAZIE  \xa0 ANNI ERLACHER CORPORATE REAL ESTATE MA

# df_2_access

In [240]:
#specify number of rows in each chunk
n=7
#split DataFrame into chunks
list_df = [df_2_access[i:i+n] for i in range(0,len(df_2_access),n)]
    #print(list_df)

In [241]:
len(list_df)

27

In [242]:
list_df[26]

Title  \
182                 Foxxit PDF Viewer   
183                    ACROBAT WRITER   
184             Downloading adobe pro   
185  ONE DRIVE TECHNOALPIN EPOWERTRAC   
186                    Setup nuovo PC   
187                    Update Windows   

                                                 Topic  \
182  {"12":"Standard Software: Operating systems, M...   
183  {"12":"Standard Software: Operating systems, M...   
184  {"12":"Standard Software: Operating systems, M...   
185  {"12":"Standard Software: Operating systems, M...   
186  {"12":"Standard Software: Operating systems, M...   
187  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
182  IT ONLY SHOWED 4 STARS AS THE PASSWORD IN THE ...  
183  LUTENZA  STATA COMPRATA DALLA DITTA EPOWERTRAC...  
184  I AM TRYING TO INSTALL ADOBE PRO AND IT WILL N...  
185  BUONGIORNO  NON HO ACCESSO  NON VEDO 10 CARTEL...  
186  LID RIMANE PASSWORD AVEVA TIMEOUT QUI QUELLA N...  
187  HI  COULD YOU HELP ME UPDATE WINDOWS TEAM VIEW...

In [243]:
def put_together():
    list1=[]
    for index in range(0,26):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
 ANCHE NEL TEAMS NON SONO PIU LE DATI CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRETTAMENTE FUNZIONA PER I MIEI COLLEGHI RICEVO QUESTO MESSAGGIOCOMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO UNA PERSONA CHIAMA NON SUONA SUL PC  IL VOLUME  ACCESO E ABBIAMO TESTATO  GRAZIECIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GR

[' ANCHE NEL TEAMS NON SONO PIU LE DATI CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRETTAMENTE FUNZIONA PER I MIEI COLLEGHI RICEVO QUESTO MESSAGGIOCOMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO UNA PERSONA CHIAMA NON SUONA SUL PC  IL VOLUME  ACCESO E ABBIAMO TESTATO  GRAZIECIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS\xa0 GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE 

In [244]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 26):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [245]:
blocks_to_skip = [17]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
 ANCHE NEL TEAMS NON SONO PIU LE DATI CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRETTAMENTE FUNZIONA PER I MIEI COLLEGHI RICEVO QUESTO MESSAGGIOCOMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO UNA PERSONA CHIAMA NON SUONA SUL PC  IL VOLUME  ACCESO E ABBIAMO TESTATO  GRAZIECIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GR

In [246]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
 ANCHE NEL TEAMS NON SONO PIU LE DATI CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRETTAMENTE FUNZIONA PER I MIEI COLLEGHI RICEVO QUESTO MESSAGGIOCOMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO UNA PERSONA CHIAMA NON SUONA SUL PC  IL VOLUME  ACCESO E ABBIAMO TESTATO  GRAZIECIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS  GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GR

[' ANCHE NEL TEAMS NON SONO PIU LE DATI CIAO IL MIO MICROSOFT TEAMS NON FUNZIONA CORRETTAMENTE FUNZIONA PER I MIEI COLLEGHI RICEVO QUESTO MESSAGGIOCOMPUTER C405  HO UN PROBLEMA CON TEAMS QUANDO UNA PERSONA CHIAMA NON SUONA SUL PC  IL VOLUME  ACCESO E ABBIAMO TESTATO  GRAZIECIAO DA OGGI NON VEDO PIU IL LINK PER IL TEAMS MEETING SE CREO UN APPUNTAMENTO IN OUTLOOKBUONGIORNO IL COLLEGAMENTO TRA I DUE PROGRAMMI SOPRACITATI NON FUNZIONA NON RIESCO PI A FISSARE MEETING MS TEAMS TRAMITE L INTERFACCIA OUTLOOK OUTLOOK COLLEGA TEAMVIEWER AL POSTO DI MS TEAMS\xa0 GRAZIE IN ANTICIPOCIAO PER FAVORE AGGIUNGERE IL NOSTRO PARTNER IN FINLANDIA MANU LAARI MANULAARISGNFI COME OSPITE NEL MSTEAMS GRAZIE WOLFGANG HCIAO DA QUALCHE SETTIMANA HO QUESTO PROBLEMA CHE LA CAMERA DEL COMPUTER NON FUNZIONA QUANDO SONO IN HOME OFFICE DALLUFFICIO FUNZIONA INVECE NORMALMENTE HO PROVATO A DARE ACCESSO DALLE IMPOSTAZIONI MA NON SONO RIUSCITA A FARLA ANDARE SPECIALMENTE SU TEAMS  UN PROBLEMA RIUSCIRESTE AD AIUTARMI GRAZIE 

# df_2_software 

In [247]:
#specify number of rows in each chunk
n=7
#split DataFrame into chunks
list_df = [df_2_software[i:i+n] for i in range(0,len(df_2_software),n)]
    #print(list_df)

In [248]:
len(list_df)

29

In [249]:
list_df[28]

Title  \
196  Outlook Synchroisierungsprobleme   
197                 Foxxit PDF Viewer   
198                 Solid Edge Lizenz   
199                    Setup nuovo PC   
200                Solide Edge Lizenz   

                                                 Topic  \
196  {"12":"Standard Software: Operating systems, M...   
197  {"12":"Standard Software: Operating systems, M...   
198  {"12":"Standard Software: Operating systems, M...   
199  {"12":"Standard Software: Operating systems, M...   
200  {"12":"Standard Software: Operating systems, M...   

                                                  Text  
196  HALLO HABE AM FREITAG MEIN LAPTOP GEWECHSELT H...  
197  HELLO IS THE FOXXIT PDF VIEWER INSTALLEREXE SO...  
198  GUTEN NACHMITTAG MEIN SOLID EDGE FOUNDATION FU...  
199  UPDATE NON DOBBIAMO INSTALLARLO MA C DA SISTEM...  
200  ERA IL SERVER DI LICENZA GRAZIE ADESSA FUNZION...

In [250]:
def put_together():
    list1=[]
    for index in range(0,29):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATION DA DANIELSSON PATRICK PER IL BC14 CONTROLLARE SE C IL WEBVIEWER 2 INSTALLATO I PERMESSI SUL USER SETUP GLI HA GI CONTROLLARE I PLUGIN SOTTO CPROGRAM FILES X86MICROSOFT DYNAMICS 365 BUSINESS CENTRAL140ROLETAILORED CLIENTADDINSSALUTIHO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI  RISOLTO NIENTE      CIAO MANUEL    AVREI BISOGNO DI INSTALLARE IL PROGRAMMA IN OGGETTO AL POSTO DEL PROGRAMMA ATTUALE E DRAWINGS  CHE NON HA NESSUNA FUNZIONE UTILE E MI IMPALLA IL PC OGNO VOLTA CHE DEVO APRIRE UN FILE DWG   MI FAI SAPERE QUANDO HAI TEMPO CHE TI LANCIO LA CONDIVISIONE DELLO SCHERMO    GRZ   FEDERICO                  FEDERICO MILAN  SALES MANAGEMENT INDOOR SNOW DIVISION TECHNOALPIN SPA  ITALY  39100  BOLZANO  BOZEN  PAGOSTINISTRAE 2 VIA P AGOSTINI   M 39 346 5305912  INDOORTECHNOALPINCOM                                                        PLEASE FIND OUR PRIVACY POLICY HERE   MI SERVE IL PERMESSO DEL AMMINISTRATORE PER INSTALLARE CODESY

['CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATION DA DANIELSSON PATRICK PER IL BC14 CONTROLLARE SE C IL\xa0WEBVIEWER 2 INSTALLATO I PERMESSI SUL USER SETUP GLI HA GI CONTROLLARE I PLUGIN SOTTO\xa0CPROGRAM FILES X86MICROSOFT DYNAMICS 365 BUSINESS CENTRAL140ROLETAILORED CLIENTADDINSSALUTIHO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI  RISOLTO NIENTE\xa0 \xa0 \xa0 CIAO MANUEL  \xa0 AVREI BISOGNO DI INSTALLARE IL PROGRAMMA IN OGGETTO AL POSTO DEL PROGRAMMA ATTUALE E DRAWINGS  CHE NON HA NESSUNA FUNZIONE UTILE E MI IMPALLA IL PC OGNO VOLTA CHE DEVO APRIRE UN FILE DWG \xa0 MI FAI SAPERE QUANDO HAI TEMPO CHE TI LANCIO LA CONDIVISIONE DELLO SCHERMO  \xa0 GRZ \xa0 FEDERICO \xa0 \xa0 \xa0 \xa0 \xa0        FEDERICO MILAN  SALES MANAGEMENT INDOOR SNOW DIVISION TECHNOALPIN SPA  ITALY  39100  BOLZANO  BOZEN  PAGOSTINISTRAE 2 VIA P AGOSTINI   M 39 346 5305912  INDOORTECHNOALPINCOM          \xa0 \xa0          \xa0                \xa0               PLEASE FIND OUR PRIVACY POLICY HERE   MI SERVE IL PER

In [251]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 29):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [252]:
blocks_to_skip = [15,27,28]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)


Result 0:
CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATION DA DANIELSSON PATRICK PER IL BC14 CONTROLLARE SE C IL WEBVIEWER 2 INSTALLATO I PERMESSI SUL USER SETUP GLI HA GI CONTROLLARE I PLUGIN SOTTO CPROGRAM FILES X86MICROSOFT DYNAMICS 365 BUSINESS CENTRAL140ROLETAILORED CLIENTADDINSSALUTIHO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI  RISOLTO NIENTE      CIAO MANUEL    AVREI BISOGNO DI INSTALLARE IL PROGRAMMA IN OGGETTO AL POSTO DEL PROGRAMMA ATTUALE E DRAWINGS  CHE NON HA NESSUNA FUNZIONE UTILE E MI IMPALLA IL PC OGNO VOLTA CHE DEVO APRIRE UN FILE DWG   MI FAI SAPERE QUANDO HAI TEMPO CHE TI LANCIO LA CONDIVISIONE DELLO SCHERMO    GRZ   FEDERICO                  FEDERICO MILAN  SALES MANAGEMENT INDOOR SNOW DIVISION TECHNOALPIN SPA  ITALY  39100  BOLZANO  BOZEN  PAGOSTINISTRAE 2 VIA P AGOSTINI   M 39 346 5305912  INDOORTECHNOALPINCOM                                                        PLEASE FIND OUR PRIVACY POLICY HERE   MI SERVE IL PERMESSO DEL AMMINISTRATORE PER INSTALLARE CODESY

In [253]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATION DA DANIELSSON PATRICK PER IL BC14 CONTROLLARE SE C IL WEBVIEWER 2 INSTALLATO I PERMESSI SUL USER SETUP GLI HA GI CONTROLLARE I PLUGIN SOTTO CPROGRAM FILES X86MICROSOFT DYNAMICS 365 BUSINESS CENTRAL140ROLETAILORED CLIENTADDINSSALUTIHO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI  RISOLTO NIENTE      CIAO MANUEL    AVREI BISOGNO DI INSTALLARE IL PROGRAMMA IN OGGETTO AL POSTO DEL PROGRAMMA ATTUALE E DRAWINGS  CHE NON HA NESSUNA FUNZIONE UTILE E MI IMPALLA IL PC OGNO VOLTA CHE DEVO APRIRE UN FILE DWG   MI FAI SAPERE QUANDO HAI TEMPO CHE TI LANCIO LA CONDIVISIONE DELLO SCHERMO    GRZ   FEDERICO                  FEDERICO MILAN  SALES MANAGEMENT INDOOR SNOW DIVISION TECHNOALPIN SPA  ITALY  39100  BOLZANO  BOZEN  PAGOSTINISTRAE 2 VIA P AGOSTINI   M 39 346 5305912  INDOORTECHNOALPINCOM                                                        PLEASE FIND OUR PRIVACY POLICY HERE   MI SERVE IL PERMESSO DEL AMMINISTRATORE PER INSTALLARE CODESY

['CIAO PER FAVORE INSTALLARE LA ECM WEBINTEGRATION DA DANIELSSON PATRICK PER IL BC14 CONTROLLARE SE C IL\xa0WEBVIEWER 2 INSTALLATO I PERMESSI SUL USER SETUP GLI HA GI CONTROLLARE I PLUGIN SOTTO\xa0CPROGRAM FILES X86MICROSOFT DYNAMICS 365 BUSINESS CENTRAL140ROLETAILORED CLIENTADDINSSALUTIHO GI PROVATO A REINSTALLARE TEAMVIEWER NON SI  RISOLTO NIENTE\xa0 \xa0 \xa0 CIAO MANUEL  \xa0 AVREI BISOGNO DI INSTALLARE IL PROGRAMMA IN OGGETTO AL POSTO DEL PROGRAMMA ATTUALE E DRAWINGS  CHE NON HA NESSUNA FUNZIONE UTILE E MI IMPALLA IL PC OGNO VOLTA CHE DEVO APRIRE UN FILE DWG \xa0 MI FAI SAPERE QUANDO HAI TEMPO CHE TI LANCIO LA CONDIVISIONE DELLO SCHERMO  \xa0 GRZ \xa0 FEDERICO \xa0 \xa0 \xa0 \xa0 \xa0        FEDERICO MILAN  SALES MANAGEMENT INDOOR SNOW DIVISION TECHNOALPIN SPA  ITALY  39100  BOLZANO  BOZEN  PAGOSTINISTRAE 2 VIA P AGOSTINI   M 39 346 5305912  INDOORTECHNOALPINCOM          \xa0 \xa0          \xa0                \xa0               PLEASE FIND OUR PRIVACY POLICY HERE   MI SERVE IL PER

# df_3

# df_3_printer 

In [254]:
#specify number of rows in each chunk
n=9
#split DataFrame into chunks
list_df = [df_3_printer[i:i+n] for i in range(0,len(df_3_printer),n)]
    #print(list_df)

In [255]:
len(list_df)

37

In [256]:
list_df[36]

Title  \
324  Formati di stampa del plotter   

                                                 Topic  \
324  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
324  BUON POMERIGGIOCAPITA CHE PER INTERI POMERIGGI...

In [257]:
def put_together():
    list1=[]
    for index in range(0,36):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block


Result 0:
BUON D DA QUALCHE TEMPO ORMAI CHE HO NOTATO UNA RIDUZIONE NEL TEMPO DI ATTESA PRIMA CHE LE TELEFONATE IN INGRESSO SIANO DEVIATE IN RECEPTION IL TELEFONO SQUILLA E DOPO DUE SQUILLI LA TELEFONATA VIENE DEVIATA DA BASSO CAPITA SIA CON LE TELEFONATE ESTERNE SIA CON QUELLE INTERNE LA MAGGIOR PARTE DELLE VOLTE IO SONO FISICAMENTE IN UFFICIO MA MAGARI STO AIUTANDO UN COLLEGA O SONO A PRENDERE UN FOGLIO ALLA STAMPANTE E MI PERDO LA TELEFONATA IN INGRESSO SI PU AUMENTARE IL TEMPO PRIMA DELLA DEVIAZIONE BASTEREBBE ANCHE SOLO RADDOPPIARLO GRAZIESALUTIGGA CIAO A VOI QUANDO MANDO IN STAMPA UN PDF SULLA STAMPANTE HP LASERJET 400 M401 DELLUFFICIO DI MICHELE I FOGLI ESCONO BIANCHI GLI EXCEL LI STAMPA  RIUSCITE AD AIUTARMI DEVO STAMPARE I REGISTRI RIFIUTI SU FOGLI VIDIMATI GRAZIE ELISABUONGIORNO NON RIESCO A STAMPARE MERANER MI DICE CHE LA STAMPANTE CHE ABBIAMO IN UFFICIO DOVREBBE CHIAMARSI HP ANGEBOT MA NON RIESCO A TROVARLA IN LISTA E DI CONSEGUENZA NON RIESCO A STAMPARE CORDIALI SALUTI LA 

['BUON D DA QUALCHE TEMPO ORMAI CHE HO NOTATO UNA RIDUZIONE NEL TEMPO DI ATTESA PRIMA CHE LE TELEFONATE IN INGRESSO SIANO DEVIATE IN RECEPTION IL TELEFONO SQUILLA E DOPO DUE SQUILLI LA TELEFONATA VIENE DEVIATA DA BASSO CAPITA SIA CON LE TELEFONATE ESTERNE SIA CON QUELLE INTERNE LA MAGGIOR PARTE DELLE VOLTE IO SONO FISICAMENTE IN UFFICIO MA MAGARI STO AIUTANDO UN COLLEGA O SONO A PRENDERE UN FOGLIO ALLA STAMPANTE E MI PERDO LA TELEFONATA IN INGRESSO SI PU AUMENTARE IL TEMPO PRIMA DELLA DEVIAZIONE BASTEREBBE ANCHE SOLO RADDOPPIARLO GRAZIESALUTIGGA CIAO A VOI QUANDO MANDO IN STAMPA UN PDF SULLA STAMPANTE\xa0HP LASERJET 400 M401 DELLUFFICIO DI MICHELE I FOGLI ESCONO BIANCHI GLI EXCEL LI STAMPA  RIUSCITE AD AIUTARMI DEVO STAMPARE I REGISTRI RIFIUTI SU FOGLI VIDIMATI GRAZIE ELISABUONGIORNO NON RIESCO A STAMPARE MERANER MI DICE CHE LA STAMPANTE CHE ABBIAMO IN UFFICIO DOVREBBE CHIAMARSI HP ANGEBOT MA NON RIESCO A TROVARLA IN LISTA E DI CONSEGUENZA NON RIESCO A STAMPARE CORDIALI SALUTI LA STAMP

# df_3_docking

In [258]:
#specify number of rows in each chunk
n=4
#split DataFrame into chunks
list_df = [df_3_docking[i:i+n] for i in range(0,len(df_3_docking),n)]
    #print(list_df)

In [259]:
len(list_df)

37

In [260]:
list_df[36]

Title  \
144     Stazione di lavoro da Christian Tschimben    
145                    Docking station no ethernet   
146  PC che fa rumore. Microfono o audio difettoso   

                                                 Topic  \
144  {"11":"Hardware, Telephony, Smartphones, Monit...   
145  {"11":"Hardware, Telephony, Smartphones, Monit...   
146  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
144  CON DOCKINGSTATION DUE MONITOR PI TASTIERA  GR...  
145  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
146  CIAO ARASH  HO SEMPRE QUEL PROBLEMA DEL RUMORE...

In [261]:
def put_together():
    list1=[]
    for index in range(0,36):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ANSCHLUSS PC AN DOCKING STATIONCIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBBIAMO LAVORARE SEMPRE USANDO IL WIFI PERCH OGNITANTO PERDIAMO LA CONNESSIONE DEL ETH NON SO SE IL PROBLEMA VIENE CREATO DALLA DOCKING SWITCH SUL MIO TAVOLO  GI STATO CAMBIATO  NOI ABBIAMO TRE RETI NEL NOSTRO UFFICIO 10010XXX 10011XXX 10012XXX  GRAZIE  SALUTI HANNESDEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH A THINK PAD DOCKING STATION WHICH IS NOT MINE UNFORTUNATELY I CANNOT CONNECT TO THE EXTERNAL MONITOR DO YOU HAVE ANY ADVICE  THANKS SOPHIACIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MONITOR LO AVEVO STACCATO DALLA DOCKING STATION PER ANDARE IN RIUNIONE QUANDO LHO RIATTACCATO NON ANDAVANO PI HO RIAVVIATO E ANCHE SPENTO E RIACCESO IL PC PI VOLTE MA NON FUNZIONA PRIMA DEL RIAVVIO NON FUNZIONAVA NAEMMENO LA TASTIERA ADESSO S  UN SALUTO ELISA

Result 1:
CIAO  LE PORTE DELLA MIA NUOVA DOCKINGSTATION NON COMUNICANO FUNGONO DA ALLIMENTATORE MA NON ALTRO SALUT

['STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ANSCHLUSS PC AN DOCKING STATIONCIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBBIAMO LAVORARE SEMPRE USANDO IL WIFI PERCH OGNITANTO PERDIAMO LA CONNESSIONE DEL ETH NON SO SE IL PROBLEMA VIENE CREATO DALLA DOCKING SWITCH SUL MIO TAVOLO  GI STATO CAMBIATO  NOI ABBIAMO TRE RETI NEL NOSTRO UFFICIO 10010XXX 10011XXX 10012XXX  GRAZIE  SALUTI HANNESDEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH A THINK PAD DOCKING STATION WHICH IS NOT MINE\xa0UNFORTUNATELY I CANNOT CONNECT TO THE EXTERNAL MONITOR DO YOU HAVE ANY ADVICE  THANKS SOPHIACIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MONITOR LO AVEVO STACCATO DALLA\xa0DOCKING STATION PER ANDARE IN RIUNIONE QUANDO LHO RIATTACCATO NON ANDAVANO PI HO RIAVVIATO E ANCHE SPENTO E RIACCESO IL PC PI VOLTE MA NON FUNZIONA PRIMA DEL RIAVVIO NON FUNZIONAVA NAEMMENO LA TASTIERA ADESSO S  UN SALUTO ELISA',
 'CIAO\xa0 LE PORTE DELLA MIA NUOVA DOCKINGSTATION NON COMUNICANO FUNGONO DA ALLIMENTATORE MA NON ALTRO SALUTI CIAO

In [262]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 36):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [263]:
blocks_to_skip = [27,28]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ANSCHLUSS PC AN DOCKING STATIONCIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBBIAMO LAVORARE SEMPRE USANDO IL WIFI PERCH OGNITANTO PERDIAMO LA CONNESSIONE DEL ETH NON SO SE IL PROBLEMA VIENE CREATO DALLA DOCKING SWITCH SUL MIO TAVOLO  GI STATO CAMBIATO  NOI ABBIAMO TRE RETI NEL NOSTRO UFFICIO 10010XXX 10011XXX 10012XXX  GRAZIE  SALUTI HANNESDEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH A THINK PAD DOCKING STATION WHICH IS NOT MINE UNFORTUNATELY I CANNOT CONNECT TO THE EXTERNAL MONITOR DO YOU HAVE ANY ADVICE  THANKS SOPHIACIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MONITOR LO AVEVO STACCATO DALLA DOCKING STATION PER ANDARE IN RIUNIONE QUANDO LHO RIATTACCATO NON ANDAVANO PI HO RIAVVIATO E ANCHE SPENTO E RIACCESO IL PC PI VOLTE MA NON FUNZIONA PRIMA DEL RIAVVIO NON FUNZIONAVA NAEMMENO LA TASTIERA ADESSO S  UN SALUTO ELISA

Result 1:
CIAO  LE PORTE DELLA MIA NUOVA DOCKINGSTATION NON COMUNICANO FUNGONO DA ALLIMENTATORE MA NON ALTRO SALUT

In [264]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ANSCHLUSS PC AN DOCKING STATIONCIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBBIAMO LAVORARE SEMPRE USANDO IL WIFI PERCH OGNITANTO PERDIAMO LA CONNESSIONE DEL ETH NON SO SE IL PROBLEMA VIENE CREATO DALLA DOCKING SWITCH SUL MIO TAVOLO  GI STATO CAMBIATO  NOI ABBIAMO TRE RETI NEL NOSTRO UFFICIO 10010XXX 10011XXX 10012XXX  GRAZIE  SALUTI HANNESDEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH A THINK PAD DOCKING STATION WHICH IS NOT MINE UNFORTUNATELY I CANNOT CONNECT TO THE EXTERNAL MONITOR DO YOU HAVE ANY ADVICE  THANKS SOPHIACIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MONITOR LO AVEVO STACCATO DALLA DOCKING STATION PER ANDARE IN RIUNIONE QUANDO LHO RIATTACCATO NON ANDAVANO PI HO RIAVVIATO E ANCHE SPENTO E RIACCESO IL PC PI VOLTE MA NON FUNZIONA PRIMA DEL RIAVVIO NON FUNZIONAVA NAEMMENO LA TASTIERA ADESSO S  UN SALUTO ELISA

Result 1:
CIAO  LE PORTE DELLA MIA NUOVA DOCKINGSTATION NON COMUNICANO FUNGONO DA ALLIMENTATORE MA NON ALTRO SALUT

['STNDIGES FLIMMERN DES BILDSCHIRMES IIYAMA BEI ANSCHLUSS PC AN DOCKING STATIONCIAO  CI POTETE VERIFICARE LA NOSTRA RETE DOBBIAMO LAVORARE SEMPRE USANDO IL WIFI PERCH OGNITANTO PERDIAMO LA CONNESSIONE DEL ETH NON SO SE IL PROBLEMA VIENE CREATO DALLA DOCKING SWITCH SUL MIO TAVOLO  GI STATO CAMBIATO  NOI ABBIAMO TRE RETI NEL NOSTRO UFFICIO 10010XXX 10011XXX 10012XXX  GRAZIE  SALUTI HANNESDEAR IT TEAM I WORK AT EMICONTROLS TODAY WITH A THINK PAD DOCKING STATION WHICH IS NOT MINE\xa0UNFORTUNATELY I CANNOT CONNECT TO THE EXTERNAL MONITOR DO YOU HAVE ANY ADVICE  THANKS SOPHIACIAO A VOI IL MIO PORTATILE NON VEDE PI I 2 MONITOR LO AVEVO STACCATO DALLA\xa0DOCKING STATION PER ANDARE IN RIUNIONE QUANDO LHO RIATTACCATO NON ANDAVANO PI HO RIAVVIATO E ANCHE SPENTO E RIACCESO IL PC PI VOLTE MA NON FUNZIONA PRIMA DEL RIAVVIO NON FUNZIONAVA NAEMMENO LA TASTIERA ADESSO S  UN SALUTO ELISA',
 'CIAO\xa0 LE PORTE DELLA MIA NUOVA DOCKINGSTATION NON COMUNICANO FUNGONO DA ALLIMENTATORE MA NON ALTRO SALUTI CIAO

# df_3_tcp

In [265]:
#specify number of rows in each chunk
n=3
#split DataFrame into chunks
list_df = [df_3_tcp[i:i+n] for i in range(0,len(df_3_tcp),n)]
    #print(list_df)

In [266]:
len(list_df)

3

In [267]:
list_df[2]

Title  \
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...  
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...

In [268]:
def put_together():
    list1=[]
    for index in range(0,2):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE

Result 1:
A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIEHALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WI

['SCUSA MANUEL NON SO DOVE FARLO \xa0UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE',
 'A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO\xa0APPENA TORNO IN UFFICIO GRAZIEHALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL\xa0KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WINDO

In [269]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 2):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [270]:
blocks_to_skip = [1]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE



In [271]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE



['SCUSA MANUEL NON SO DOVE FARLO \xa0UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE']

# df_3_db

In [272]:
#specify number of rows in each chunk
n=3
#split DataFrame into chunks
list_df = [df_3_db[i:i+n] for i in range(0,len(df_3_db),n)]
    #print(list_df)

In [273]:
len(list_df)

3

In [274]:
list_df[2]

Title  \
6                                      ticket 381298   
7                        Docking station no ethernet   
8  für die elektronische Übermittlung statistisch...   

                                               Topic  \
6  {"11":"Hardware, Telephony, Smartphones, Monit...   
7  {"11":"Hardware, Telephony, Smartphones, Monit...   
8  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                Text  
6   HELLO I AM NOT ABLE TO LOG INTO THIS COMPUTER...  
7  CIAO CON IL TICKET 473713 AVEVAMO AGGIORNATO T...  
8   ENTSCHULDIGUNG ABER DIESE SEITE IST NICHT VER...

In [275]:
def put_together():
    list1=[]
    for index in range(0,2):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE

Result 1:
A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO APPENA TORNO IN UFFICIO GRAZIEHALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WI

['SCUSA MANUEL NON SO DOVE FARLO \xa0UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE',
 'A PARTE WINDOWS 11 IL RESTO  FATTO ORA HO UN APPUNTAMENTO CON UN FORNITORE CI SENTIAMO POCO PRIMA DI PRANZO\xa0APPENA TORNO IN UFFICIO GRAZIEHALLO ICH KANN BEI MEINEM DRUCKER IN DEN EINSTELLUNGEN NICHT FESTLEGEN DASS DOPPELSEITIG UND FARBIG GEDRUCKT WERDEN SOLL\xa0KANN ES SEIN DASS DER TREIBER ZU AKTUALISIEREN WRE BZW MIT WINDO

In [276]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 2):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [277]:
blocks_to_skip = [1]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE



In [278]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
SCUSA MANUEL NON SO DOVE FARLO  UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10 DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE



['SCUSA MANUEL NON SO DOVE FARLO \xa0UPDATE WINDOWSSERVUS WIR HABEN HIER IN UNSEREM BRO IN SAVIESE TACH EINEN NEUEN DRUCKER UND WIR SCHAFFEN ES NICHT DIESEN ZU VERBINDEN ER IST ANGESCHLOSSEN UND ALLES WINDOWS SIEHT IHN JEDOCH KANN SICH NICHT VERBINDEN BITTE HILFE PATRICK VARONIER TACH0026 IST MORGEN IM BRO UM ZU HELFEN UND PROBIEREN GRUSSCIAO COME DACCORDO CON FRANCESCO FACCIO IL TICKET DI POTER RICEVERE UN PC FISSO CON WINDOWS 10\xa0DA VOI COME SOSTITUTIVO DELLESISTENTE ATASSSCHULUNG CHE ATTUALMENTE HA SU UN WINDOWS 7 E CHE  MOLTO LENTO IL PC DEVE ESSERE NELLA RETE DEL SERVICE CHE PUO GESTIRE ANCHE DEI GATEWAY TUTTI I PROGRAMMI DEL SERVICE FACCIO IO  GRAZIE']

# df_3_pc

In [279]:
#specify number of rows in each chunk
n=4
#split DataFrame into chunks
list_df = [df_3_pc[i:i+n] for i in range(0,len(df_3_pc),n)]
    #print(list_df)

In [280]:
len(list_df)

90

In [281]:
list_df[89]

Title  \
356  Nuovo telefono montatori svizzera   
357                Cambio nome sul 537   
358          Suono - Pro Call - cuffie   

                                                 Topic  \
356  {"11":"Hardware, Telephony, Smartphones, Monit...   
357  {"11":"Hardware, Telephony, Smartphones, Monit...   
358  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                  Text  
356  CI SERVE UN TELEFONO DI SOSTITUZIONE PER UNO P...  
357  CIAO  QUANDO CHIAMO DAL MIO TELEFONO CON IL 53...  
358  CIAO ARASHDEEP PURTROPPO CON IL NR 832 LA CHIA...

In [282]:
def put_together():
    list1=[]
    for index in range(0,89):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block

Result 0:
HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A NEW INSTALLATION OF THE OPERATING SYSTEM UPDATE AND SETTINGS IS DONETHE SECOND OPTION IS BETTER IF YOU INHERIT A LAPTOP FROM SOMEONE ELSELET US KNOW WHAT YOU WOULD LIKE WITH IT OR YOU CAN DELIVER IT DIRECTLY TO US FOR SERVICE INCLUDING A POWER ADAPTERIF YOU HAVE ANY QUESTIONS ABOUT THE PRICE OFFER I AM OF COURSE H

['HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A NEW INSTALLATION OF THE OPERATING SYSTEM UPDATE AND SETTINGS IS DONETHE SECOND OPTION IS BETTER IF YOU INHERIT A LAPTOP FROM SOMEONE ELSELET US KNOW WHAT YOU WOULD LIKE WITH IT OR YOU CAN DELIVER IT DIRECTLY TO US FOR SERVICE INCLUDING A POWER ADAPTERIF YOU HAVE ANY QUESTIONS ABOUT THE PRICE OFFER I AM OF COURSE HERE FOR 

In [283]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 89):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

In [284]:
blocks_to_skip = []  # List of block numbers to skip
result_list = put_together(blocks_to_skip)


Result 0:
HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A NEW INSTALLATION OF THE OPERATING SYSTEM UPDATE AND SETTINGS IS DONETHE SECOND OPTION IS BETTER IF YOU INHERIT A LAPTOP FROM SOMEONE ELSELET US KNOW WHAT YOU WOULD LIKE WITH IT OR YOU CAN DELIVER IT DIRECTLY TO US FOR SERVICE INCLUDING A POWER ADAPTERIF YOU HAVE ANY QUESTIONS ABOUT THE PRICE OFFER I AM OF COURSE H

In [285]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test


Result 0:
HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A NEW INSTALLATION OF THE OPERATING SYSTEM UPDATE AND SETTINGS IS DONETHE SECOND OPTION IS BETTER IF YOU INHERIT A LAPTOP FROM SOMEONE ELSELET US KNOW WHAT YOU WOULD LIKE WITH IT OR YOU CAN DELIVER IT DIRECTLY TO US FOR SERVICE INCLUDING A POWER ADAPTERIF YOU HAVE ANY QUESTIONS ABOUT THE PRICE OFFER I AM OF COURSE H

['HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A NEW INSTALLATION OF THE OPERATING SYSTEM UPDATE AND SETTINGS IS DONETHE SECOND OPTION IS BETTER IF YOU INHERIT A LAPTOP FROM SOMEONE ELSELET US KNOW WHAT YOU WOULD LIKE WITH IT OR YOU CAN DELIVER IT DIRECTLY TO US FOR SERVICE INCLUDING A POWER ADAPTERIF YOU HAVE ANY QUESTIONS ABOUT THE PRICE OFFER I AM OF COURSE HERE FOR 

# df_3_vulnerabilities

In [286]:
#empty

# df_3_email

In [287]:
#specify number of rows in each chunk
n=6
#split DataFrame into chunks
list_df = [df_3_email[i:i+n] for i in range(0,len(df_3_email),n)]
    #print(list_df)

In [288]:
len(list_df)

6

In [289]:
list_df[5]

Title  \
30  E-mail Adresse e PC per Bruno Campaner   
31   WG: Fernzugriff Visualisierungsserver   
32                           Problemi ENGO   

                                                Topic  \
30  {"11":"Hardware, Telephony, Smartphones, Monit...   
31  {"11":"Hardware, Telephony, Smartphones, Monit...   
32  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
30  BUONGIORNO POTETE FARE UN INDIRIZZO EMAIL ANCH...  
31   HALLO   WER KANN HIER DEN ZUGANG ERSTELLEN   ...  
32   QUESTI SONO I PROBLEMI CHE ABBIAMO AL MOMENTO...

In [290]:
def put_together():
    list1=[]
    for index in range(0,5):
        res = ''.join(map(str,list_df[index]['Text']))
        #print('Result:\n',res,'\n')
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1

summ_block = put_together()
summ_block


Result 0:
 LIEBE KOLLEGINNEN UND KOLLEGEN   BEI MEINEM COMPUTER FUNKTIONIERT FOLGENDES NICHT SCANNER NAVISION UPDATE EMAIL SIGNATUR INTRANET   AUS DIESEM GRUND KANN ICH LEIDER AUCH KEINE OFFIZIELLE ANFRAGE BER EIN TICKET ERSTELLEN   ID                   1 518 522 939 PASSWORT        H2V6CQ6D   LIEBE GRE SENDET EUCH ROBERT  HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A 

[' LIEBE KOLLEGINNEN UND KOLLEGEN \xa0 BEI MEINEM COMPUTER FUNKTIONIERT FOLGENDES NICHT SCANNER NAVISION UPDATE EMAIL SIGNATUR INTRANET \xa0 AUS DIESEM GRUND KANN ICH LEIDER AUCH KEINE OFFIZIELLE ANFRAGE BER EIN TICKET ERSTELLEN \xa0 ID\xa0\xa0\xa0\xa0\xa0\xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0 1 518 522 939 PASSWORT\xa0\xa0\xa0\xa0\xa0\xa0\xa0 H2V6CQ6D \xa0 LIEBE GRE SENDET EUCH ROBERT  HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS 

In [291]:
## Skip the block if it's in the list of blocks to skip
def put_together(blocks_to_skip=[]):
    list1 = []
    for index in range(0, 5):
        if index in blocks_to_skip:
            continue  # Skip the block if it's in the list of blocks to skip

        res = ''.join(map(str, list_df[index]['Text']))
        print(f'Result {index}:\n{res}\n')
        list1.append(res)
    return list1


In [292]:
blocks_to_skip = [2]  # List of block numbers to skip
result_list = put_together(blocks_to_skip)

Result 0:
 LIEBE KOLLEGINNEN UND KOLLEGEN   BEI MEINEM COMPUTER FUNKTIONIERT FOLGENDES NICHT SCANNER NAVISION UPDATE EMAIL SIGNATUR INTRANET   AUS DIESEM GRUND KANN ICH LEIDER AUCH KEINE OFFIZIELLE ANFRAGE BER EIN TICKET ERSTELLEN   ID                   1 518 522 939 PASSWORT        H2V6CQ6D   LIEBE GRE SENDET EUCH ROBERT  HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A 

In [293]:
summ_block_test = put_together(blocks_to_skip)
summ_block_test

Result 0:
 LIEBE KOLLEGINNEN UND KOLLEGEN   BEI MEINEM COMPUTER FUNKTIONIERT FOLGENDES NICHT SCANNER NAVISION UPDATE EMAIL SIGNATUR INTRANET   AUS DIESEM GRUND KANN ICH LEIDER AUCH KEINE OFFIZIELLE ANFRAGE BER EIN TICKET ERSTELLEN   ID                   1 518 522 939 PASSWORT        H2V6CQ6D   LIEBE GRE SENDET EUCH ROBERT  HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS CLONED WITH ALL DATA THE NOTEBOOK IS IN ITS ORIGINAL STATE SO TO SPEAK OR A 

[' LIEBE KOLLEGINNEN UND KOLLEGEN \xa0 BEI MEINEM COMPUTER FUNKTIONIERT FOLGENDES NICHT SCANNER NAVISION UPDATE EMAIL SIGNATUR INTRANET \xa0 AUS DIESEM GRUND KANN ICH LEIDER AUCH KEINE OFFIZIELLE ANFRAGE BER EIN TICKET ERSTELLEN \xa0 ID\xa0\xa0\xa0\xa0\xa0\xa0 \xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0\xa0 1 518 522 939 PASSWORT\xa0\xa0\xa0\xa0\xa0\xa0\xa0 H2V6CQ6D \xa0 LIEBE GRE SENDET EUCH ROBERT  HI ARASHDEEP HEREBY THE ANSWER FROM ALEXA BASED ON AN EMAIL INQUIRY AND A SUBSEQUENT TELEPHONE CONVERSATION I AM SENDING YOU A PRICE OFFER FOR A LAPTOP UPGRADE RAM UPGRADE TO 16GB 145  VATAVAILABILITY 13 WORKING DAYS FROM THE ORDERHOWEVER WE COULD ALSO OFFER TO EXCHANGE THE DISK FOR A LARGER ONE BECAUSE APPARENTLY THERE IS ONLY 256GBBUT WE WOULD HAVE TO HAVE THE LAPTOP HERE AND DISASSEMBLE IT  BECAUSE THERE IS AN OPTION TO PUT TWO TYPES OF DISKS AND IT IS NECESSARY TO KNOW WHICH ONE IS MORE PRECISETHEN WHEN REPLACING THE DISK THERE ARE AGAIN TWO OPTIONS WHAT TO DO EITHER THE ORIGINAL DISK IS 

### df_3_software

In [294]:
#specify number of rows in each chunk
n=3
#split DataFrame into chunks
list_df = [df_3_software[i:i+n] for i in range(0,len(df_3_software),n)]
    #print(list_df)

In [295]:
len(list_df)

9

In [296]:
list_df[8]

Title                                              Topic  \
24  Server MFD  {"11":"Hardware, Telephony, Smartphones, Monit...   
25  Server MFD  {"11":"Hardware, Telephony, Smartphones, Monit...   
26  Server MFD  {"11":"Hardware, Telephony, Smartphones, Monit...   

                                                 Text  
24  CIAO  POSSIBILE CONNETERMI AL SERVER IN FRANCI...  
25  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...  
26  IL SERVER PER AVERE LA STAMPANTE E LA STAMPANT...

In [297]:
def put_together():
    list1=[]
    for index in range(0,8):
        res = ''.join(map(str,list_df[index]['Text']))
        print('Result:\n',res,'\n')
        list1.append(res)
    return list1

In [298]:
summ_block = put_together()
summ_block

Result:
 MY PC HAS BEEN RUNNING VERY SLOW FOR THE PAST FEW WEEKS SOFTWARE UPDATE WAS MADE INTERNET CONNECTION IS SUFFICIENT PC SEEMS TO BE STRUGGLING THE FAN ALSO SEEMS TO BE RUNNING MORE OFTEN THAN IT USED TO  PLEASE LET ME KNOW IF THERE IS SOMETHING YOU CAN HELP ME WITH CIAO STAMATTINA NON RIESCO A COLLEGARMI COL MONITOR POTRESTE CONTROLLARE PENSO SIA UN PROBLEMA DI SOFTWARE PERCH IL MONITOR SEMBRA ACCESO E IL CAVO  ATTACCATO BENE  GRAZIE SALUTI ALEXASALVE SE POSSIBILE CHIEDEREI CHE FRANCESCO O MANUEL MI CHIAMINO PER IL SCAFFALE CHE VIENE INSTALLATO DA ENGO IN QUESTE SETTIMANEDEVO CHIARIRE COME SAR GESTITO IL CLIENT O SOFTWARE MODULA 39 349 785 7499 GRAZIE E SALUTI TOBIA 

Result:
 PER ME VA BENE PER DOMANI VIENE CONCLUSO LA COSTRUZIONE E PENSO CHE VORRANNO INSTALLARE IL SOFTWARE VERSO LE 1011 ABBIAMO UN PC MA NON SO CHE USER VERR USATO ETC E POI DEVO ANCHE VEDERE QUALE IP  ASSOCIATO CON IL SCAFFALECLIENT  PREGO FAMMI SAPERE QUANDO AVRESTI TEMPO DOMANIGRAZIE E BUON LAVORO   WIE VON H

['MY PC HAS BEEN RUNNING VERY SLOW FOR THE PAST FEW WEEKS SOFTWARE UPDATE WAS MADE INTERNET CONNECTION IS SUFFICIENT PC SEEMS TO BE STRUGGLING THE FAN ALSO SEEMS TO BE RUNNING MORE OFTEN THAN IT USED TO\xa0 PLEASE LET ME KNOW IF THERE IS SOMETHING YOU CAN HELP ME WITH\xa0CIAO STAMATTINA NON RIESCO A COLLEGARMI COL MONITOR POTRESTE CONTROLLARE PENSO SIA UN PROBLEMA DI SOFTWARE PERCH IL MONITOR SEMBRA ACCESO E IL CAVO  ATTACCATO BENE  GRAZIE SALUTI ALEXASALVE SE POSSIBILE CHIEDEREI CHE FRANCESCO O MANUEL MI CHIAMINO PER IL SCAFFALE CHE VIENE INSTALLATO DA ENGO IN QUESTE SETTIMANEDEVO CHIARIRE COME SAR GESTITO IL CLIENT O SOFTWARE MODULA 39 349 785 7499 GRAZIE E SALUTI TOBIA',
 'PER ME VA BENE PER DOMANI VIENE CONCLUSO LA COSTRUZIONE E PENSO CHE VORRANNO INSTALLARE IL SOFTWARE VERSO LE 1011 ABBIAMO UN PC MA NON SO CHE USER VERR USATO ETC E POI DEVO ANCHE VEDERE QUALE IP  ASSOCIATO CON IL SCAFFALECLIENT  PREGO FAMMI SAPERE QUANDO AVRESTI TEMPO DOMANIGRAZIE E BUON LAVORO   WIE VON HANNES SI

In [299]:
import pickle